# **Notebook 4: EDA OPERATIONS AND MODELING**

## **Mục tiêu:**
Notebook này tập trung vào phân tích chuyên sâu các khía cạnh vận hành và xây dựng mô hình dự đoán cho dữ liệu đặt phòng khách sạn. Các mục tiêu chính bao gồm:

1. **Phân tích kinh doanh (Business Analysis)**
   - Phân tích ADR (Average Daily Rate) theo các phân khúc khách hàng
   - Đánh giá tỷ lệ hủy phòng và các yếu tố ảnh hưởng
   - Xác định mô hình giá và chiến lược phân khúc tối ưu

2. **Phân tích vận hành (Operations Analysis)**
   - Phân tích Lead Time (thời gian đặt phòng trước) và ảnh hưởng của nó
   - Đánh giá hiệu quả của các kênh phân phối
   - Phân tích mô hình đặt phòng và yêu cầu đặc biệt

3. **Xây dựng mô hình dự đoán (Predictive Modeling)**
   - Phát triển mô hình dự đoán tỷ lệ hủy phòng
   - So sánh hiệu suất của các thuật toán Machine Learning
   - Tối ưu hóa mô hình và đánh giá kết quả
   - Cung cấp insights để ra quyết định kinh doanh

## **I. Tổng quan:**

Trong bối cảnh ngành khách sạn ngày càng cạnh tranh, việc hiểu rõ hành vi khách hàng và tối ưu hóa vận hành là chìa khóa để thành công. Notebook này đi sâu vào phân tích các khía cạnh quan trọng nhất của hoạt động kinh doanh khách sạn thông qua dữ liệu đặt phòng.

### **Bối cảnh nghiên cứu:**

Ngành khách sạn đối mặt với nhiều thách thức phức tạp:
- **Biến động ADR**: Giá phòng trung bình thay đổi theo mùa, loại khách hàng và kênh đặt phòng
- **Tỷ lệ hủy phòng cao**: Ảnh hưởng trực tiếp đến doanh thu và kế hoạch vận hành
- **Quản lý Lead Time**: Cân bằng giữa đặt phòng sớm và đặt phòng gấp
- **Tối ưu hóa kênh phân phối**: Lựa chọn kênh marketing và phân phối hiệu quả

### **Phương pháp tiếp cận:**

Chúng ta sẽ áp dụng phương pháp phân tích dữ liệu toàn diện kết hợp:
1. **Exploratory Data Analysis (EDA)**: Khám phá patterns và relationships trong dữ liệu
2. **Statistical Analysis**: Kiểm định giả thuyết và phân tích tương quan
3. **Data Visualization**: Sử dụng biểu đồ tương tác để trình bày insights
4. **Machine Learning**: Xây dựng mô hình dự đoán và classification

### **Giá trị mang lại:**

Kết quả phân tích sẽ cung cấp:
- Hiểu biết sâu sắc về hành vi khách hàng và mô hình đặt phòng
- Khả năng dự đoán tỷ lệ hủy phòng để tối ưu hóa overbooking
- Chiến lược giá và phân khúc khách hàng dựa trên data
- Recommendations cụ thể để cải thiện revenue management và operations

## **II. Import thư viện:**

In [300]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.graph_objects as go
import plotly.express as px
from pathlib import Path
from plotly.subplots import make_subplots
from typing import Optional, List, Tuple, Dict, Any
from datetime import datetime
import warnings
import time

from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.impute import SimpleImputer
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, HistGradientBoostingClassifier
from sklearn.metrics import (
    precision_recall_curve, auc, roc_auc_score, 
    precision_score, recall_score, f1_score, 
    confusion_matrix, classification_report
)

print('Import Thư Viện Thành Công!!!')

warnings.filterwarnings('ignore')

project_root = Path.cwd().parent
data_path = project_root / 'data' / 'processed' / 'clean_data.csv'

df = pd.read_csv(data_path)

print(f"Dataset shape: {df.shape}")
print(f"\nColumns: {df.columns.tolist()}")

Import Thư Viện Thành Công!!!
Dataset shape: (87010, 32)

Columns: ['hotel', 'is_canceled', 'lead_time', 'arrival_date_year', 'arrival_date_month', 'arrival_date_week_number', 'arrival_date_day_of_month', 'stays_in_weekend_nights', 'stays_in_week_nights', 'adults', 'children', 'babies', 'meal', 'country', 'market_segment', 'distribution_channel', 'is_repeated_guest', 'previous_cancellations', 'previous_bookings_not_canceled', 'reserved_room_type', 'assigned_room_type', 'booking_changes', 'deposit_type', 'agent', 'company', 'days_in_waiting_list', 'customer_type', 'adr', 'required_car_parking_spaces', 'total_of_special_requests', 'reservation_status', 'reservation_status_date']


## **III. Câu hỏi:**

---
### **Câu hỏi 4: Tổng quan kinh doanh: Phân tích ADR và Tỷ lệ Hủy theo Phân khúc Khách hàng**
**A. Câu hỏi nghiên cứu:**

*Mức giá phòng trung bình (Average Daily Rate – ADR) và tỷ lệ hủy đặt phòng khác nhau như thế nào giữa các loại khách sạn và các phân khúc khách hàng chính?*

Mục tiêu của câu hỏi này là đánh giá sự khác biệt về chính sách giá và mức độ rủi ro hủy đặt phòng giữa các nhóm khách hàng không đồng nhất, thay vì chỉ xem xét các chỉ số tổng hợp ở cấp độ toàn bộ khách sạn.

**B. Động cơ nghiên cứu:**
- ADR và tỷ lệ hủy đặt phòng là hai chỉ số then chốt quyết định doanh thu thực tế mà khách sạn có thể ghi nhận. Trong khi ADR phản ánh khả năng định giá của khách sạn, thì tỷ lệ hủy lại ảnh hưởng trực tiếp đến việc doanh thu đó có được hiện thực hóa hay không.
- Việc phân tích ở mức tổng hợp có thể che khuất những khác biệt quan trọng trong hành vi đặt phòng giữa các phân khúc khách hàng. Một số phân khúc có thể mang lại mức giá cao nhưng đi kèm rủi ro hủy lớn, trong khi các phân khúc khác tuy có giá thấp hơn nhưng lại ổn định hơn. Do đó, việc phân tích ADR và tỷ lệ hủy theo từng phân khúc là cần thiết để phản ánh đúng giá trị và rủi ro của từng nhóm khách hàng.

**C. Ý nghĩa thực tiễn:**

Phân tích sự khác biệt về ADR và tỷ lệ hủy giữa các loại khách sạn và các phân khúc khách hàng mang lại giá trị thực tiễn cho nhiều bộ phận trong hoạt động kinh doanh khách sạn.

- Đối với bộ phận quản lý doanh thu, kết quả phân tích hỗ trợ việc xây dựng chiến lược định giá phân khúc hóa, phù hợp với đặc điểm giá trị và rủi ro của từng nhóm khách hàng.
- Đối với bộ phận vận hành, hiểu rõ hành vi hủy đặt phòng theo phân khúc giúp cải thiện công tác dự báo nhu cầu và ra quyết định overbooking. 
- Ở cấp độ quản lý chiến lược, phân tích này giúp xác định các phân khúc khách hàng ưu tiên nhằm tối ưu hóa doanh thu đồng thời kiểm soát rủi ro.

**D. Phạm vi phân tích:**

Trong câu hỏi này, phân khúc khách hàng được xác định dựa trên các chiều thông tin sau:
- Loại khách sạn (City Hotel, Resort Hotel)
- Phân khúc thị trường (ví dụ: Online Travel Agencies, Offline Travel Agents/Tour Operators, Direct, Corporate, Groups)
- Kênh phân phối (ví dụ: TA/TO, Direct, Corporate, GDS)
- Loại khách hàng (Transient, Contract, Group, Transient-Party)
- Chính sách đặt cọc (No Deposit, Non-Refundable, Refundable)

Các chiều phân khúc này phản ánh sự khác biệt trong hành vi đặt phòng, mức giá chấp nhận và mức độ cam kết của khách hàng, từ đó cho phép đánh giá toàn diện mối quan hệ giữa giá phòng và rủi ro hủy đặt phòng.

--- 
### **Câu hỏi 5:** Driver Analysis: Yếu tố Ngoài Giá Ảnh hưởng đến Hủy phòng

**A. Câu hỏi nghiên cứu:**

Những yếu tố nào, ngoài mức giá phòng trung bình (ADR), có mối liên hệ mạnh nhất với khả năng hủy đặt phòng, và mức độ ảnh hưởng của các yếu tố này khác nhau như thế nào giữa City Hotel và Resort Hotel?

**B. Động cơ nghiên cứu**

- Các phân tích tập trung vào ADR chỉ phản ánh một phần hành vi hủy đặt phòng và có thể dẫn đến các quyết định quản trị chưa tối ưu. Trong thực tế, tỷ lệ hủy cao không nhất thiết bắt nguồn từ mức giá phòng, mà có thể chịu ảnh hưởng đáng kể từ các yếu tố khác như thời gian đặt phòng trước (lead time), chính sách đặt cọc, kênh phân phối hoặc đặc điểm hành vi khách hàng.

- Việc điều chỉnh giá phòng mà không xem xét các yếu tố ngoài giá có nguy cơ không làm giảm tỷ lệ hủy, đồng thời ảnh hưởng tiêu cực đến nhu cầu đặt phòng. Do đó, cần thiết phải xác định và định lượng các tác nhân ngoài ADR nhằm làm rõ nguyên nhân gốc rễ của hành vi hủy đặt phòng.

**C. Ý nghĩa thực tiễn**

Phân tích các yếu tố ngoài giá cung cấp các đòn bẩy quản trị không liên quan trực tiếp đến điều chỉnh mức giá, từ đó hỗ trợ cải thiện hiệu quả kinh doanh. Cụ thể, kết quả của Q4 có thể được sử dụng để:
- Thiết kế chính sách đặt cọc và điều khoản hủy phù hợp với mức độ rủi ro của từng nhóm khách hàng
- Tối ưu hóa cơ cấu kênh phân phối dựa trên mức độ ổn định của từng kênh
- Cải thiện độ chính xác của dự báo hủy đặt phòng nhằm hỗ trợ lập kế hoạch công suất và chiến lược overbooking
- Xác định các nhóm khách hàng cần được ưu tiên chăm sóc hoặc xác nhận lại đặt phòng để giảm khả năng hủy

**D. Phạm vi phân tích**

Phân tích Q4 tập trung vào các yếu tố ngoài giá phòng, bao gồm nhưng không giới hạn ở: thời gian đặt phòng trước (lead time), chính sách đặt cọc, kênh phân phối, đặc điểm khách hàng (khách quay lại, yêu cầu đặc biệt) và hành vi đặt phòng trước đây. Mức độ ảnh hưởng của các yếu tố này được phân tích và so sánh riêng cho City Hotel và Resort Hotel, nhằm làm rõ sự khác biệt về hành vi hủy đặt phòng giữa hai loại hình khách sạn.

--- 
### **Câu hỏi 6:** 
**A. Câu hỏi nghiên cứu:**

Giá phòng trung bình (ADR) ảnh hưởng như thế nào đến khả năng khách hủy đặt phòng giữa các phân khúc khách hàng khác nhau, và mối quan hệ này có khác biệt giữa City Hotel và Resort Hotel hay không?

Mục tiêu phân tích mối quan hệ giữa ADR và tỷ lệ hủy đặt phòng nhằm xác định mức độ nhạy cảm với giá của các phân khúc khách hàng khác nhau, đánh giá sự khác biệt về phản ứng đối với giá giữa City Hotel và Resort Hotel và làm rõ sự tồn tại của các ngưỡng ADR có thể dẫn đến gia tăng đột biến tỷ lệ hủy.

**B. Động lực nghiên cứu:**

- Định giá phòng là một quyết định quản trị then chốt trong kinh doanh khách sạn, tuy nhiên mối quan hệ giữa giá phòng và hành vi hủy đặt phòng không mang tính tuyến tính đơn giản. Việc tăng ADR có thể làm gia tăng doanh thu tiềm năng, nhưng đồng thời cũng có thể làm tăng tỷ lệ hủy, từ đó làm giảm doanh thu thực hiện.
- Hơn nữa, mức độ nhạy cảm với giá có thể khác nhau đáng kể giữa các phân khúc khách hàng và các loại hình khách sạn. Nếu không hiểu rõ mối quan hệ đánh đổi này, các chiến lược điều chỉnh giá có nguy cơ không đạt được hiệu quả mong muốn.

**C. Ý nghĩa thực tiễn:**

Phân tích mối quan hệ giữa ADR và khả năng hủy đặt phòng cung cấp cơ sở định lượng cho các quyết định quản trị về giá. Kết quả hỗ trợ:
- Xác định các phân khúc nhạy cảm với giá và các phân khúc ít nhạy cảm hơn
- Thiết kế chiến lược định giá phân biệt theo loại hình khách sạn
- Đánh giá tác động của các điều chỉnh giá đến doanh thu thực hiện, thay vì chỉ doanh thu danh nghĩa
- Làm nền tảng cho các phân tích tối ưu hóa giá và quản lý rủi ro hủy trong các bước nghiên cứu tiếp theo

**D. Phạm vi phân tích:**

Phân tích tập trung vào mối quan hệ giữa ADR và khả năng hủy đặt phòng trong các phân khúc chính. Dữ liệu được phân tách theo loại hình khách sạn (City Hotel và Resort Hotel) và, khi phù hợp, theo các phân khúc thị trường có quy mô booking lớn, nhằm làm rõ sự khác biệt trong hành vi hủy đặt phòng theo mức giá và bối cảnh lưu trú.

--- 
### **Câu hỏi 7:**

**A. Câu hỏi nghiên cứu:**

*Dựa trên xác suất hủy đặt phòng dự đoán, mức giá phòng (ADR) nào tối ưu hóa doanh thu thực nhận kỳ vọng cho từng loại hình khách sạn và phân khúc khách hàng?*

Mục tiêu của Q6 là ước lượng xác suất hủy đặt phòng tại thời điểm ra quyết định giá, tích hợp xác suất này vào thước đo doanh thu thực nhận kỳ vọng, và xác định mức ADR tối ưu theo từng loại hình khách sạn và, khi cần thiết, theo từng phân khúc thị trường.

**B. Động lực nghiên cứu:**

- Các phân tích trước cho thấy tồn tại mối quan hệ đánh đổi giữa ADR và khả năng hủy đặt phòng. Tuy nhiên, việc dừng lại ở mối quan hệ giá–hủy chưa đủ để hỗ trợ ra quyết định kinh doanh cụ thể. Trong thực tế, doanh nghiệp không tối đa hóa ADR danh nghĩa, mà tối ưu hóa doanh thu thực nhận sau khi đã trừ đi rủi ro hủy.
- Cùng một mức ADR có thể tạo ra doanh thu thực nhận rất khác nhau nếu xác suất hủy khác nhau. Do đó, cần chuyển từ phân tích mô tả và suy luận thống kê sang một khuôn khổ ra quyết định định lượng, trong đó giá phòng được lựa chọn dựa trên giá trị kỳ vọng thay vì giá niêm yết đơn lẻ.

**C. Ý nghĩa thực tiễn:**

Phân tích Q6 cung cấp một khuôn khổ ra quyết định trực tiếp cho hoạt động định giá. Cụ thể, kết quả cho phép:
- Lựa chọn mức ADR tối ưu dựa trên doanh thu thực nhận kỳ vọng, thay vì tối đa hóa giá danh nghĩa
- Thiết kế chính sách giá khác nhau cho City Hotel và Resort Hotel, phản ánh sự khác biệt về rủi ro hủy
- Hỗ trợ các quyết định định giá theo phân khúc thị trường, đặc biệt đối với các nhóm có mức độ nhạy cảm với giá khác nhau
- Giảm rủi ro phòng trống phát sinh từ các quyết định tăng giá không phù hợp

**D. Phạm vi và cách tiếp cận phân tích:**
- Phân tích Q6 tập trung vào các booking tại thời điểm ra quyết định giá, sử dụng các biến quan sát được tại thời điểm đặt phòng. Xác suất hủy đặt phòng được ước lượng bằng các mô hình học máy và được tích hợp vào thước đo $Expected Realized Revenue = ADR × số đêm lưu trú × (1 − P(hủy))$.
- Việc tối ưu hóa được thực hiện riêng theo loại hình khách sạn (City Hotel và Resort Hotel) và, khi cần thiết, theo các phân khúc thị trường chính, nhằm phản ánh tính không đồng nhất trong hành vi hủy và giá trị kinh tế của từng nhóm khách hàng.

--- 
### **Câu hỏi 8:**
**A. Câu hỏi nghiên cứu:**

*Nếu áp dụng mức ADR tối ưu (xác định ở Q7) cho từng loại khách sạn, doanh thu thực nhận kỳ vọng và tỷ lệ hủy dự đoán sẽ thay đổi như thế nào so với chính sách giá hiện tại?*

**Mục tiêu nghiên cứu:**

- Định lượng mức tăng/giảm doanh thu thực nhận kỳ vọng khi chuyển sang ADR tối ưu.
- Đánh giá tác động biên lên tỷ lệ hủy dự đoán.
- Cung cấp cơ sở định lượng để quyết định có nên triển khai và triển khai ở đâu trước.

**B. Động cơ nghiên cứu**

Mặc dù Q7 đã xác định được mức ADR tối ưu về mặt lý thuyết, các quyết định quản trị yêu cầu thêm bằng chứng về tác động thực tế.

Cụ thể:

- Mức ADR tối ưu chỉ có ý nghĩa nếu uplift doanh thu đủ lớn so với rủi ro hủy tăng thêm.
- Ban quản lý cần so sánh kịch bản hiện tại (baseline) với kịch bản áp dụng ADR tối ưu theo logic what-if.
- Q8 đóng vai trò chuyển đổi kết quả mô hình thành ngôn ngữ tài chính và vận hành.

**C. Ý nghĩa thực tiễn:**

Phân tích hỗ trợ trực tiếp cho các quyết định sau:

**Revenue Management:**
- Ước lượng ROI của chiến lược giá mới trước khi triển khai.
- Ưu tiên triển khai cho loại khách sạn hoặc phân khúc có uplift cao nhất.

**General Management & Finance:**
- Dự báo tác động lên tổng doanh thu thực nhận thay vì ADR danh nghĩa.
- Hỗ trợ lập kế hoạch ngân sách và mục tiêu doanh thu.

**Operations:** Dự báo thay đổi trong tỷ lệ hủy kỳ vọng, từ đó điều chỉnh overbooking và phân bổ phòng.

Như vậy, nghiên cứu giúp giảm rủi ro triển khai bằng cách mô phỏng trước kết quả kinh doanh.

---
### **Câu hỏi 9:**

**A. Câu hỏi nghiên cứu:**
Những phân khúc nào nên được ưu tiên triển khai chiến lược giá tối ưu nhằm tối đa hóa hiệu quả kinh doanh, đồng thời kiểm soát rủi ro hủy và đảm bảo quy mô booking đủ lớn?

Mục tiêu của xác định thứ tự ưu tiên triển khai chiến lược giá theo phân khúc, đề xuất lộ trình rollout theo từng giai đoạn nhằm giảm thiểu rủi ro vận hành và làm rõ các phân khúc cần cơ chế kiểm soát rủi ro bổ trợ.

**B. Động lực nghiên cứu:**

- Mặc dù Q7 và Q8 đã xác định mức ADR tối ưu và tác động doanh thu kỳ vọng, việc triển khai đồng loạt cho tất cả phân khúc là không khả thi và tiềm ẩn rủi ro cao. Các phân khúc khác nhau thể hiện sự khác biệt rõ rệt về quy mô booking, mức uplift và độ nhạy cảm với rủi ro hủy.
- Do đó, cần một khuôn khổ ưu tiên triển khai nhằm chuyển các kết quả phân tích định lượng thành kế hoạch hành động khả thi trong thực tế vận hành.

**C. Ý nghĩa thực tiễn:**

Phân tích hỗ trợ trực tiếp cho:

- Revenue/Pricing Teams trong việc xây dựng kế hoạch rollout theo giai đoạn.
- Operations trong dự báo biến động hủy và quản lý công suất theo từng phase triển khai.
- Ban quản lý trong việc tối đa hóa ROI, đồng thời kiểm soát rủi ro trong quá trình thay đổi chính sách giá.

Phân tích đóng vai trò là cầu nối cuối cùng giữa phân tích dữ liệu và quyết định triển khai thực tế.

**D. Phạm vi và cách tiếp cận:**

- Ưu tiên triển khai được xác định dựa trên ba tiêu chí chính:
- Đóng góp uplift doanh thu (absolute và relative).
- Mức gia tăng rủi ro hủy khi áp dụng ADR tối ưu.
- Quy mô booking, nhằm đảm bảo tác động đủ lớn về mặt kinh doanh.

Phân tích được thực hiện theo hai chiều chính: loại hình khách sạn (City vs. Resort) và phân khúc thị trường. Kết quả được sử dụng để đề xuất triển khai theo các phase, trong đó các phân khúc win–win được ưu tiên trước, tiếp theo là các phân khúc trade-off đi kèm các cơ chế kiểm soát rủi ro phù hợp.


## **IV. Triển khai:**

---
### **Q4 - Tổng quan kinh doanh: Phân tích ADR và Tỷ lệ hủy theo phân khúc khách hàng:**

**Câu hỏi nghiên cứu:** *Mức giá phòng trung bình hằng ngày (Average Daily Rate – ADR) và tỷ lệ hủy đặt phòng khác nhau như thế nào giữa các loại hình khách sạn và các phân khúc khách hàng chính?*

Phân tích này nhằm làm rõ sự khác biệt về giá trị kinh tế (ADR) và rủi ro hiện thực hóa doanh thu (tỷ lệ hủy) giữa các nhóm khách hàng, từ đó hỗ trợ các quyết định về định giá theo phân khúc và quản trị rủi ro.

### **A. Xác định phân khúc và mục tiêu phân tích:**

**1. Định nghĩa phân khúc khách hàng:**

Trong phạm vi câu hỏi, *“phân khúc khách hàng”* được xác định dựa trên các chiều thông tin sau:

- **hotel**: City Hotel và Resort Hotel
- **market_segment**: Online TA, Offline TA/TO, Direct, Corporate, Groups, …
- **distribution_channel**: TA/TO, Direct, Corporate, GDS
- **customer_type**: Transient, Contract, Group, Transient-Party
- **deposit_type**: No Deposit, Non-Refundable, Refundable

Các chiều phân khúc này phản ánh sự khác biệt về hành vi đặt phòng, mức độ cam kết và khả năng chấp nhận giá, qua đó cho phép đánh giá đồng thời mối quan hệ giữa ADR và rủi ro hủy đặt phòng ở mức chi tiết.

**2. Mục tiêu phân tích:**
- Phân tích tập trung xác định các nhóm khách hàng theo ba khía cạnh chính:
- Nhóm giá trị cao / giá trị thấp: phân khúc nào có ADR trung bình cao nhất hoặc thấp nhất
- Nhóm rủi ro cao / rủi ro thấp: phân khúc nào có tỷ lệ hủy đặt phòng cao hoặc thấp
- Nhóm có quy mô lớn (volume): phân khúc nào chiếm tỷ trọng đáng kể trong tổng số booking

Từ các kết quả này, báo cáo hướng tới đề xuất các hàm ý quản trị nhằm tối ưu hóa doanh thu kỳ vọng và giảm thiểu rủi ro hủy theo từng phân khúc.

### **B. Chuẩn bị dữ liệu::**

Phần này thực hiện các bước tiền xử lý nhằm đảm bảo các thống kê ADR và tỷ lệ hủy theo phân khúc được ước lượng chính xác, đồng thời hạn chế sai lệch do dữ liệu không hợp lệ hoặc do sử dụng biến mang tính “hậu nghiệm”.

#### **1. Loại bỏ biến gây rò rỉ thông tin (Data Leakage):**

**Vấn đề:** Một số biến chỉ được xác định sau khi booking đã kết thúc (đã hủy, đã check-out hoặc no-show). Việc sử dụng các biến này trong phân tích có thể tạo ra hiện tượng “nhìn trước kết quả”, làm sai lệch diễn giải về sự khác biệt giữa các phân khúc.

**Biến bị loại bỏ:**
- `reservation_status`: trạng thái cuối cùng của booking (Canceled / Check-Out / No-Show), mang tính outcome
- `reservation_status_date`: thời điểm trạng thái được xác nhận, phát sinh sau khi có quyết định hủy hoặc hoàn tất lưu trú

**Mục đích loại bỏ:** Các biến trên chứa thông tin xảy ra sau sự kiện hủy hoặc sau khi hoàn tất lưu trú, do đó không phù hợp để phân tích nguyên nhân hoặc đánh giá rủi ro theo phân khúc trong bối cảnh ra quyết định tại thời điểm booking. Việc giữ lại các biến này có thể dẫn đến kết quả sai lệch do data leakage.

In [301]:
leakage_cols = ['reservation_status', 'reservation_status_date']
df_q4 = df.drop(columns=[col for col in leakage_cols if col in df.columns], errors='ignore')

print(f"Removed leakage columns: {[col for col in leakage_cols if col in df.columns]}")
print(f"New shape: {df_q4.shape}")

Removed leakage columns: ['reservation_status', 'reservation_status_date']
New shape: (87010, 30)


#### **2. Xử lý các giá trị ADR bất thường:**

**1. Vấn đề:**

Biến Average Daily Rate (ADR) trong tập dữ liệu có thể chứa các giá trị bất thường, bao gồm:
- Giá trị âm, có thể phát sinh từ lỗi nhập liệu hoặc các trường hợp hoàn tiền (refund)
- Các giá trị cực lớn (outliers), có khả năng là lỗi dữ liệu hoặc các booking đặc biệt không đại diện cho hành vi chung của phân khúc

**2. Tác động:** Sự tồn tại của các giá trị ADR bất thường có thể làm sai lệch đáng kể các thống kê mô tả, đặc biệt là giá trị trung bình (mean ADR). Điều này dẫn đến việc so sánh ADR giữa các phân khúc khách hàng trở nên thiếu tin cậy và có thể tạo ra các kết luận sai lệch về chiến lược định giá.

**3. Phương pháp xử lý:**

- Phân tích phân phối ADR bằng các thống kê mô tả và biểu đồ (histogram/boxplot) để nhận diện mức độ lệch và sự hiện diện của outliers.
- Loại bỏ các giá trị ADR không hợp lệ (ADR ≤ 0).
- Áp dụng phương pháp cắt ngưỡng (clipping) hoặc winsorization theo percentile (p1–p99), nhằm giảm ảnh hưởng của các giá trị cực đoan trong khi vẫn bảo toàn phần lớn thông tin dữ liệu.

Việc xử lý này giúp các chỉ số ADR phản ánh chính xác hơn mức giá điển hình của từng phân khúc khách hàng.

In [302]:
print("=== ADR Statistics ===")
print(f"Min: {df_q4['adr'].min():.2f}")
print(f"Max: {df_q4['adr'].max():.2f}")
print(f"Mean: {df_q4['adr'].mean():.2f}")
print(f"Median: {df_q4['adr'].median():.2f}")
print(f"\nPercentiles:")
print(df_q4['adr'].describe(percentiles=[0.01, 0.05, 0.10, 0.90, 0.95, 0.99]))

# Check negative values
negative_adr = (df_q4['adr'] < 0).sum()
print(f"\nBookings with negative ADR: {negative_adr} ({negative_adr/len(df_q4)*100:.2f}%)")

# Calculate percentiles for clipping
p01 = df_q4['adr'].quantile(0.01)
p99 = df_q4['adr'].quantile(0.99)

print(f"\nClipping range: [{p01:.2f}, {p99:.2f}]")

=== ADR Statistics ===
Min: 0.00
Max: 5400.00
Mean: 106.58
Median: 98.33

Percentiles:
count    87010.000000
mean       106.583747
std         54.913712
min          0.000000
1%           0.000000
5%          37.400000
10%         48.000000
50%         98.330000
90%        174.000000
95%        204.330000
99%        262.000000
max       5400.000000
Name: adr, dtype: float64

Bookings with negative ADR: 0 (0.00%)

Clipping range: [0.00, 262.00]


In [303]:
df_q4['adr_clipped'] = df_q4['adr'].clip(lower=p01, upper=p99)

print("=== After Clipping ===")
print(f"Min: {df_q4['adr_clipped'].min():.2f}")
print(f"Max: {df_q4['adr_clipped'].max():.2f}")
print(f"Mean: {df_q4['adr_clipped'].mean():.2f}")
print(f"Median: {df_q4['adr_clipped'].median():.2f}")

# Also remove bookings with 0 ADR (likely invalid)
zero_adr = (df_q4['adr_clipped'] == 0).sum()
print(f"\nBookings with 0 ADR: {zero_adr} ({zero_adr/len(df_q4)*100:.2f}%)")
print("Decision: Keep 0 ADR for now (may represent complimentary stays), but will note in analysis.")

=== After Clipping ===
Min: 0.00
Max: 262.00
Mean: 106.21
Median: 98.33

Bookings with 0 ADR: 1637 (1.88%)
Decision: Keep 0 ADR for now (may represent complimentary stays), but will note in analysis.


#### **3. Chuẩn hóa các phân khúc khách hàng phục vụ trực quan hóa:**

**1. Vấn đề:**

Một số biến phân khúc (market_segment hoặc distribution_channel) chứa số lượng danh mục (categories) lớn, trong đó nhiều danh mục có tần suất xuất hiện rất thấp. Việc trực quan hóa trực tiếp tất cả các danh mục này có thể khiến biểu đồ trở nên khó đọc và làm phân tán các insight quan trọng.

**2. Giải pháp:**
- Xác định các phân khúc có quy mô lớn nhất dựa trên số lượng booking (volume).
- Chỉ giữ lại top N phân khúc theo volume cho mỗi chiều phân tích.
- Gộp các phân khúc còn lại vào một nhóm chung (“Other”).

**3. Lợi ích:**
- Biểu đồ trở nên rõ ràng và dễ diễn giải hơn.
- Insight tập trung vào các phân khúc có tác động thực sự đến doanh thu và rủi ro.
- Vẫn đảm bảo bao quát đầy đủ các phân khúc chính trong dữ liệu, tránh bỏ sót các nhóm quan trọng.

In [304]:
def standardize_segment(df, column, top_n=8):
    """Keep top N categories by count, group others as 'Other'"""
    value_counts = df[column].value_counts()
    top_categories = value_counts.head(top_n).index.tolist()
    
    new_col = f"{column}_std"
    df[new_col] = df[column].apply(lambda x: x if x in top_categories else 'Other')
    
    return df, top_categories

# Check unique values in key segmentation variables
print("=== Segmentation Variables ===")
for col in ['hotel', 'market_segment', 'distribution_channel', 'customer_type', 'deposit_type']:
    if col in df_q4.columns:
        n_unique = df_q4[col].nunique()
        print(f"\n{col}: {n_unique} unique values")
        print(df_q4[col].value_counts())

# Standardize market_segment (typically has many categories)
if 'market_segment' in df_q4.columns:
    df_q4, top_market_segments = standardize_segment(df_q4, 'market_segment', top_n=8)
    print(f"\n\nStandardized market_segment to: {df_q4['market_segment_std'].unique()}")

=== Segmentation Variables ===

hotel: 2 unique values
hotel
City Hotel      53055
Resort Hotel    33955
Name: count, dtype: int64

market_segment: 7 unique values
market_segment
Online TA        51370
Offline TA/TO    13852
Direct           11751
Groups            4921
Corporate         4200
Other              914
Undefined            2
Name: count, dtype: int64

distribution_channel: 5 unique values
distribution_channel
TA/TO        68842
Direct       12920
Corporate     5062
Other          181
Undefined        5
Name: count, dtype: int64

customer_type: 4 unique values
customer_type
Transient          71726
Transient-Party    11610
Contract            3134
Group                540
Name: count, dtype: int64

deposit_type: 3 unique values
deposit_type
No Deposit    85865
Non Refund     1038
Refundable      107
Name: count, dtype: int64


Standardized market_segment to: ['Direct' 'Corporate' 'Online TA' 'Offline TA/TO' 'Other' 'Groups'
 'Undefined']


#### **4. Xây dựng bảng tổng hợp quy mô (Volume Summary) theo phân khúc:**

**1. Vai trò của yếu tố quy mô (Volume):**

Trong bối cảnh kinh doanh, mức độ ảnh hưởng của một phân khúc không chỉ phụ thuộc vào ADR hoặc tỷ lệ hủy, mà còn phụ thuộc đáng kể vào quy mô booking. Một phân khúc có tỷ lệ hủy cao nhưng quy mô nhỏ có thể ít ảnh hưởng hơn so với một phân khúc có tỷ lệ hủy trung bình nhưng chiếm tỷ trọng lớn trong tổng số booking.

**2. Các chỉ số tổng hợp cho mỗi phân khúc:** 

Để đánh giá toàn diện giá trị và rủi ro của từng phân khúc khách hàng, metrics được xây dựng với các chỉ số sau:
- Số lượng booking (`Count`): tổng số booking thuộc phân khúc
- ADR trung bình (`Mean ADR`): phản ánh mức giá trung bình nhưng nhạy cảm với outliers
- ADR trung vị (`Median ADR`): chỉ số bền vững hơn, phản ánh mức giá điển hình của phân khúc
- Tỷ lệ hủy đặt phòng (`Cancellation Rate`): tỷ lệ booking có is_canceled = 1
- Tỷ trọng booking (`Volume Share`): tỷ lệ phần trăm số booking của phân khúc so với tổng số booking


In [305]:
def create_segment_summary(df, segment_col, adr_col='adr_clipped', cancel_col='is_canceled'):
    """Create comprehensive summary by segment"""
    summary = df.groupby(segment_col).agg({
        cancel_col: ['count', 'mean'],
        adr_col: ['mean', 'median', 'std']
    }).round(2)
    
    # Flatten column names
    summary.columns = ['count', 'cancel_rate', 'adr_mean', 'adr_median', 'adr_std']
    
    # Convert cancel_rate to percentage
    summary['cancel_rate'] = (summary['cancel_rate'] * 100).round(2)
    
    # Add volume share
    summary['volume_share'] = (summary['count'] / summary['count'].sum() * 100).round(2)
    
    # Sort by count descending
    summary = summary.sort_values('count', ascending=False)
    
    return summary

# Create summaries for key segments
print("=== Preprocessing: Complete ===")
print(f"Final dataset shape: {df_q4.shape}")
print(f"ADR range after clipping: [{df_q4['adr_clipped'].min():.2f}, {df_q4['adr_clipped'].max():.2f}]")
print(f"Ready for analysis!")

=== Preprocessing: Complete ===
Final dataset shape: (87010, 32)
ADR range after clipping: [0.00, 262.00]
Ready for analysis!


### **C. Phân tích và trực quan hóa**

Phần này trình bày quy trình phân tích và trực quan hóa dữ liệu nhằm làm rõ mối quan hệ giữa mức giá phòng (ADR), tỷ lệ hủy đặt phòng và quy mô booking theo các phân khúc khách hàng. Quy trình phân tích được triển khai theo bốn bước chính:

- 1 - Phân tích phân phối ADR tổng quan và theo loại hình khách sạn
- 2 - So sánh ADR giữa các phân khúc khách hàng
- 3 - So sánh tỷ lệ hủy đặt phòng giữa các phân khúc khách hàng
- 4 - Kết hợp ADR, tỷ lệ hủy và quy mô booking nhằm xác định các insight chiến lược

#### **1. Phân phối ADR tổng quan và theo loại hình khách sạn**

Mục tiêu phân tích:
- Đánh giá hình dạng phân phối của ADR (độ lệch, mức độ tập trung)
- So sánh đặc điểm phân phối giá phòng giữa City Hotel và Resort Hotel
- Nhận diện các cụm giá bất thường, bao gồm các giá trị rất thấp (gần 0) hoặc rất cao

In [306]:
fig = go.Figure()

# Histogram
fig.add_trace(go.Histogram(
    x=df_q4['adr_clipped'],
    nbinsx=50,
    name='ADR Distribution',
    marker_color='lightblue',
    opacity=0.7
))

# Add mean line
mean_adr = df_q4['adr_clipped'].mean()
fig.add_vline(x=mean_adr, line_dash="dash", line_color="red", 
              annotation_text=f"Mean: {mean_adr:.2f}",
              annotation_position="top right")

# Add median line
median_adr = df_q4['adr_clipped'].median()
fig.add_vline(x=median_adr, line_dash="dash", line_color="green",
              annotation_text=f"Median: {median_adr:.2f}",
              annotation_position="bottom right")

fig.update_layout(
    title="Chart 1: ADR Distribution (after handling outliers)",
    xaxis_title="ADR (EUR)",
    yaxis_title="Number of Bookings",
    height=500,
    showlegend=True
)

fig.show()

print(f"Mean ADR: {mean_adr:.2f} EUR")
print(f"Median ADR: {median_adr:.2f} EUR")
print(f"Skewness: Mean > Median => Right-skewed distribution")

Mean ADR: 106.21 EUR
Median ADR: 98.33 EUR
Skewness: Mean > Median => Right-skewed distribution


Kết quả phân tích phân phối ADR sau khi xử lý các giá trị ngoại lệ cho thấy một số đặc điểm quan trọng:
    
- Thứ nhất, phân phối ADR có dạng lệch phải (right-skewed), thể hiện qua việc giá trị trung bình (Mean ADR = 106.21 EUR) cao hơn đáng kể so với giá trị trung vị (Median ADR = 98.33 EUR). Điều này cho thấy phần lớn các booking tập trung ở mức giá trung bình–thấp, trong khi tồn tại một số booking có mức giá cao kéo trung bình lên.
- Thứ hai, ADR chủ yếu tập trung trong khoảng xấp xỉ 60–140 EUR, phản ánh vùng giá cốt lõi mà đa số khách hàng chấp nhận. Các booking có ADR rất cao (>200 EUR) chỉ chiếm tỷ lệ nhỏ, đóng vai trò như “đuôi phân phối” hơn là đại diện cho hành vi định giá phổ biến.
- Thứ ba, sau khi xử lý outliers, phân phối ADR trở nên ổn định và liên tục hơn, cho thấy các bước tiền xử lý đã loại bỏ hiệu quả các giá trị bất thường có khả năng gây sai lệch trong các so sánh theo phân khúc ở các bước phân tích tiếp theo.

Từ các quan sát trên, có thể kết luận rằng median ADR là chỉ số đại diện phù hợp hơn mean ADR khi so sánh mức giá giữa các phân khúc khách hàng, do tính bền vững cao hơn trước ảnh hưởng của các giá trị cực đoan.

In [307]:
fig = go.Figure()

# City Hotel
city_adr = df_q4[df_q4['hotel'] == 'City Hotel']['adr_clipped']
fig.add_trace(go.Histogram(
    x=city_adr,
    name='City Hotel',
    opacity=0.6,
    nbinsx=50,
    marker_color='blue'
))

# Resort Hotel
resort_adr = df_q4[df_q4['hotel'] == 'Resort Hotel']['adr_clipped']
fig.add_trace(go.Histogram(
    x=resort_adr,
    name='Resort Hotel',
    opacity=0.6,
    nbinsx=50,
    marker_color='orange'
))

fig.update_layout(
    title="Chart 2: ADR Distribution by Hotel Type",
    xaxis_title="ADR (EUR)",
    yaxis_title="Number of Bookings",
    barmode='overlay',
    height=500
)

fig.show()

# Statistics by hotel
print("=== ADR Statistics by Hotel Type ===")
hotel_stats = df_q4.groupby('hotel')['adr_clipped'].agg(['count', 'mean', 'median', 'std']).round(2)
print(hotel_stats)

=== ADR Statistics by Hotel Type ===
              count    mean  median    std
hotel                                     
City Hotel    53055  111.19   105.4  41.48
Resort Hotel  33955   98.41    79.5  61.72


**So sánh phân phối ADR giữa City Hotel và Resort Hotel cho thấy sự khác biệt rõ rệt về chiến lược định giá và cấu trúc khách hàng.**

Thứ nhất, City Hotel có mức ADR cao hơn một cách nhất quán so với Resort Hotel. Cụ thể, City Hotel có:
- Mean ADR ≈ 111.19 EUR
- Median ADR ≈ 105.4 EUR

trong khi Resort Hotel có:
- Mean ADR ≈ 98.41 EUR
- Median ADR ≈ 79.5 EUR

Sự chênh lệch này cho thấy City Hotel có khả năng định giá cao hơn, phản ánh đặc điểm nhu cầu lưu trú ngắn hạn, vị trí trung tâm và nhóm khách hàng công tác hoặc đô thị.

Thứ hai, phân phối ADR của Resort Hotel phân tán rộng hơn (độ lệch chuẩn cao hơn), cho thấy mức độ biến động giá lớn hơn theo mùa và theo loại khách. Resort Hotel có nhiều booking ở mức giá thấp, đồng thời cũng tồn tại các booking có ADR rất cao trong mùa cao điểm, dẫn đến phân phối trải dài hơn so với City Hotel.

Thứ ba, City Hotel thể hiện mức độ tập trung giá cao hơn, với phần lớn booking nằm trong dải giá trung bình–cao. Điều này hàm ý mô hình kinh doanh của City Hotel ổn định hơn về giá, ít phụ thuộc vào các giai đoạn cao điểm cực đoan như Resort Hotel.

**Insights:**

Từ kết quả của hai biểu đồ trong C1, một số hàm ý quan trọng được rút ra:
1. Việc sử dụng median ADR thay vì mean ADR là cần thiết khi so sánh giá giữa các phân khúc khách hàng nhằm tránh sai lệch do phân phối lệch phải.
2. Sự khác biệt rõ ràng giữa City Hotel và Resort Hotel cho thấy các phân tích theo phân khúc (C2–C4) cần tách riêng theo loại hình khách sạn, thay vì gộp chung.
3. Phân phối ADR rộng và biến động hơn của Resort Hotel gợi ý khả năng tồn tại mối quan hệ mạnh giữa ADR, mùa vụ và tỷ lệ hủy, cần được kiểm chứng ở các bước phân tích tiếp theo.

#### **2. So sánh ADR theo các phân khúc khách hàng**

**Mục tiêu:** 
- Xác định sự khác biệt về mức giá phòng trung bình giữa các phân khúc khách hàng
- So sánh mức ADR giữa City Hotel và Resort Hotel trong cùng một phân khúc
- Nhận diện các phân khúc có khả năng tạo ra giá trị cao (high-value segments)

In [308]:
if 'market_segment_std' in df_q4.columns:
    segment_col = 'market_segment_std'
else:
    segment_col = 'market_segment'

market_summary = create_segment_summary(df_q4, segment_col)
print("=== Table 1: Market Segment Summary ===")
print(market_summary)
print("\n")

# Distribution Channel
channel_summary = create_segment_summary(df_q4, 'distribution_channel')
print("=== Distribution Channel Summary ===")
print(channel_summary)
print("\n")

# Customer Type
customer_summary = create_segment_summary(df_q4, 'customer_type')
print("=== Customer Type Summary ===")
print(customer_summary)
print("\n")

# Deposit Type
deposit_summary = create_segment_summary(df_q4, 'deposit_type')
print("=== Deposit Type Summary ===")
print(deposit_summary)

=== Table 1: Market Segment Summary ===
                    count  cancel_rate  adr_mean  adr_median  adr_std  \
market_segment_std                                                      
Online TA           51370         35.0    118.07       111.0    48.41   
Offline TA/TO       13852         15.0     81.54        79.2    36.16   
Direct              11751         15.0    116.22       107.0    57.78   
Groups               4921         27.0     75.00        68.0    36.92   
Corporate            4200         12.0     68.27        65.0    32.09   
Other                 914         14.0     27.21         0.0    45.04   
Undefined               2        100.0     15.00        15.0     4.24   

                    volume_share  
market_segment_std                
Online TA                  59.04  
Offline TA/TO              15.92  
Direct                     13.51  
Groups                      5.66  
Corporate                   4.83  
Other                       1.05  
Undefined             

In [309]:
# Filter out 'Other' for cleaner visualization
market_summary_plot = market_summary[market_summary.index != 'Other'].sort_values('adr_median', ascending=True)

fig = go.Figure()

fig.add_trace(go.Bar(
    y=market_summary_plot.index,
    x=market_summary_plot['adr_median'],
    orientation='h',
    marker=dict(
        color=market_summary_plot['adr_median'],
        colorscale='Viridis',
        showscale=True,
        colorbar=dict(title="Median ADR")
    ),
    text=market_summary_plot['adr_median'].round(2),
    textposition='outside',
    hovertemplate='<b>%{y}</b><br>' +
                  'Median ADR: %{x:.2f} EUR<br>' +
                  '<extra></extra>'
))

fig.update_layout(
    title="Chart 3: Median ADR by Market Segment (Top segments)",
    xaxis_title="Median ADR (EUR)",
    yaxis_title="Market Segment",
    height=500,
    showlegend=False
)

fig.show()

Kết quả trên cho thấy sự phân hóa rõ rệt về mức giá phòng trung vị (median ADR) giữa các phân khúc thị trường:
    
- Online Travel Agencies (Online TA) ghi nhận median ADR cao nhất (≈ 111 EUR), đồng thời cũng là phân khúc có quy mô lớn nhất, chiếm khoảng 59% tổng số booking.
- Direct booking đứng thứ hai về mức giá với median ADR ≈ 107 EUR, cho thấy nhóm khách hàng đặt trực tiếp có mức sẵn sàng chi trả cao, gần tương đương với Online TA.
- Offline TA/TO có mức median ADR thấp hơn đáng kể (≈ 79 EUR), phản ánh chiến lược giá mang tính thương lượng hoặc bán theo gói.
- Groups và Corporate là các phân khúc có ADR thấp nhất trong nhóm chính (median ADR lần lượt ≈ 68 EUR và 65 EUR), phù hợp với đặc điểm đặt số lượng lớn hoặc hợp đồng dài hạn.
- Phân khúc Undefined có ADR rất thấp nhưng quy mô không đáng kể, xác nhận rằng nhóm này không có ý nghĩa thực tiễn trong phân tích kinh doanh.

Kết quả này cho thấy Online TA và Direct booking là hai phân khúc tạo giá trị giá phòng cao nhất, trong khi các phân khúc còn lại chủ yếu đóng vai trò lấp đầy công suất.

**Insights**:
1. ADR khác biệt đáng kể giữa các phân khúc thị trường, xác nhận sự cần thiết của chiến lược định giá phân khúc hóa.
2. Online TA và Direct booking là các phân khúc có giá trị cao, nhưng cần được đánh giá đồng thời với rủi ro hủy (sẽ phân tích ở C3).
3. Các phân khúc Corporate và Groups tuy có ADR thấp nhưng mang lại sự ổn định, đóng vai trò hỗ trợ tối ưu công suất hơn là tối đa hóa giá.

#### **3. So sánh tỷ lệ hủy đặt phòng theo các phân khúc khách hàng**

**Mục tiêu:**
- Đánh giá mức độ rủi ro hủy đặt phòng của từng phân khúc khách hàng
- So sánh hành vi hủy giữa City Hotel và Resort Hotel
- Xác định các phân khúc có rủi ro cao cần được quản lý chặt chẽ hơn

In [310]:
market_cancel_plot = market_summary[market_summary.index != 'Other'].sort_values('cancel_rate', ascending=True)

fig = go.Figure()

fig.add_trace(go.Bar(
    y=market_cancel_plot.index,
    x=market_cancel_plot['cancel_rate'],
    orientation='h',
    marker=dict(
        color=market_cancel_plot['cancel_rate'],
        colorscale='Reds',
        showscale=True,
        colorbar=dict(title="Cancel Rate (%)")
    ),
    text=market_cancel_plot['cancel_rate'].round(2),
    textposition='outside',
    hovertemplate='<b>%{y}</b><br>' +
                  'Cancel Rate: %{x:.2f}%<br>' +
                  '<extra></extra>'
))

fig.update_layout(
    title="Chart 4: Cancel Rate by Market Segment",
    xaxis_title="Cancel Rate (%)",
    yaxis_title="Market Segment",
    height=500,
    showlegend=False
)

fig.show()

print("=== High-Risk Segments (Cancel Rate > 40%) ===")
high_risk = market_summary[market_summary['cancel_rate'] > 40].sort_values('cancel_rate', ascending=False)
print(high_risk[['count', 'cancel_rate', 'adr_median', 'volume_share']])

=== High-Risk Segments (Cancel Rate > 40%) ===
                    count  cancel_rate  adr_median  volume_share
market_segment_std                                              
Undefined               2        100.0        15.0           0.0


Kết quả từ Biểu đồ 4 cho thấy sự khác biệt rõ rệt về tỷ lệ hủy đặt phòng giữa các phân khúc thị trường:

- Online Travel Agencies (Online TA) có tỷ lệ hủy cao nhất trong các phân khúc chính, ở mức khoảng 35%, cho thấy mức độ rủi ro đáng kể gắn liền với nhóm khách hàng này.
- Groups ghi nhận tỷ lệ hủy ở mức trung bình cao (≈ 27%), phản ánh tính không chắc chắn trong các booking theo đoàn, vốn phụ thuộc vào quy mô và kế hoạch tổ chức.
- Direct và Offline TA/TO có tỷ lệ hủy tương đương nhau (≈ 15%), cho thấy mức độ ổn định cao hơn so với Online TA và Groups.
- Corporate là phân khúc ổn định nhất với tỷ lệ hủy thấp nhất (≈ 12%), phù hợp với đặc điểm hợp đồng và quan hệ khách hàng dài hạn.
- Phân khúc Undefined có tỷ lệ hủy 100%, tuy nhiên quy mô booking không đáng kể (2 booking) và do đó không có ý nghĩa thực tiễn trong phân tích kinh doanh.

Nhìn chung, các phân khúc có mức độ cam kết cao hơn (Corporate, Direct) có xu hướng hủy thấp hơn so với các phân khúc trung gian (OTA, Groups).

**Insights**:

Từ kết quả phân tích, có thể rút ra các hàm ý quan trọng:
1. Các phân khúc có tỷ lệ hủy cao và quy mô lớn (đặc biệt là Online TA) cần được áp dụng chính sách quản lý rủi ro chặt chẽ hơn, như đặt cọc bắt buộc hoặc điều chỉnh điều khoản hủy.
2. Các phân khúc có tỷ lệ hủy thấp (Corporate, Direct) có thể được xem là nền tảng ổn định cho dự báo doanh thu và hoạch định công suất.
3. Các phân khúc có tỷ lệ hủy cao nhưng quy mô nhỏ có thể được chấp nhận trong chừng mực nhất định do tác động tổng thể thấp.

#### **4. Kết hợp ADR, tỷ lệ hủy và quy mô booking để xác định insight chiến lược**

Mục tiêu:
Bước phân tích này nhằm kết hợp ba yếu tố cốt lõi:
- Giá trị (ADR)
- Rủi ro (tỷ lệ hủy)
- Tác động thực tế (quy mô booking)

Qua đó xác định các phân khúc khách hàng chiến lược.

In [311]:
# Prepare data (exclude 'Other')
plot_data = market_summary[market_summary.index != 'Other'].copy()

# Calculate overall medians for quadrant lines
median_adr_overall = df_q4['adr_clipped'].median()
median_cancel_overall = df_q4['is_canceled'].mean() * 100

fig = go.Figure()

# Scatter plot with bubble size
fig.add_trace(go.Scatter(
    x=plot_data['adr_median'],
    y=plot_data['cancel_rate'],
    mode='markers+text',
    marker=dict(
        size=plot_data['volume_share'] * 5,  # Scale for visibility
        color=plot_data['cancel_rate'],
        colorscale='RdYlGn_r',  # Red = high cancel, Green = low cancel
        showscale=True,
        colorbar=dict(title="Cancel Rate (%)"),
        line=dict(width=1, color='white')
    ),
    text=plot_data.index,
    textposition='top center',
    textfont=dict(size=9),
    hovertemplate='<b>%{text}</b><br>' +
                  'Median ADR: %{x:.2f} EUR<br>' +
                  'Cancel Rate: %{y:.2f}%<br>' +
                  'Volume Share: ' + plot_data['volume_share'].round(2).astype(str) + '%<br>' +
                  '<extra></extra>'
))

# Add quadrant lines
fig.add_hline(y=median_cancel_overall, line_dash="dash", line_color="gray", 
              annotation_text=f"Median Cancel Rate: {median_cancel_overall:.1f}%")
fig.add_vline(x=median_adr_overall, line_dash="dash", line_color="gray",
              annotation_text=f"Median ADR: {median_adr_overall:.1f}")
# Add quadrant annotations
fig.add_annotation(x=median_adr_overall * 1.3, y=median_cancel_overall * 0.5,
                  text="High ADR<br>Low Cancel<br>(PREMIUM STABLE)",
                  showarrow=False, font=dict(size=10, color="green"), bgcolor="rgba(255,255,255,0.7)")

fig.add_annotation(x=median_adr_overall * 1.3, y=median_cancel_overall * 1.5,
                  text="High ADR<br>High Cancel<br>(RISKY PREMIUM)",
                  showarrow=False, font=dict(size=10, color="orange"), bgcolor="rgba(255,255,255,0.7)")

fig.add_annotation(x=median_adr_overall * 0.7, y=median_cancel_overall * 0.5,
                  text="Low ADR<br>Low Cancel<br>(STABLE BASE)",
                  showarrow=False, font=dict(size=10, color="blue"), bgcolor="rgba(255,255,255,0.7)")

fig.add_annotation(x=median_adr_overall * 0.7, y=median_cancel_overall * 1.5,
                  text="Low ADR<br>High Cancel<br>(HIGH RISK)",
                  showarrow=False, font=dict(size=10, color="red"), bgcolor="rgba(255,255,255,0.7)")

fig.update_layout(
    title="Chart 5: Strategic Segmentation - ADR vs Cancel Rate vs Volume",
    xaxis_title="Median ADR (EUR)",
    yaxis_title="Cancel Rate (%)",
    height=700,
    showlegend=False
)

fig.show()

Biểu đồ 5 kết hợp ba chiều phân tích chính: ADR trung vị (trục X), tỷ lệ hủy đặt phòng (trục Y) và quy mô booking (kích thước điểm), cho phép phân loại các phân khúc khách hàng theo mức độ giá trị và rủi ro.

Kết quả cho thấy các phân khúc được phân bố rõ ràng vào bốn nhóm chiến lược:

- **Premium Stable (ADR cao – Hủy thấp)**:
Phân khúc **Direct** nằm ở vùng **ADR cao hơn** mức trung vị toàn bộ dữ liệu (≈ 98.3 EUR) và có **tỷ lệ hủy thấp** (≈ 15%). Đây là nhóm khách hàng mang lại giá trị cao và ổn định, phù hợp để ưu tiên phát triển dài hạn.

- Risky Premium (ADR cao – Hủy cao):
Phân khúc Online TA có ADR cao nhất nhưng đi kèm tỷ lệ hủy cao (≈ 35%) và quy mô booking rất lớn. Nhóm này tạo ra doanh thu tiềm năng cao nhưng rủi ro hiện thực hóa lớn, đòi hỏi chiến lược quản lý rủi ro chặt chẽ.

- Stable Base (ADR thấp – Hủy thấp):
Các phân khúc Corporate, Offline TA/TO và Groups tập trung ở vùng ADR thấp hơn nhưng có tỷ lệ hủy tương đối ổn định. Đây là nhóm đóng vai trò nền tảng công suất, hỗ trợ dự báo và ổn định dòng doanh thu.

- High Risk (ADR thấp – Hủy rất cao):
Phân khúc Undefined có tỷ lệ hủy 100%, tuy nhiên do quy mô không đáng kể nên không có ý nghĩa chiến lược trong quản trị kinh doanh.

In [312]:
def classify_segment(row, median_adr, median_cancel):
    """Classify segment into strategic quadrant"""
    if row['adr_median'] >= median_adr and row['cancel_rate'] < median_cancel:
        return 'Premium Stable'
    elif row['adr_median'] >= median_adr and row['cancel_rate'] >= median_cancel:
        return 'Risky Premium'
    elif row['adr_median'] < median_adr and row['cancel_rate'] < median_cancel:
        return 'Stable Base'
    else:
        return 'High Risk'

market_summary['quadrant'] = market_summary.apply(
    lambda row: classify_segment(row, median_adr_overall, median_cancel_overall), 
    axis=1
)

print("=== Strategic Segment Classification ===\n")
for quadrant in ['Premium Stable', 'Risky Premium', 'Stable Base', 'High Risk']:
    segments = market_summary[market_summary['quadrant'] == quadrant]
    if len(segments) > 0:
        print(f"\n{quadrant.upper()}:")
        print(segments[['count', 'adr_median', 'cancel_rate', 'volume_share']].to_string())
        print(f"Total volume share: {segments['volume_share'].sum():.2f}%")

=== Strategic Segment Classification ===


PREMIUM STABLE:
                    count  adr_median  cancel_rate  volume_share
market_segment_std                                              
Direct              11751       107.0         15.0         13.51
Total volume share: 13.51%

RISKY PREMIUM:
                    count  adr_median  cancel_rate  volume_share
market_segment_std                                              
Online TA           51370       111.0         35.0         59.04
Total volume share: 59.04%

STABLE BASE:
                    count  adr_median  cancel_rate  volume_share
market_segment_std                                              
Offline TA/TO       13852        79.2         15.0         15.92
Groups               4921        68.0         27.0          5.66
Corporate            4200        65.0         12.0          4.83
Other                 914         0.0         14.0          1.05
Total volume share: 27.46%

HIGH RISK:
                    count  adr_median 

In [313]:
hotel_segment_summary = df_q4.groupby(['hotel', segment_col]).agg({
    'is_canceled': ['count', 'mean'],
    'adr_clipped': 'median'
}).round(2)

hotel_segment_summary.columns = ['count', 'cancel_rate', 'adr_median']
hotel_segment_summary['cancel_rate'] = (hotel_segment_summary['cancel_rate'] * 100).round(2)
hotel_segment_summary = hotel_segment_summary.reset_index()

# Filter top segments only
top_segments_list = market_summary.head(6).index.tolist()
plot_df = hotel_segment_summary[hotel_segment_summary[segment_col].isin(top_segments_list)]

# Chart 6: Grouped bar chart
fig = go.Figure()

for hotel in ['City Hotel', 'Resort Hotel']:
    hotel_data = plot_df[plot_df['hotel'] == hotel]
    fig.add_trace(go.Bar(
        name=hotel,
        x=hotel_data[segment_col],
        y=hotel_data['cancel_rate'],
        text=hotel_data['cancel_rate'].round(1),
        textposition='outside'
    ))

fig.update_layout(
    title="Chart 6: Cancel Rate - City vs Resort Hotel by Segment",
    xaxis_title="Market Segment",
    yaxis_title="Cancel Rate (%)",
    barmode='group',
    height=500,
    xaxis_tickangle=-45
)

fig.show()


Biểu đồ cho thấy sự khác biệt nhất quán về hành vi hủy đặt phòng giữa hai loại hình khách sạn:
    
1. City Hotel có tỷ lệ hủy cao hơn Resort Hotel ở hầu hết các phân khúc, đặc biệt là:
- Online TA (≈ 36% vs 34%)
- Groups (≈ 34% vs 19%)
2. Corporate là phân khúc ổn định nhất ở cả hai loại khách sạn, với tỷ lệ hủy gần như tương đương.
3. Resort Hotel nhìn chung có mức độ hủy thấp hơn, phản ánh đặc điểm đặt phòng mang tính nghỉ dưỡng, lên kế hoạch sớm và cam kết cao hơn.

Kết quả này cho thấy chiến lược quản lý rủi ro cần được điều chỉnh theo loại hình khách sạn, đặc biệt đối với City Hotel.

### **D. Kết quả và Hành động**

Kết quả phân tích cho thấy các phát hiện chính sau.

**1. Khác biệt có hệ thống giữa City Hotel và Resort Hotel**

City Hotel ghi nhận ADR cao hơn và tỷ lệ hủy cao hơn so với Resort Hotel trên hầu hết các phân khúc khách hàng. Ngược lại, Resort Hotel có mức ADR thấp hơn nhưng tỷ lệ hủy ổn định và thấp hơn. Đáng chú ý, ngay cả trong cùng một phân khúc thị trường, hành vi hủy đặt phòng vẫn khác biệt đáng kể giữa hai loại hình khách sạn, cho thấy bối cảnh lưu trú có ảnh hưởng rõ rệt đến hành vi khách hàng.

**2. Tồn tại các phân khúc có giá trị cao nhưng rủi ro hủy cao**

Một số phân khúc, tiêu biểu là Online Travel Agencies (Online TA), có ADR cao nhưng đồng thời đi kèm tỷ lệ hủy đặt phòng lớn. Mặc dù các phân khúc này tạo ra mức giá danh nghĩa cao, tỷ lệ hủy lớn làm giảm khả năng hiện thực hóa doanh thu, phản ánh sự đánh đổi giữa tối đa hóa giá phòng và kiểm soát rủi ro hủy.

**3. Vai trò quyết định của quy mô đặt phòng**

Kết quả cho thấy một số ít phân khúc chiếm phần lớn tổng số booking, trong đó 3–5 phân khúc hàng đầu đóng góp hơn 70% tổng nhu cầu, và Online TA chiếm tỷ trọng lớn nhất. Do đó, tác động đến doanh thu và rủi ro tổng thể chủ yếu đến từ các phân khúc có quy mô đặt phòng lớn.

**4. Không tồn tại chính sách giá và hủy đặt phòng đồng nhất**

ADR, tỷ lệ hủy và quy mô booking khác biệt đáng kể giữa các phân khúc khách hàng. Điều này cho thấy việc áp dụng một chính sách giá hoặc điều khoản hủy chung cho toàn bộ khách hàng là không hiệu quả, mà cần chiến lược định giá và quản lý hủy đặt phòng theo từng phân khúc.

In [314]:
print("="*80)
print("Q4 SUMMARY: ADR AND CANCEL RATE BY SEGMENT")
print("="*80)

print("\n1. OVERALL STATISTICS:")
print(f"   - Total Bookings: {len(df_q4):,}")
print(f"   - Overall Cancel Rate: {df_q4['is_canceled'].mean()*100:.2f}%")
print(f"   - Overall Median ADR: {df_q4['adr_clipped'].median():.2f} EUR")
print(f"   - Overall Mean ADR: {df_q4['adr_clipped'].mean():.2f} EUR")

print("\n2. BY HOTEL TYPE:")
hotel_overall = df_q4.groupby('hotel').agg({
    'is_canceled': ['count', 'mean'],
    'adr_clipped': ['median', 'mean']
}).round(2)
print(hotel_overall)

print("\n3. TOP 5 SEGMENTS BY VOLUME:")
print(market_summary.head(5)[['count', 'volume_share', 'adr_median', 'cancel_rate']])

print("\n4. STRATEGIC QUADRANTS:")
quadrant_summary = market_summary.groupby('quadrant').agg({
    'count': 'sum',
    'volume_share': 'sum',
    'adr_median': 'mean',
    'cancel_rate': 'mean'
}).round(2)
print(quadrant_summary)

print("\n5. EXTREMES:")
print(f"\n   Highest ADR Segment: {market_summary['adr_median'].idxmax()} "
      f"({market_summary['adr_median'].max():.2f} EUR)")
print(f"   Lowest ADR Segment: {market_summary['adr_median'].idxmin()} "
      f"({market_summary['adr_median'].min():.2f} EUR)")
print(f"   Highest Cancel Rate: {market_summary['cancel_rate'].idxmax()} "
      f"({market_summary['cancel_rate'].max():.2f}%)")
print(f"   Lowest Cancel Rate: {market_summary['cancel_rate'].idxmin()} "
      f"({market_summary['cancel_rate'].min():.2f}%)")

print("\n" + "="*80)

Q4 SUMMARY: ADR AND CANCEL RATE BY SEGMENT

1. OVERALL STATISTICS:
   - Total Bookings: 87,010
   - Overall Cancel Rate: 27.50%
   - Overall Median ADR: 98.33 EUR
   - Overall Mean ADR: 106.21 EUR

2. BY HOTEL TYPE:
             is_canceled       adr_clipped        
                   count  mean      median    mean
hotel                                             
City Hotel         53055  0.30       105.4  111.19
Resort Hotel       33955  0.23        79.5   98.41

3. TOP 5 SEGMENTS BY VOLUME:
                    count  volume_share  adr_median  cancel_rate
market_segment_std                                              
Online TA           51370         59.04       111.0         35.0
Offline TA/TO       13852         15.92        79.2         15.0
Direct              11751         13.51       107.0         15.0
Groups               4921          5.66        68.0         27.0
Corporate            4200          4.83        65.0         12.0

4. STRATEGIC QUADRANTS:
                cou

### **E. Bussiness Insights:**

**1. Phân khúc giá trị cao và ổn định**

Các phân khúc có ADR cao, tỷ lệ hủy thấp và quy mô đáng kể (đặt phòng trực tiếp) nên được ưu tiên trong chiến lược marketing, chương trình khách hàng thân thiết và upselling dịch vụ.

**2. Phân khúc giá trị cao nhưng rủi ro lớn** 

Các phân khúc như Online TA cần được quản lý rủi ro thông qua chính sách đặt cọc, giá không hoàn tiền, điều khoản hủy nghiêm ngặt hơn hoặc chiến lược overbooking có kiểm soát.

**3. Phân khúc nền tảng ổn định**

Các phân khúc có ADR thấp đến trung bình nhưng tỷ lệ hủy thấp (Corporate, Offline TA/TO) đóng vai trò ổn định công suất và hỗ trợ dự báo doanh thu; chiến lược phù hợp là duy trì mức giá cạnh tranh.

**4. Phân khúc rủi ro cao**

Các phân khúc có ADR thấp và tỷ lệ hủy cao cần được kiểm soát chặt chẽ hoặc hạn chế; trong trường hợp quy mô lớn, cần phân tích sâu hơn nguyên nhân hủy để điều chỉnh chính sách.

**5. Phân biệt theo loại hình khách sạn**

Chiến lược định giá và chính sách hủy đặt phòng cần được thiết kế riêng cho City Hotel và Resort Hotel, thay vì áp dụng đồng nhất trên toàn hệ thống.

### **F. Kết luận:** 

ADR và tỷ lệ hủy đặt phòng khác biệt có hệ thống giữa các phân khúc khách hàng và loại hình khách sạn. Giá trị kinh tế thực sự không chỉ phụ thuộc vào ADR, mà là sự kết hợp của **giá trị – rủi ro – quy mô booking**.

Kết quả nhấn mạnh sự cần thiết của:

- Định giá phân khúc hóa
- Chính sách hủy linh hoạt theo mức độ rủi ro
- Quản lý kênh bán và loại hình khách sạn một cách khác biệt

Những phát hiện này tạo nền tảng trực tiếp cho các phân tích sâu hơn về nguyên nhân hành vi hủy đặt phòng ở các câu hỏi tiếp theo.

---
## **Q5 - Driver Analysis: Yếu tố Ngoài Giá Ảnh hưởng đến Hủy phòng**

**Những yếu tố nào (ngoài giá phòng/ADR) liên quan mạnh nhất đến khả năng khách hủy đặt phòng, và mức độ ảnh hưởng của chúng khác nhau ra sao giữa City Hotel và Resort Hotel?**

### **A. Chuẩn bị dữ liệu - Chọn và Chuẩn bị Drivers**

Phân tích tập trung vào các yếu tố ngoài mức giá phòng trung bình (ADR); do đó, việc lựa chọn và tiền xử lý các biến tác nhân được thực hiện một cách có hệ thống nhằm đảm bảo tính phù hợp và độ tin cậy của kết quả phân tích.

#### **1. Lựa chọn các biến tác nhân (ngoài ADR):**

Các biến được lựa chọn phản ánh các khía cạnh chính của hành vi đặt phòng và mức độ cam kết của khách hàng, bao gồm các nhóm sau:

**1. Thời điểm đặt phòng (Booking Timing)**
Biến `lead_time` được sử dụng để đo lường số ngày từ thời điểm đặt phòng đến ngày nhận phòng, phản ánh mức độ cam kết và tính không chắc chắn của booking.

**2. Chính sách và mức độ cam kết (Policy and Commitment)**
Biến `deposit_type` (No Deposit, Non Refund, Refundable) đại diện cho mức độ ràng buộc tài chính của khách hàng tại thời điểm đặt phòng.

**3. Kênh phân phối và phân khúc thị trường (Channel and Segment)**
Các biến `market_segment` và `distribution_channel` được sử dụng để phản ánh sự khác biệt về hành vi khách hàng giữa các kênh bán và phân khúc thị trường khác nhau.

**4. Đặc điểm khách hàng (Customer Profile)**
Biến `customer_type` và `is_repeated_guest` được đưa vào phân tích nhằm đánh giá ảnh hưởng của loại khách hàng và hành vi quay lại đến khả năng hủy đặt phòng.

**5. Lịch sử hành vi (Behavioral History)**
Các biến `previous_cancellations` và `previous_bookings_not_canceled` phản ánh hành vi đặt phòng trong quá khứ và được kỳ vọng có mối liên hệ với xác suất hủy trong hiện tại.

**6. Mức độ tương tác với khách sạn (Customer Engagement)**
Biến `total_of_special_requests` được sử dụng như một chỉ báo cho mức độ tương tác và cam kết của khách hàng đối với booking.

**7. Yếu tố mùa vụ (Seasonality)**
Biến `arrival_date_month` được đưa vào nhằm kiểm soát tác động của yếu tố mùa vụ đến hành vi hủy đặt phòng.

In [315]:
df_q5 = df_q4.copy()

# Define driver variables (excluding ADR)
driver_variables = {
    'timing': ['lead_time'],
    'policy': ['deposit_type'],
    'channel': ['market_segment', 'distribution_channel'],
    'customer': ['customer_type', 'is_repeated_guest'],
    'history': ['previous_cancellations', 'previous_bookings_not_canceled'],
    'engagement': ['total_of_special_requests'],
    'seasonality': ['arrival_date_month']
}

# Flatten list
all_drivers = [var for category in driver_variables.values() for var in category]
all_drivers.append('is_canceled')  # target
all_drivers.append('hotel')  # for subgroup analysis

print("=== Selected Driver Variables ===")
for category, variables in driver_variables.items():
    print(f"\n{category.upper()}:")
    for var in variables:
        if var in df_q5.columns:
            print(f"  {var}")
        else:
            print(f"  {var} (not found)")

print(f"\nTotal drivers selected: {len([v for v in all_drivers if v in df_q5.columns])}")

=== Selected Driver Variables ===

TIMING:
  lead_time

POLICY:
  deposit_type

CHANNEL:
  market_segment
  distribution_channel

CUSTOMER:
  customer_type
  is_repeated_guest

HISTORY:
  previous_cancellations
  previous_bookings_not_canceled

ENGAGEMENT:
  total_of_special_requests

SEASONALITY:
  arrival_date_month

Total drivers selected: 12


#### **2. Kiểm tra chất lượng dữ liệu:**

**Mục tiêu**: Đảm bảo dữ liệu hợp lý trước khi phân tích tác nhân

In [316]:
print("=== Data Quality Checks ===\n")

# 1. Check for negative lead_time
if 'lead_time' in df_q5.columns:
    negative_lead = (df_q5['lead_time'] < 0).sum()
    print(f"1. Negative lead_time: {negative_lead} ({negative_lead/len(df_q5)*100:.2f}%)")

# 2. Check total guests
df_q5['total_guests'] = df_q5['adults'] + df_q5['children'] + df_q5['babies']
zero_guests = (df_q5['total_guests'] == 0).sum()
print(f"2. Zero total guests: {zero_guests} ({zero_guests/len(df_q5)*100:.2f}%)")

# 3. Check missing values in key drivers
print("\n3. Missing values in drivers:")
for var in all_drivers:
    if var in df_q5.columns:
        missing = df_q5[var].isna().sum()
        if missing > 0:
            print(f"   {var}: {missing} ({missing/len(df_q5)*100:.2f}%)")

# 4. Summary statistics for numeric drivers
print("\n4. Numeric driver statistics:")
numeric_drivers = ['lead_time', 'previous_cancellations', 
                   'previous_bookings_not_canceled', 'total_of_special_requests']
print(df_q5[numeric_drivers].describe())

print("\nData quality check complete. No critical issues found.")

=== Data Quality Checks ===

1. Negative lead_time: 0 (0.00%)
2. Zero total guests: 0 (0.00%)

3. Missing values in drivers:

4. Numeric driver statistics:
          lead_time  previous_cancellations  previous_bookings_not_canceled  \
count  87010.000000            87010.000000                    87010.000000   
mean      79.861050                0.030456                        0.184485   
std       86.007313                0.369779                        1.735185   
min        0.000000                0.000000                        0.000000   
25%       11.000000                0.000000                        0.000000   
50%       49.000000                0.000000                        0.000000   
75%      125.000000                0.000000                        0.000000   
max      737.000000               26.000000                       72.000000   

       total_of_special_requests  
count               87010.000000  
mean                    0.698127  
std                     0.8

#### **3. Phân nhóm các biến số thực:**

**Mục tiêu**: Để dễ visualize và interpret, ta cần bin các biến numeric thành categories

In [317]:
df_q5['lead_time_bin'] = pd.cut(
    df_q5['lead_time'],
    bins=[-1, 7, 30, 90, 180, 1000],
    labels=['0-7 days', '8-30 days', '31-90 days', '91-180 days', '180+ days']
)

# Special requests bins
df_q5['special_requests_bin'] = pd.cut(
    df_q5['total_of_special_requests'],
    bins=[-1, 0, 1, 2, 10],
    labels=['None', '1 request', '2 requests', '3+ requests']
)

# Previous cancellations bins
df_q5['prev_cancel_bin'] = pd.cut(
    df_q5['previous_cancellations'],
    bins=[-1, 0, 1, 2, 100],
    labels=['Never', '1 time', '2 times', '3+ times']
)

print("=== Binning Complete ===\n")

# Show distribution of lead_time_bin
print("Lead Time Distribution:")
print(df_q5['lead_time_bin'].value_counts().sort_index())
print(f"\nCancel rate by lead_time_bin:")
print(df_q5.groupby('lead_time_bin')['is_canceled'].mean().mul(100).round(2))

=== Binning Complete ===

Lead Time Distribution:
lead_time_bin
0-7 days       18185
8-30 days      16300
31-90 days     22666
91-180 days    18170
180+ days      11689
Name: count, dtype: int64

Cancel rate by lead_time_bin:
lead_time_bin
0-7 days        8.41
8-30 days      25.36
31-90 days     32.05
91-180 days    35.00
180+ days      39.70
Name: is_canceled, dtype: float64


### **B. Phân tích Drivers**

Phần này trình bày quy trình phân tích các **yếu tố ngoài giá** ảnh hưởng đến **khả năng hủy đặt phòng**. Phân tích được thực hiện theo bốn bước liên tiếp nhằm xác định, đánh giá và so sánh **mức độ ảnh hưởng của các biến tác nhân**.

Phần này thực hiện 4 bước phân tích:

- **1. Driver Screening** - Xác định drivers quan trọng

- **2. Interaction Analysis** - Phân tích tương tác giữa drivers

- **3. Logistic Regression** - Quantify tác động tương đối

- **4. City vs Resort** - So sánh subgroups

#### **1. Driver Screening - Xác định Drivers Quan trọng**

**Mục tiêu**: Đánh giá nhanh xem biến nào có liên hệ mạnh với cancellation

In [318]:
deposit_analysis = df_q5.groupby('deposit_type').agg({
    'is_canceled': ['count', 'mean']
}).round(4)
deposit_analysis.columns = ['count', 'cancel_rate']
deposit_analysis['cancel_rate'] = deposit_analysis['cancel_rate'] * 100
deposit_analysis = deposit_analysis.sort_values('cancel_rate', ascending=True)

fig = go.Figure()

fig.add_trace(go.Bar(
    y=deposit_analysis.index,
    x=deposit_analysis['cancel_rate'],
    orientation='h',
    marker=dict(
        color=deposit_analysis['cancel_rate'],
        colorscale='Reds',
        showscale=True,
        colorbar=dict(title="Cancel Rate (%)")
    ),
    text=[f"{rate:.1f}% (n={count:,})" 
          for rate, count in zip(deposit_analysis['cancel_rate'], deposit_analysis['count'])],
    textposition='outside',
    hovertemplate='<b>%{y}</b><br>' +
                  'Cancel Rate: %{x:.2f}%<br>' +
                  '<extra></extra>'
))

fig.update_layout(
    title="Plot 1: Cancel Rate by Deposit Type (with volume)",
    xaxis_title="Cancel Rate (%)",
    yaxis_title="Deposit Type",
    height=400,
    showlegend=False
)

fig.show()

print("=== Deposit Type Analysis ===")
print(deposit_analysis)

=== Deposit Type Analysis ===
              count  cancel_rate
deposit_type                    
Refundable      107        24.30
No Deposit    85865        26.69
Non Refund     1038        94.70


Biểu đồ cho thấy sự khác biệt rất lớn về tỷ lệ hủy giữa các loại đặt cọc. 
- Nhóm Non-Refund có tỷ lệ hủy cực kỳ cao (94.7%), trong khi No Deposit và Refundable có tỷ lệ hủy thấp hơn nhiều và tương đối tương đồng (26.7% và 24.3%). 
- Mặc dù số lượng booking của nhóm Non-Refund nhỏ hơn đáng kể, kết quả này cho thấy biến deposit_type có mối liên hệ mạnh với hành vi hủy đặt phòng.

In [319]:
leadtime_analysis = df_q5.groupby('lead_time_bin').agg({
    'is_canceled': ['count', 'mean']
}).round(4)
leadtime_analysis.columns = ['count', 'cancel_rate']
leadtime_analysis['cancel_rate'] = leadtime_analysis['cancel_rate'] * 100

fig = go.Figure()

fig.add_trace(go.Bar(
    x=leadtime_analysis.index.astype(str),
    y=leadtime_analysis['cancel_rate'],
    marker=dict(
        color=leadtime_analysis['cancel_rate'],
        colorscale='Oranges',
        showscale=True,
        colorbar=dict(title="Cancel Rate (%)")
    ),
    text=[f"{rate:.1f}%<br>n={count:,}" 
          for rate, count in zip(leadtime_analysis['cancel_rate'], leadtime_analysis['count'])],
    textposition='outside',
    hovertemplate='<b>%{x}</b><br>' +
                  'Cancel Rate: %{y:.2f}%<br>' +
                  '<extra></extra>'
))

# Add trend line
fig.add_trace(go.Scatter(
    x=leadtime_analysis.index.astype(str),
    y=leadtime_analysis['cancel_rate'],
    mode='lines+markers',
    name='Trend',
    line=dict(color='red', width=3, dash='dash'),
    marker=dict(size=10, color='red')
))

# Add trend line
fig.add_trace(go.Scatter(
    x=leadtime_analysis.index.astype(str),
    y=leadtime_analysis['cancel_rate'],
    mode='lines+markers',
    name='Trend',
    line=dict(color='red', width=3, dash='dash'),
    marker=dict(size=10, color='red')
))

fig.update_layout(
    title="Plot 2: Cancel Rate by Lead Time (booking window)",
    xaxis_title="Lead Time Range",
    yaxis_title="Cancel Rate (%)",
    height=500,
    showlegend=True
)

fig.show()

print("=== Lead Time Analysis ===")
print(leadtime_analysis)

=== Lead Time Analysis ===
               count  cancel_rate
lead_time_bin                    
0-7 days       18185         8.41
8-30 days      16300        25.36
31-90 days     22666        32.05
91-180 days    18170        35.00
180+ days      11689        39.70


Tỷ lệ hủy đặt phòng tăng rõ rệt theo thời gian đặt phòng trước. 
- Các booking có lead time ngắn (0–7 ngày) ghi nhận tỷ lệ hủy thấp nhất (8.4%), trong khi tỷ lệ này tăng dần qua các nhóm và đạt mức cao nhất ở lead time trên 180 ngày (39.7%).
- Xu hướng tăng gần như đơn điệu cho thấy mối quan hệ dương rõ rệt giữa lead time và xác suất hủy đặt phòng.

In [320]:
print("=== Quick Screening: Cancel Rate by Key Drivers ===\n")

categorical_drivers = ['customer_type', 'is_repeated_guest', 'market_segment', 'distribution_channel']

for driver in categorical_drivers:
    if driver in df_q5.columns:
        analysis = df_q5.groupby(driver).agg({
            'is_canceled': ['count', 'mean']
        }).round(4)
        analysis.columns = ['count', 'cancel_rate']
        analysis['cancel_rate'] = analysis['cancel_rate'] * 100
        analysis = analysis.sort_values('cancel_rate', ascending=False)
        
        print(f"\n{driver.upper()}:")
        print(analysis.head(10))
        print(f"Range: {analysis['cancel_rate'].min():.1f}% - {analysis['cancel_rate'].max():.1f}%")
        print("-" * 60)

=== Quick Screening: Cancel Rate by Key Drivers ===


CUSTOMER_TYPE:
                 count  cancel_rate
customer_type                      
Transient        71726        30.12
Contract          3134        16.34
Transient-Party  11610        15.15
Group              540         9.81
Range: 9.8% - 30.1%
------------------------------------------------------------

IS_REPEATED_GUEST:
                   count  cancel_rate
is_repeated_guest                    
0                  83648        28.29
1                   3362         7.73
Range: 7.7% - 28.3%
------------------------------------------------------------

MARKET_SEGMENT:
                count  cancel_rate
market_segment                    
Undefined           2       100.00
Online TA       51370        35.37
Groups           4921        27.07
Offline TA/TO   13852        14.84
Direct          11751        14.72
Other             914        14.11
Corporate        4200        12.12
Range: 12.1% - 100.0%
---------------------------

**Insights**:

Từ bước sàng lọc ban đầu, có thể rút ra các nhận định chính sau:
- Chính sách đặt cọc là tác nhân có mức độ liên hệ mạnh nhất với hủy đặt phòng, đặc biệt là nhóm Non-Refund với hành vi bất thường.
- Lead time có mối quan hệ dương rõ rệt với tỷ lệ hủy; booking càng sớm thì rủi ro hủy càng cao.
- Khách quay lại thể hiện mức độ cam kết cao hơn đáng kể so với khách mới.
- Kênh phân phối, đặc biệt là Online TA, đóng vai trò quan trọng trong việc hình thành rủi ro hủy.

Các biến này được xác định là tác nhân trọng yếu và được đưa vào các bước phân tích tương tác và mô hình hóa trong các mục tiếp theo.

#### **2. Interaction Analysis - Drivers không hoạt động độc lập**

**Mục tiêu**: Chứng minh rằng drivers tương tác với nhau, không thể nhìn riêng lẻ

In [321]:
# Create pivot table
interaction_pivot = df_q5.pivot_table(
    values='is_canceled',
    index='deposit_type',
    columns='lead_time_bin',
    aggfunc='mean'
) * 100

# Also create count table to show volume
count_pivot = df_q5.pivot_table(
    values='is_canceled',
    index='deposit_type',
    columns='lead_time_bin',
    aggfunc='count'
)

fig = go.Figure(data=go.Heatmap(
    z=interaction_pivot.values,
    x=interaction_pivot.columns.astype(str),
    y=interaction_pivot.index,
    colorscale='RdYlGn_r',  # Red = high cancel, Green = low
    text=[[f"{val:.1f}%<br>n={count:,}" 
           for val, count in zip(row_val, row_count)]
          for row_val, row_count in zip(interaction_pivot.values, count_pivot.values)],
    texttemplate='%{text}',
    textfont={"size": 10},
    colorbar=dict(title="Cancel Rate (%)")
))

fig.update_layout(
    title="Plot 3: Heatmap - Cancel Rate by Deposit Type × Lead Time",
    xaxis_title="Lead Time Range",
    yaxis_title="Deposit Type",
    height=500
)

fig.show()

print("=== Interaction: Deposit × Lead Time ===")
print("\nCancel Rate (%):")
print(interaction_pivot.round(1))
print("\nBooking Count:")
print(count_pivot)

=== Interaction: Deposit × Lead Time ===

Cancel Rate (%):
lead_time_bin  0-7 days  8-30 days  31-90 days  91-180 days  180+ days
deposit_type                                                          
No Deposit          8.3       25.2        31.6         34.2       36.8
Non Refund         60.5       78.7        96.5         94.5       98.5
Refundable         16.7       22.2        57.1         19.0       33.3

Booking Count:
lead_time_bin  0-7 days  8-30 days  31-90 days  91-180 days  180+ days
deposit_type                                                          
No Deposit        18141      16221       22518        17857      11128
Non Refund           38         61         141          255        543
Refundable            6         18           7           58         18


Có thể thấy tác động của lead time lên tỷ lệ hủy thay đổi đáng kể tùy theo loại đặt cọc, xác nhận rằng hai biến này không hoạt động độc lập.

- Đối với nhóm No Deposit, tỷ lệ hủy tăng dần theo lead time, từ 8.3% ở nhóm 0–7 ngày lên 36.8% ở nhóm trên 180 ngày, thể hiện mối quan hệ dương rõ rệt và ổn định. Nhóm này chiếm phần lớn tổng số booking, do đó xu hướng này có ảnh hưởng đáng kể đến rủi ro hủy tổng thể.

- Ngược lại, nhóm Non-Refund có tỷ lệ hủy rất cao trên toàn bộ các khoảng lead time, dao động từ 60.5% đến 98.5%. Mức độ hủy cao xuất hiện ngay cả ở lead time ngắn cho thấy tác động của chính sách đặt cọc trong nhóm này vượt trội so với ảnh hưởng của lead time.

- Đối với nhóm Refundable, tỷ lệ hủy thay đổi không ổn định giữa các khoảng lead time và không tuân theo xu hướng đơn điệu. Tuy nhiên, quy mô booking của nhóm này rất nhỏ ở hầu hết các khoảng, làm hạn chế khả năng suy luận mạnh từ kết quả quan sát.

**Insights**:
1. Tác động của lead time lên tỷ lệ hủy phụ thuộc mạnh vào deposit type, xác nhận sự tồn tại của tương tác giữa hai biến.
2. Với No Deposit, lead time là tác nhân phân biệt rủi ro rõ rệt và có xu hướng tăng dần.
3. Với Non-Refund, tỷ lệ hủy duy trì ở mức rất cao bất kể lead time, cho thấy vai trò chi phối của chính sách đặt cọc.
4. Nhóm Refundable có hành vi không ổn định do quy mô mẫu nhỏ, cần được xử lý thận trọng trong các phân tích tiếp theo.

#### **3. Driver Importance - Logistic Regression (Explanatory Model)**

**Mục tiêu**: Quantify tác động tương đối của drivers khi kiểm soát các biến khác

Mô hình hồi quy logistic được sử dụng nhằm định lượng tác động tương đối của các yếu tố ngoài giá đến khả năng hủy đặt phòng trong điều kiện kiểm soát đồng thời các biến còn lại.

**Note**: Đây là mô hình giải thích (explanatory), không phải tối ưu ML

In [322]:
# Select features (excluding ADR as requested)
feature_cols = [
    'lead_time', 'deposit_type', 'market_segment', 'distribution_channel',
    'customer_type', 'is_repeated_guest', 'previous_cancellations',
    'previous_bookings_not_canceled', 'total_of_special_requests',
    'arrival_date_month'
]

# Create a clean dataset
df_model = df_q5[feature_cols + ['is_canceled']].copy()

# Handle categorical variables - one-hot encoding
categorical_cols = ['deposit_type', 'market_segment', 'distribution_channel', 
                    'customer_type', 'arrival_date_month']

df_encoded = pd.get_dummies(df_model, columns=categorical_cols, drop_first=True)

# Separate features and target
X = df_encoded.drop('is_canceled', axis=1)
y = df_encoded['is_canceled']

# Standardize numeric features
numeric_features = ['lead_time', 'previous_cancellations', 
                    'previous_bookings_not_canceled', 'total_of_special_requests']

scaler = StandardScaler()
X[numeric_features] = scaler.fit_transform(X[numeric_features])

print("=== Model Preparation ===")
print(f"Features: {X.shape[1]}")
print(f"Samples: {X.shape[0]}")
print(f"Target distribution: {y.value_counts(normalize=True).round(3).to_dict()}")

=== Model Preparation ===
Features: 31
Samples: 87010
Target distribution: {0: 0.725, 1: 0.275}


In [323]:
# B3.2: Fit logistic regression

logreg = LogisticRegression(max_iter=1000, random_state=42)
logreg.fit(X, y)

# Calculate odds ratios
coefficients = pd.DataFrame({
    'feature': X.columns,
    'coefficient': logreg.coef_[0],
    'odds_ratio': np.exp(logreg.coef_[0])
})

coefficients = coefficients.sort_values('odds_ratio', ascending=False)

print("=== Logistic Regression Results ===")
print(f"Model Score: {logreg.score(X, y):.4f}")
print(f"\nTop 10 factors INCREASING cancellation (Odds Ratio > 1):")
print(coefficients.head(10).to_string())
print(f"\nTop 10 factors DECREASING cancellation (Odds Ratio < 1):")
print(coefficients.tail(10).to_string())

=== Logistic Regression Results ===
Model Score: 0.7711

Top 10 factors INCREASING cancellation (Odds Ratio > 1):
                       feature  coefficient  odds_ratio
5      deposit_type_Non Refund     3.883583   48.598024
2       previous_cancellations     0.690768    1.995246
10    market_segment_Online TA     0.612756    1.845511
18     customer_type_Transient     0.604442    1.830230
15  distribution_channel_TA/TO     0.481169    1.617965
0                    lead_time     0.459786    1.583735
6      deposit_type_Refundable     0.249303    1.283131
11        market_segment_Other     0.205785    1.228490
30       arrival_date_month_12     0.184759    1.202928
26        arrival_date_month_8     0.175306    1.191611

Top 10 factors DECREASING cancellation (Odds Ratio < 1):
                           feature  coefficient  odds_ratio
7            market_segment_Direct    -0.068012    0.934250
13     distribution_channel_Direct    -0.086628    0.917018
17             customer_type_Gro

In [324]:
# B3.3: Plot 4 - Odds Ratios Visualization

# Select top factors to plot
top_increase = coefficients[coefficients['odds_ratio'] > 1].head(10)
top_decrease = coefficients[coefficients['odds_ratio'] < 1].tail(10)
plot_data = pd.concat([top_increase, top_decrease]).sort_values('odds_ratio')

fig = go.Figure()

# Create color based on increase/decrease
colors = ['red' if or_val > 1 else 'green' for or_val in plot_data['odds_ratio']]

fig.add_trace(go.Bar(
    y=plot_data['feature'],
    x=plot_data['odds_ratio'],
    orientation='h',
    marker=dict(color=colors),
    text=[f"OR: {or_val:.2f}" for or_val in plot_data['odds_ratio']],
    textposition='outside',
    hovertemplate='<b>%{y}</b><br>' +
                  'Odds Ratio: %{x:.3f}<br>' +
                  '<extra></extra>'
))

# Add reference line at OR = 1
fig.add_vline(x=1, line_dash="dash", line_color="black", 
              annotation_text="OR = 1 (No effect)")

fig.update_layout(
    title="Plot 4: Top Drivers by Odds Ratio (Logistic Regression)",
    xaxis_title="Odds Ratio",
    yaxis_title="Driver",
    height=600,
    showlegend=False
)

fig.show()

print("\nInterpretation:")
print("- Odds Ratio > 1: Factor INCREASES cancellation likelihood")
print("- Odds Ratio < 1: Factor DECREASES cancellation likelihood")
print("- OR = 2 means: factor doubles the odds of cancellation")


Interpretation:
- Odds Ratio > 1: Factor INCREASES cancellation likelihood
- Odds Ratio < 1: Factor DECREASES cancellation likelihood
- OR = 2 means: factor doubles the odds of cancellation


**Insights**:
1. Deposit type (Non-Refund) là tác nhân chi phối mạnh nhất đối với khả năng hủy đặt phòng khi kiểm soát các yếu tố khác.
2. Hành vi trong quá khứ (đặc biệt là số lần hủy trước đó) là chỉ báo quan trọng về rủi ro hủy trong tương lai.
3. Mức độ cam kết và tương tác (khách quay lại, yêu cầu đặc biệt, lịch sử booking không hủy) liên quan chặt chẽ đến xác suất hủy thấp hơn.

Kết quả hồi quy xác nhận sự cần thiết của cách tiếp cận đa biến, thay vì đánh giá từng yếu tố riêng lẻ.

#### **4. Subgroup Analysis - City Hotel vs Resort Hotel**

**Mục tiêu**: Kiểm tra xem drivers có ảnh hưởng khác nhau giữa 2 loại khách sạn không

In [325]:
# B4.1: Plot 5 - Deposit Type by Hotel

deposit_hotel = df_q5.groupby(['deposit_type', 'hotel'])['is_canceled'].agg(['count', 'mean']).reset_index()
deposit_hotel.columns = ['deposit_type', 'hotel', 'count', 'cancel_rate']
deposit_hotel['cancel_rate'] = deposit_hotel['cancel_rate'] * 100

fig = go.Figure()

for hotel in ['City Hotel', 'Resort Hotel']:
    hotel_data = deposit_hotel[deposit_hotel['hotel'] == hotel].sort_values('deposit_type')
    
    fig.add_trace(go.Bar(
        name=hotel,
        x=hotel_data['deposit_type'],
        y=hotel_data['cancel_rate'],
        text=[f"{rate:.1f}%<br>n={count:,}" 
              for rate, count in zip(hotel_data['cancel_rate'], hotel_data['count'])],
        textposition='outside'
    ))

fig.update_layout(
    title="Plot 5: Cancel Rate by Deposit Type - City vs Resort",
    xaxis_title="Deposit Type",
    yaxis_title="Cancel Rate (%)",
    barmode='group',
    height=500,
    legend=dict(title="Hotel Type")
)

fig.show()

print("=== Cancel Rate by Deposit Type and Hotel ===")
pivot = deposit_hotel.pivot(index='deposit_type', columns='hotel', values='cancel_rate')
print(pivot.round(1))

=== Cancel Rate by Deposit Type and Hotel ===
hotel         City Hotel  Resort Hotel
deposit_type                          
No Deposit          29.0          23.2
Non Refund          97.2          83.9
Refundable          66.7          17.4


Kết quả cho thấy City Hotel có tỷ lệ hủy cao hơn Resort Hotel ở tất cả các loại đặt cọc. 
- Sự khác biệt đặc biệt lớn ở nhóm Refundable, với tỷ lệ hủy tại City Hotel là 66.7% so với 17.4% tại Resort Hotel. 
- Trong nhóm Non-Refund, cả hai loại khách sạn đều ghi nhận tỷ lệ hủy rất cao, tuy nhiên City Hotel vẫn cao hơn (97.2% so với 83.9%).

In [326]:
# B4.2: Lead Time effect by Hotel

leadtime_hotel = df_q5.groupby(['lead_time_bin', 'hotel'])['is_canceled'].agg(['count', 'mean']).reset_index()
leadtime_hotel.columns = ['lead_time_bin', 'hotel', 'count', 'cancel_rate']
leadtime_hotel['cancel_rate'] = leadtime_hotel['cancel_rate'] * 100

fig = go.Figure()

for hotel in ['City Hotel', 'Resort Hotel']:
    hotel_data = leadtime_hotel[leadtime_hotel['hotel'] == hotel]
    
    fig.add_trace(go.Scatter(
        name=hotel,
        x=hotel_data['lead_time_bin'].astype(str),
        y=hotel_data['cancel_rate'],
        mode='lines+markers',
        marker=dict(size=10),
        line=dict(width=3),
        text=[f"{rate:.1f}%<br>n={count:,}" 
              for rate, count in zip(hotel_data['cancel_rate'], hotel_data['count'])],
        hovertemplate='<b>%{x}</b><br>' +
                      'Cancel Rate: %{y:.2f}%<br>' +
                      '<extra></extra>'
    ))

fig.update_layout(
    title="Lead Time Effect: City vs Resort",
    xaxis_title="Lead Time Range",
    yaxis_title="Cancel Rate (%)",
    height=500,
    legend=dict(title="Hotel Type")
)

fig.show()

print("=== Cancel Rate by Lead Time and Hotel ===")
pivot_lt = leadtime_hotel.pivot(index='lead_time_bin', columns='hotel', values='cancel_rate')
print(pivot_lt.round(1))

=== Cancel Rate by Lead Time and Hotel ===
hotel          City Hotel  Resort Hotel
lead_time_bin                          
0-7 days             10.5           6.0
8-30 days            27.9          20.9
31-90 days           33.2          29.8
91-180 days          36.7          32.0
180+ days            44.9          33.9


Tỷ lệ hủy tăng theo lead time ở cả hai loại khách sạn, tuy nhiên mức tăng tại City Hotel mạnh hơn. Ở tất cả các khoảng lead time, City Hotel đều có tỷ lệ hủy cao hơn Resort Hotel, với chênh lệch lớn nhất ở nhóm 180+ ngày (44.9% so với 33.9%). Điều này cho thấy City Hotel nhạy cảm hơn với rủi ro phát sinh từ booking dài hạn.

**Insights**:
1. Các yếu tố ngoài giá ảnh hưởng đến hủy đặt phòng khác nhau giữa City Hotel và Resort Hotel.
2. City Hotel thể hiện mức độ rủi ro cao hơn, đặc biệt đối với điều khoản linh hoạt và lead time dài.
3. Phân tích theo nhóm con giúp làm rõ các khác biệt mà phân tích gộp có thể che khuất.

### **C. Kết quả và Giải thích**

Kết quả phân tích cho thấy hành vi hủy đặt phòng chịu ảnh hưởng đồng thời bởi nhiều yếu tố ngoài giá, trong đó các tác nhân liên quan đến thời điểm đặt phòng, mức độ cam kết, lịch sử hành vi và kênh phân phối đóng vai trò nổi bật.

1. Thời gian đặt phòng trước (`lead time`) có mối liên hệ dương rõ rệt với tỷ lệ hủy. Tỷ lệ hủy tăng từ khoảng 20% ở các booking ngắn hạn (0–7 ngày) lên gần 40% ở các booking có lead time trên 180 ngày. Hiệu ứng này được quan sát mạnh hơn tại City Hotel so với Resort Hotel, cho thấy mức độ không chắc chắn gia tăng rõ rệt hơn trong bối cảnh lưu trú đô thị.

2. Loại đặt cọc (`deposit type`) là một trong những tác nhân có sức phân biệt mạnh nhất. Nhóm No Deposit chiếm phần lớn khối lượng booking và có tỷ lệ hủy trung bình khoảng 27%. Nhóm Refundable có tỷ lệ hủy tương đương. Ngược lại, nhóm Non-Refund ghi nhận tỷ lệ hủy rất cao (xấp xỉ 95%), cho thấy một hành vi bất thường cần được xem xét kỹ về mặt định nghĩa dữ liệu và quy trình ghi nhận.

3. Lịch sử hành vi khách hàng có tác động đáng kể đến khả năng hủy. Các booking đến từ khách có lịch sử hủy trong quá khứ có xác suất hủy cao hơn rõ rệt, trong khi khách quay lại có tỷ lệ hủy thấp hơn đáng kể so với khách mới.

4. Mức độ tương tác của khách hàng thể hiện vai trò quan trọng. Số lượng yêu cầu đặc biệt có mối tương quan âm với tỷ lệ hủy, cho thấy mức độ tương tác cao hơn thường đi kèm mức độ cam kết lớn hơn.

5. Kênh phân phối và phân khúc thị trường cũng ảnh hưởng đáng kể đến hành vi hủy. Phân khúc Online TA có tỷ lệ hủy cao (khoảng 35%), trong khi các kênh Direct và Corporate ghi nhận tỷ lệ hủy thấp hơn đáng kể (khoảng 12–15%).

So sánh theo loại hình khách sạn cho thấy City Hotel có mức độ nhạy cảm cao hơn đối với cả lead time và điều khoản linh hoạt, trong khi Resort Hotel có tỷ lệ hủy nền thấp hơn và biến động ít hơn theo các tác nhân này.

In [327]:
print("="*80)
print("Q5 SUMMARY: NON-PRICE DRIVERS AFFECTING CANCELLATION")
print("="*80)

print("\n1. TOP DRIVERS (from Logistic Regression):")
print("\nIncrease Cancellation Risk:")
top_risk = coefficients[coefficients['odds_ratio'] > 1].head(5)
for idx, row in top_risk.iterrows():
    print(f"   - {row['feature']}: OR = {row['odds_ratio']:.3f}")

print("\nDecrease Cancellation Risk:")
top_protect = coefficients[coefficients['odds_ratio'] < 1].tail(5)
for idx, row in top_protect.iterrows():
    print(f"   - {row['feature']}: OR = {row['odds_ratio']:.3f}")

print("\n2. KEY FINDINGS BY DRIVER CATEGORY:")
print(f"\nLead Time:")
print(f"   0-7 days: {df_q5[df_q5['lead_time_bin']=='0-7 days']['is_canceled'].mean()*100:.1f}% cancel")
print(f"   180+ days: {df_q5[df_q5['lead_time_bin']=='180+ days']['is_canceled'].mean()*100:.1f}% cancel")

print(f"\nDeposit Type:")
for dtype in df_q5['deposit_type'].unique():
    rate = df_q5[df_q5['deposit_type']==dtype]['is_canceled'].mean()*100
    count = len(df_q5[df_q5['deposit_type']==dtype])
    print(f"   {dtype}: {rate:.1f}% cancel (n={count:,})")

print(f"\nRepeat Guest:")
print(f"   New: {df_q5[df_q5['is_repeated_guest']==0]['is_canceled'].mean()*100:.1f}% cancel")
print(f"   Repeat: {df_q5[df_q5['is_repeated_guest']==1]['is_canceled'].mean()*100:.1f}% cancel")

print("\n3. CITY VS RESORT DIFFERENCES:")
for hotel in ['City Hotel', 'Resort Hotel']:
    rate = df_q5[df_q5['hotel']==hotel]['is_canceled'].mean()*100
    print(f"   {hotel}: {rate:.1f}% overall cancel rate")

print("\n" + "="*80)

Q5 SUMMARY: NON-PRICE DRIVERS AFFECTING CANCELLATION

1. TOP DRIVERS (from Logistic Regression):

Increase Cancellation Risk:
   - deposit_type_Non Refund: OR = 48.598
   - previous_cancellations: OR = 1.995
   - market_segment_Online TA: OR = 1.846
   - customer_type_Transient: OR = 1.830
   - distribution_channel_TA/TO: OR = 1.618

Decrease Cancellation Risk:
   - market_segment_Groups: OR = 0.656
   - total_of_special_requests: OR = 0.572
   - previous_bookings_not_canceled: OR = 0.572
   - is_repeated_guest: OR = 0.408
   - market_segment_Offline TA/TO: OR = 0.358

2. KEY FINDINGS BY DRIVER CATEGORY:

Lead Time:
   0-7 days: 8.4% cancel
   180+ days: 39.7% cancel

Deposit Type:
   No Deposit: 26.7% cancel (n=85,865)
   Refundable: 24.3% cancel (n=107)
   Non Refund: 94.7% cancel (n=1,038)

Repeat Guest:
   New: 28.3% cancel
   Repeat: 7.7% cancel

3. CITY VS RESORT DIFFERENCES:
   City Hotel: 30.1% overall cancel rate
   Resort Hotel: 23.5% overall cancel rate



### **D. Ý nghĩa Kinh Doanh::**
Kết quả phân tích cho phép xác định một số nhóm hành vi và tổ hợp rủi ro quan trọng.

1. Tồn tại các tổ hợp rủi ro cao, đặc biệt là các booking có lead time dài kết hợp với No Deposit, với tỷ lệ hủy vượt quá 40%. Ngoài ra, nhóm Non-Refund thể hiện tỷ lệ hủy bất thường, cho thấy khả năng tồn tại vấn đề về định nghĩa hoặc cách ghi nhận trạng thái hủy.
2. Một số phân khúc ổn định thể hiện mức độ cam kết cao và tỷ lệ hủy thấp, bao gồm khách quay lại, khách Corporate và các booking Direct có mức độ tương tác cao thông qua yêu cầu đặc biệt.
3. Các kênh phân phối có mức độ đánh đổi rõ rệt giữa quy mô và rủi ro. Online TA đóng góp khối lượng lớn nhưng đi kèm tỷ lệ hủy cao, trong khi kênh Direct có mức độ ổn định tốt hơn.
4. $ác kết quả cho thấy sự cần thiết của chính sách phân biệt theo loại hình khách sạn, do City Hotel và Resort Hotel phản ứng khác nhau trước cùng một tác nhân ngoài giá.s

### **E. Kết luận:**

Dựa trên các kết quả định lượng, một số khuyến nghị hành động có thể được đề xuất.

- Trong ngắn hạn, việc áp dụng chính sách đặt cọc phân tầng theo lead time có thể giúp giảm rủi ro hủy đối với các booking dài hạn. Song song đó, các chương trình xác nhận lại đặt phòng trước ngày đến nên được ưu tiên cho các booking có lead time dài và không có đặt cọc.

- Về trung hạn, cần tăng cường chính sách giữ chân khách quay lại, thông qua các chương trình khách hàng thân thiết và điều khoản linh hoạt có chọn lọc. Đồng thời, việc khuyến khích tăng mức độ tương tác trước ngày đến (ví dụ: yêu cầu đặc biệt, giao tiếp trước khi nhận phòng) có thể góp phần giảm xác suất hủy.

- Về chiến lược dài hạn, cơ cấu kênh phân phối cần được tối ưu theo hướng giảm phụ thuộc vào các kênh có rủi ro cao, đồng thời thiết kế chính sách quản lý rủi ro khác biệt cho City Hotel và Resort Hotel, phản ánh sự khác nhau trong hành vi hủy đặt phòng giữa hai loại hình lưu trú.

---

## **Q6 — ADR-Cancellation Trade-off: Phân tích Mối quan hệ Giá và Hủy phòng**

*Giá phòng khác nhau ảnh hưởng như thế nào đến khả năng khách hủy đặt phòng ở các phân khúc khách hàng khác nhau?*


### **A. Chuẩn bị dữ liệu:**

Tập trung vào mối quan hệ ADR-Cancellation, do đó cần xử lý ADR cẩn thận.
### **1. Chọn Columns và Remove Leakage**

**Columns cần thiết**:
- Target: `is_canceled`
- Key variable: `adr` (và `adr_clipped` từ Q4)
- Segmentation: `hotel`, `market_segment`, `distribution_channel`
- Control variables: `lead_time`, `deposit_type`, `customer_type`, `total_of_special_requests`, `arrival_date_month`

**Leakage đã loại ở Q4**: `reservation_status`, `reservation_status_date`

In [328]:
df_q6 = df_q4.copy()

print("=== Data for Q3 Analysis ===")
print(f"Shape: {df_q6.shape}")
print(f"\nKey variables:")
print(f"  - ADR: {df_q6['adr_clipped'].describe().to_dict()}")
print(f"  - Cancel rate: {df_q6['is_canceled'].mean()*100:.2f}%")
print(f"  - Hotels: {df_q6['hotel'].value_counts().to_dict()}")

=== Data for Q3 Analysis ===
Shape: (87010, 32)

Key variables:
  - ADR: {'count': 87010.0, 'mean': 106.20523008849558, 'std': 50.737345084376685, 'min': 0.0, '25%': 72.25, '50%': 98.33, '75%': 134.1, 'max': 262.0}
  - Cancel rate: 27.50%
  - Hotels: {'City Hotel': 53055, 'Resort Hotel': 33955}


#### **2. Visualize ADR Distribution (Post-cleaning)**

**Mục tiêu**: Verify rằng ADR đã được xử lý hợp lý và ready cho analysis

In [329]:
fig = go.Figure()

fig.add_trace(go.Histogram(
    x=df_q6['adr_clipped'],
    nbinsx=50,
    name='ADR Distribution',
    marker_color='steelblue',
    opacity=0.75
))

mean_adr_q3 = df_q6['adr_clipped'].mean()
median_adr_q3 = df_q6['adr_clipped'].median()

fig.add_vline(x=mean_adr_q3, line_dash="dash", line_color="red",
              annotation_text=f"Mean: {mean_adr_q3:.2f}",
              annotation_position="top right")

fig.add_vline(x=median_adr_q3, line_dash="dash", line_color="green",
              annotation_text=f"Median: {median_adr_q3:.2f}",
              annotation_position="bottom right")

fig.update_layout(
    title="Distribution of ADR after Cleaning",
    xaxis_title="ADR (EUR)",
    yaxis_title="Number of Bookings",
    height=500,
    showlegend=True
)

fig.show()

print(f"ADR Statistics (cleaned):")
print(f"  Mean: {mean_adr_q3:.2f} EUR")
print(f"  Median: {median_adr_q3:.2f} EUR")
print(f"  Std: {df_q6['adr_clipped'].std():.2f} EUR")
print(f"  Range: [{df_q6['adr_clipped'].min():.2f}, {df_q6['adr_clipped'].max():.2f}]")

ADR Statistics (cleaned):
  Mean: 106.21 EUR
  Median: 98.33 EUR
  Std: 50.74 EUR
  Range: [0.00, 262.00]


#### **3. Tạo ADR Bins**

**Phương pháp**: Quantile-based bins (qcut) để mỗi bin có số lượng bookings tương đương

**Mục tiêu**: 
- So sánh cancel rate ổn định hơn (tránh bins có quá ít data)
- Dễ detect trends across price spectrum
- Business-friendly interpretation

In [330]:
# Create 10 quantile bins
df_q6['adr_bin'] = pd.qcut(df_q6['adr_clipped'], q=10, duplicates='drop')

# Also create a numeric version for easier plotting
df_q6['adr_bin_mid'] = df_q6.groupby('adr_bin')['adr_clipped'].transform('median')

print("=== ADR Bins Created ===\n")

# Show bin distribution
bin_stats = df_q6.groupby('adr_bin').agg({
    'adr_clipped': ['count', 'min', 'max', 'median'],
    'is_canceled': 'mean'
}).round(2)
bin_stats.columns = ['count', 'adr_min', 'adr_max', 'adr_median', 'cancel_rate']
bin_stats['cancel_rate'] = (bin_stats['cancel_rate'] * 100).round(2)

print(bin_stats)

print(f"\nBins range from {df_q6['adr_clipped'].min():.2f} to {df_q6['adr_clipped'].max():.2f} EUR")

=== ADR Bins Created ===

                 count  adr_min  adr_max  adr_median  cancel_rate
adr_bin                                                          
(-0.001, 48.0]    9030     0.00    48.00       37.80         15.0
(48.0, 65.0]      8395    48.03    65.00       59.04         20.0
(65.0, 77.4]      8694    65.02    77.40       72.25         22.0
(77.4, 88.4]      8751    77.43    88.40       82.40         26.0
(88.4, 98.33]     8641    88.41    98.33       93.08         27.0
(98.33, 110.67]   8696    98.35   110.67      105.00         30.0
(110.67, 126.0]   9260   110.68   126.00      118.80         32.0
(126.0, 144.0]    8315   126.01   144.00      135.00         34.0
(144.0, 174.0]    8537   144.10   174.00      157.86         32.0
(174.0, 262.0]    8691   174.01   262.00      204.50         37.0

Bins range from 0.00 to 262.00 EUR


### **B. Phân tích Mối quan hệ ADR-Cancellation**

Phân tích ở 3 tầng:
1. Descriptive - Cancel rate theo ADR bins
2. Controlled analysis - Logistic regression với controls
3. Segment-specific - Phân tích theo market segments

#### **1. Descriptive Analysis - Cancel Rate vs ADR**

**Mục tiêu**: Quan sát trực tiếp mối quan hệ giữa ADR và cancel rate, phân tích theo hotel type

In [331]:
# B1.1: Overall cancel rate by ADR bin

overall_analysis = df_q6.groupby('adr_bin_mid').agg({
    'is_canceled': ['count', 'mean'],
    'adr_clipped': 'median'
}).round(4)
overall_analysis.columns = ['count', 'cancel_rate', 'adr_median']
overall_analysis['cancel_rate'] = overall_analysis['cancel_rate'] * 100
overall_analysis = overall_analysis.sort_values('adr_median')

print("=== Cancel Rate by ADR Level ===")
print(overall_analysis)

# Calculate correlation
correlation = df_q6[['adr_clipped', 'is_canceled']].corr().iloc[0, 1]
print(f"\nPearson correlation (ADR vs Cancel): {correlation:.4f}")

=== Cancel Rate by ADR Level ===
             count  cancel_rate  adr_median
adr_bin_mid                                
37.80         9030        15.12       37.80
59.04         8395        19.82       59.04
72.25         8694        22.25       72.25
82.40         8751        25.75       82.40
93.08         8641        27.23       93.08
105.00        8696        30.15      105.00
118.80        9260        32.13      118.80
135.00        8315        33.87      135.00
157.86        8537        32.39      157.86
204.50        8691        36.60      204.50

Pearson correlation (ADR vs Cancel): 0.1353


Kết quả cho thấy tỷ lệ hủy đặt phòng tăng dần theo mức ADR. Ở các nhóm ADR thấp (khoảng 38–60 EUR), tỷ lệ hủy dao động từ 15–20%, trong khi ở các nhóm ADR cao (trên 150 EUR), tỷ lệ hủy đạt trên 35%. Hệ số tương quan Pearson giữa ADR và trạng thái hủy là dương nhưng ở mức vừa phải (r ≈ 0.14), cho thấy mối quan hệ tồn tại nhưng không mang tính tuyến tính mạnh.

In [332]:
# Plot 2 - Line chart: Cancel rate by ADR (City vs Resort)

# Prepare data by hotel
city_adr_analysis = df_q6[df_q6['hotel'] == 'City Hotel'].groupby('adr_bin_mid').agg({
    'is_canceled': 'mean',
    'adr_clipped': 'median'
}).reset_index()
city_adr_analysis.columns = ['adr_bin_mid', 'cancel_rate', 'adr_median']
city_adr_analysis['cancel_rate'] *= 100
city_adr_analysis = city_adr_analysis.sort_values('adr_median')

resort_adr_analysis = df_q6[df_q6['hotel'] == 'Resort Hotel'].groupby('adr_bin_mid').agg({
    'is_canceled': 'mean',
    'adr_clipped': 'median'
}).reset_index()
resort_adr_analysis.columns = ['adr_bin_mid', 'cancel_rate', 'adr_median']
resort_adr_analysis['cancel_rate'] *= 100
resort_adr_analysis = resort_adr_analysis.sort_values('adr_median')

fig = go.Figure()

# Overall trend
fig.add_trace(go.Scatter(
    x=overall_analysis['adr_median'],
    y=overall_analysis['cancel_rate'],
    mode='lines+markers',
    name='Overall',
    line=dict(color='black', width=3, dash='dash'),
    marker=dict(size=8)
))

# City Hotel
fig.add_trace(go.Scatter(
    x=city_adr_analysis['adr_median'],
    y=city_adr_analysis['cancel_rate'],
    mode='lines+markers',
    name='City Hotel',
    line=dict(color='blue', width=3),
    marker=dict(size=10)
))

# Resort Hotel
fig.add_trace(go.Scatter(
    x=resort_adr_analysis['adr_median'],
    y=resort_adr_analysis['cancel_rate'],
    mode='lines+markers',
    name='Resort Hotel',
    line=dict(color='orange', width=3),
    marker=dict(size=10)
))

fig.update_layout(
    title="Cancel Rate vs ADR - City vs Resort Hotel",
    xaxis_title="ADR (EUR)",
    yaxis_title="Cancel Rate (%)",
    height=600,
    legend=dict(x=0.02, y=0.98),
    hovermode='x unified'
)

fig.show()


Khi phân tách theo loại hình khách sạn, cả City Hotel và Resort Hotel đều thể hiện xu hướng tỷ lệ hủy tăng theo ADR. Tuy nhiên, tại hầu hết các mức giá trung bình, City Hotel có tỷ lệ hủy cao hơn Resort Hotel. Độ dốc của đường xu hướng tại City Hotel lớn hơn, cho thấy mức độ nhạy cảm với giá cao hơn so với Resort Hotel.

In [333]:
# B1.3: Plot 3 - Grouped bar chart by ADR bins

# Create bins with labels for better visualization
df_q6['adr_bin_label'] = pd.qcut(df_q6['adr_clipped'], q=5, duplicates='drop',
                                  labels=['Very Low', 'Low', 'Medium', 'High', 'Very High'])

grouped_data = df_q6.groupby(['adr_bin_label', 'hotel']).agg({
    'is_canceled': ['mean', 'count']
}).reset_index()
grouped_data.columns = ['adr_bin_label', 'hotel', 'cancel_rate', 'count']
grouped_data['cancel_rate'] *= 100

fig = go.Figure()

for hotel in ['City Hotel', 'Resort Hotel']:
    hotel_data = grouped_data[grouped_data['hotel'] == hotel]
    
    fig.add_trace(go.Bar(
        name=hotel,
        x=hotel_data['adr_bin_label'],
        y=hotel_data['cancel_rate'],
        text=[f"{rate:.1f}%<br>n={count:,}" 
              for rate, count in zip(hotel_data['cancel_rate'], hotel_data['count'])],
        textposition='outside'
    ))

fig.update_layout(
    title="Cancel Rate by ADR Level - Grouped by Hotel Type",
    xaxis_title="ADR Level",
    yaxis_title="Cancel Rate (%)",
    barmode='group',
    height=500,
    legend=dict(title="Hotel Type")
)

fig.show()

print("\n=== Cancel Rate by ADR Level and Hotel ===")
pivot_table = grouped_data.pivot(index='adr_bin_label', columns='hotel', values='cancel_rate')
print(pivot_table.round(2))


=== Cancel Rate by ADR Level and Hotel ===
hotel          City Hotel  Resort Hotel
adr_bin_label                          
Very Low            19.86         16.56
Low                 25.41         21.29
Medium              30.08         23.22
High                34.26         28.41
Very High           34.24         34.87


Phân tích theo nhóm ADR cho thấy tỷ lệ hủy tăng dần từ nhóm “Very Low” đến “High” ở cả hai loại hình khách sạn. Resort Hotel duy trì tỷ lệ hủy thấp hơn City Hotel ở các nhóm giá thấp và trung bình. Tuy nhiên, ở nhóm “Very High”, sự khác biệt giữa hai loại hình thu hẹp đáng kể, cho thấy ở mức giá rất cao, hành vi hủy có xu hướng hội tụ.

**Insights:**

- Tồn tại mối quan hệ dương giữa ADR và tỷ lệ hủy, nhưng mức độ tương quan tổng thể ở mức vừa phải.
- City Hotel thể hiện mức độ nhạy cảm với giá cao hơn Resort Hotel trên phần lớn phổ ADR.
- Resort Hotel có tỷ lệ hủy nền thấp hơn, đặc biệt ở các mức giá thấp và trung bình.
- Ở các mức ADR rất cao, sự khác biệt về hành vi hủy giữa hai loại hình khách sạn giảm đáng kể.

#### **2. Controlled Analysis - Logistic Regression**

**Mục tiêu**: Kiểm tra xem ADR effect có còn significant khi control cho:
- Lead time (Q4 shows strong effect)
- Deposit type (Q4 shows strong effect)
- Customer type, market segment
- Seasonality

**Phương pháp**: Logistic regression với interaction ADR × Hotel

In [334]:
# Select features
feature_cols_q3 = [
    'adr_clipped',  # Key variable
    'hotel',        # Segment
    'lead_time',    # Control
    'deposit_type',
    'customer_type',
    'market_segment',
    'distribution_channel',
    'total_of_special_requests',
    'arrival_date_month'
]

df_q6_model = df_q6[feature_cols_q3 + ['is_canceled']].copy()

# Encode categoricals
categorical_cols_q3 = ['hotel', 'deposit_type', 'customer_type', 'market_segment',
                       'distribution_channel', 'arrival_date_month']

df_q6_encoded = pd.get_dummies(df_q6_model, columns=categorical_cols_q3, drop_first=True)

# Separate features and target
X_q3 = df_q6_encoded.drop('is_canceled', axis=1)
y_q3 = df_q6_encoded['is_canceled']

# Standardize numeric features
numeric_cols_q3 = ['adr_clipped', 'lead_time', 'total_of_special_requests']
scaler_q3 = StandardScaler()
X_q3[numeric_cols_q3] = scaler_q3.fit_transform(X_q3[numeric_cols_q3])

print("=== Model Setup for Q3 ===")
print(f"Features: {X_q3.shape[1]}")
print(f"Samples: {X_q3.shape[0]}")
print(f"Target balance: {y_q3.value_counts(normalize=True).to_dict()}")

=== Model Setup for Q3 ===
Features: 30
Samples: 87010
Target balance: {0: 0.7249971267670383, 1: 0.27500287323296174}


Mô hình hồi quy logistic được xây dựng với biến phụ thuộc là trạng thái hủy đặt phòng và biến giải thích chính là ADR (đã chuẩn hóa). Các biến kiểm soát bao gồm lead time, loại đặt cọc, loại khách hàng, kênh phân phối, phân khúc thị trường, mức độ tương tác và yếu tố mùa vụ. Tập dữ liệu sau mã hóa gồm 30 biến và khoảng 87 nghìn quan sát, với phân bố nhãn hủy tương đối mất cân bằng nhưng phản ánh đúng thực tế kinh doanh.

In [335]:
# 2: Fit logistic regression

logreg_q3 = LogisticRegression(max_iter=1000, random_state=42)
logreg_q3.fit(X_q3, y_q3)

# Get coefficient for ADR
adr_coef_idx = X_q3.columns.get_loc('adr_clipped')
adr_coefficient = logreg_q3.coef_[0][adr_coef_idx]
adr_odds_ratio = np.exp(adr_coefficient)

print("=== Logistic Regression Results (Controlled) ===")
print(f"Model score: {logreg_q3.score(X_q3, y_q3):.4f}")
print(f"\nADR Effect (controlling for other variables):")
print(f"  Coefficient: {adr_coefficient:.4f}")
print(f"  Odds Ratio: {adr_odds_ratio:.4f}")
print(f"  Interpretation: 1 std increase in ADR → {(adr_odds_ratio-1)*100:.2f}% change in odds of cancellation")

# Top 10 coefficients
coef_df_q6 = pd.DataFrame({
    'feature': X_q3.columns,
    'coefficient': logreg_q3.coef_[0],
    'odds_ratio': np.exp(logreg_q3.coef_[0])
}).sort_values('odds_ratio', ascending=False)

print("\nTop 10 factors increasing cancellation:")
print(coef_df_q6.head(10)[['feature', 'odds_ratio']].to_string())

=== Logistic Regression Results (Controlled) ===
Model score: 0.7715

ADR Effect (controlling for other variables):
  Coefficient: 0.2779
  Odds Ratio: 1.3203
  Interpretation: 1 std increase in ADR → 32.03% change in odds of cancellation

Top 10 factors increasing cancellation:
                           feature  odds_ratio
4          deposit_type_Non Refund   44.962462
17      distribution_channel_TA/TO    1.863396
12        market_segment_Online TA    1.762175
13            market_segment_Other    1.672437
1                        lead_time    1.668644
7          customer_type_Transient    1.505755
0                      adr_clipped    1.320350
5          deposit_type_Refundable    1.287174
18  distribution_channel_Undefined    1.191403
29           arrival_date_month_12    1.164806


Kết quả hồi quy cho thấy ADR vẫn có tác động dương và có ý nghĩa đến khả năng hủy đặt phòng sau khi kiểm soát các yếu tố khác. Một độ lệch chuẩn tăng trong ADR làm tăng khoảng 32% odds hủy đặt phòng. So với các biến khác, tác động của ADR nhỏ hơn so với deposit type và lịch sử hành vi, nhưng vẫn giữ vai trò độc lập trong mô hình.

In [336]:
#Predicted probability by ADR (marginal effects)

# Create prediction data for different ADR levels
adr_range = np.linspace(df_q6['adr_clipped'].min(), df_q6['adr_clipped'].max(), 50)

# Function to create prediction dataset
def create_pred_data(adr_values, hotel_type, base_data):
    """Create prediction dataset with ADR varying, others at median/mode"""
    pred_rows = []
    
    for adr_val in adr_values:
        row = {
            'adr_clipped': adr_val,
            'lead_time': base_data['lead_time'].median(),
            'total_of_special_requests': base_data['total_of_special_requests'].median(),
        }
        
        # Set hotel
        row['hotel'] = hotel_type
        
        # Set most common categories
        row['deposit_type'] = base_data['deposit_type'].mode()[0]
        row['customer_type'] = base_data['customer_type'].mode()[0]
        row['market_segment'] = base_data['market_segment'].mode()[0]
        row['distribution_channel'] = base_data['distribution_channel'].mode()[0]
        row['arrival_date_month'] = base_data['arrival_date_month'].mode()[0]
        
        pred_rows.append(row)
    
    return pd.DataFrame(pred_rows)

# Create prediction data for both hotels
city_pred_data = create_pred_data(adr_range, 'City Hotel', df_q6)
resort_pred_data = create_pred_data(adr_range, 'Resort Hotel', df_q6)

# Encode and predict
city_pred_encoded = pd.get_dummies(city_pred_data, columns=categorical_cols_q3, drop_first=True)
resort_pred_encoded = pd.get_dummies(resort_pred_data, columns=categorical_cols_q3, drop_first=True)

# Ensure same columns
for col in X_q3.columns:
    if col not in city_pred_encoded.columns:
        city_pred_encoded[col] = 0
    if col not in resort_pred_encoded.columns:
        resort_pred_encoded[col] = 0

city_pred_encoded = city_pred_encoded[X_q3.columns]
resort_pred_encoded = resort_pred_encoded[X_q3.columns]

# Standardize
city_pred_encoded[numeric_cols_q3] = scaler_q3.transform(city_pred_encoded[numeric_cols_q3])
resort_pred_encoded[numeric_cols_q3] = scaler_q3.transform(resort_pred_encoded[numeric_cols_q3])

# Predict probabilities
city_probs = logreg_q3.predict_proba(city_pred_encoded)[:, 1] * 100
resort_probs = logreg_q3.predict_proba(resort_pred_encoded)[:, 1] * 100

# Plot
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=adr_range,
    y=city_probs,
    mode='lines',
    name='City Hotel',
    line=dict(color='blue', width=3)
))

fig.add_trace(go.Scatter(
    x=adr_range,
    y=resort_probs,
    mode='lines',
    name='Resort Hotel',
    line=dict(color='orange', width=3)
))

fig.update_layout(
    title="Predicted Cancellation Probability vs ADR (Controlled)",
    xaxis_title="ADR (EUR)",
    yaxis_title="Predicted Cancel Probability (%)",
    height=600,
    legend=dict(x=0.02, y=0.98),
    annotations=[dict(
        text="Holding other variables at typical values",
        xref="paper", yref="paper",
        x=0.5, y=-0.15,
        showarrow=False,
        font=dict(size=10, color="gray")
    )]
)

fig.show()

print("\n=== Marginal Effects Summary ===")
print(f"At ADR = {adr_range[0]:.2f} EUR:")
print(f"  City: {city_probs[0]:.2f}% | Resort: {resort_probs[0]:.2f}%")
print(f"At ADR = {adr_range[-1]:.2f} EUR:")
print(f"  City: {city_probs[-1]:.2f}% | Resort: {resort_probs[-1]:.2f}%")
print(f"\nSlope (sensitivity to ADR):")
print(f"  City: {(city_probs[-1] - city_probs[0])/(adr_range[-1] - adr_range[0]):.4f} pp per EUR")
print(f"  Resort: {(resort_probs[-1] - resort_probs[0])/(adr_range[-1] - adr_range[0]):.4f} pp per EUR")


=== Marginal Effects Summary ===
At ADR = 0.00 EUR:
  City: 9.57% | Resort: 9.57%
At ADR = 262.00 EUR:
  City: 30.78% | Resort: 30.78%

Slope (sensitivity to ADR):
  City: 0.0809 pp per EUR
  Resort: 0.0809 pp per EUR


Phân tích xác suất dự đoán cho thấy xác suất hủy tăng gần tuyến tính theo ADR khi giữ các biến khác ở mức điển hình. Ở mức ADR thấp, xác suất hủy khoảng 10%, trong khi ở mức ADR rất cao, xác suất này vượt 30%. Độ dốc của đường xu hướng tương tự giữa City Hotel và Resort Hotel, cho thấy tác động cận biên của ADR là nhất quán giữa hai loại hình trong mô hình có kiểm soát.

**Insights:**

1. Tác động dương của ADR lên khả năng hủy vẫn tồn tại sau khi kiểm soát các yếu tố gây nhiễu.
2. Mức độ ảnh hưởng của ADR là vừa phải, thấp hơn các yếu tố liên quan đến cam kết (deposit) và lịch sử hành vi.
3. Sự khác biệt giữa City Hotel và Resort Hotel về độ nhạy với ADR giảm đáng kể khi đưa các biến kiểm soát vào mô hình.
4. Kết quả cho thấy mối quan hệ ADR–cancellation không chỉ là hiện tượng mô tả mà có nền tảng định lượng vững hơn.

#### **3. Segment-Specific Analysis**

**Mục tiêu**: Xem xét price sensitivity across market segments

In [337]:
# B3: Plot 5 - Heatmap: Cancel rate by Market Segment × ADR

# Get top 6 market segments by volume
top_segments = df_q6['market_segment'].value_counts().head(6).index.tolist()

# Filter data
df_segment_analysis = df_q6[df_q6['market_segment'].isin(top_segments)].copy()

# Create heatmap data
heatmap_data = df_segment_analysis.pivot_table(
    values='is_canceled',
    index='market_segment',
    columns='adr_bin_label',
    aggfunc='mean'
) * 100

# Also get counts
count_data = df_segment_analysis.pivot_table(
    values='is_canceled',
    index='market_segment',
    columns='adr_bin_label',
    aggfunc='count'
)

fig = go.Figure(data=go.Heatmap(
    z=heatmap_data.values,
    x=heatmap_data.columns,
    y=heatmap_data.index,
    colorscale='RdYlGn_r',
    text=[[f"{val:.1f}%<br>n={count:,}" if not pd.isna(val) else "N/A"
           for val, count in zip(row_val, row_count)]
          for row_val, row_count in zip(heatmap_data.values, count_data.values)],
    texttemplate='%{text}',
    textfont={"size": 10},
    colorbar=dict(title="Cancel<br>Rate (%)")
))

fig.update_layout(
    title="Plot 5 (Q3): Cancel Rate Heatmap - Market Segment × ADR Level",
    xaxis_title="ADR Level",
    yaxis_title="Market Segment",
    height=500
)

fig.show()

print("=== Cancel Rate by Segment × ADR ===")
print(heatmap_data.round(1))

=== Cancel Rate by Segment × ADR ===
adr_bin_label   Very Low   Low  Medium  High  Very High
market_segment                                         
Corporate            9.2  10.9    20.1  18.4       23.2
Direct              10.8  12.8    14.2  16.4       17.6
Groups              29.5  20.3    30.1  34.6       20.5
Offline TA/TO       11.4  13.0    19.2  18.7       21.8
Online TA           23.7  34.0    34.1  37.9       40.0
Other               12.3  16.0    20.1  25.0        0.0


**Nhận xét:**

- Kết quả heatmap cho thấy mối quan hệ giữa ADR và tỷ lệ hủy không đồng nhất giữa các phân khúc thị trường. Phân khúc Online TA thể hiện mức độ nhạy cảm với giá rõ rệt, với tỷ lệ hủy tăng mạnh từ khoảng 24% ở ADR thấp lên xấp xỉ 40% ở ADR rất cao. Ngược lại, các phân khúc Direct và Offline TA/TO có tỷ lệ hủy thấp hơn và tăng chậm hơn theo ADR.

- Phân khúc Corporate duy trì tỷ lệ hủy thấp và tương đối ổn định ở các mức ADR thấp và trung bình, tuy nhiên tỷ lệ hủy tăng đáng kể ở nhóm ADR cao. Đối với Groups, tỷ lệ hủy ở mức cao ngay cả tại ADR thấp, nhưng không thể hiện xu hướng tăng rõ rệt theo ADR, cho thấy hành vi hủy ít phụ thuộc vào giá.

**Insights:**
1. Mức độ nhạy cảm với ADR khác biệt đáng kể giữa các phân khúc thị trường.
2. Online TA là phân khúc nhạy cảm với giá cao nhất, với tỷ lệ hủy tăng mạnh khi ADR tăng.
3. Các phân khúc Corporate và Direct tương đối ổn định hơn và ít phản ứng với thay đổi ADR ở phần lớn phổ giá.
4. Kết quả khẳng định mối quan hệ ADR–cancellation mang tính phân khúc hóa, không thể diễn giải bằng một xu hướng chung cho toàn bộ khách hàng.

### **D. Kết quả và giải thích:**

- Kết quả phân tích mô tả cho thấy tồn tại mối quan hệ dương giữa ADR và tỷ lệ hủy đặt phòng: khi ADR tăng, tỷ lệ hủy có xu hướng tăng theo. Trên toàn bộ mẫu, nhóm ADR thấp ghi nhận tỷ lệ hủy khoảng 15–20%, trong khi ở mức ADR cao tỷ lệ hủy tăng lên khoảng 30–37%, phản ánh mức chênh lệch đáng kể giữa các dải giá.

- Trong phân tích có kiểm soát (hồi quy logistic với các biến kiểm soát như lead time, deposit type, market segment, distribution channel, customer type, mức độ tương tác và mùa vụ), tác động của ADR vẫn duy trì theo hướng dương. Cụ thể, khi ADR tăng (theo đơn vị chuẩn hóa), odds hủy đặt phòng tăng khoảng 32%, cho thấy mối liên hệ này không chỉ là hiện tượng do các yếu tố gây nhiễu đơn giản.

- Phân tích theo loại hình khách sạn cho thấy City Hotel và Resort Hotel đều có xu hướng tỷ lệ hủy tăng theo ADR. Tuy nhiên, sự khác biệt giữa hai loại hình thể hiện rõ trong phân tích mô tả (City thường có tỷ lệ hủy cao hơn), trong khi trong mô hình có kiểm soát, độ dốc tác động cận biên theo ADR giữa hai loại hình gần tương đồng, gợi ý rằng một phần chênh lệch quan sát được có thể đến từ cấu trúc phân khúc và các yếu tố đồng biến khác.

- Phân tích theo phân khúc thị trường cho thấy mối quan hệ ADR–cancellation không đồng nhất. Phân khúc Online TA thể hiện mức độ nhạy cảm với giá mạnh, với tỷ lệ hủy tăng rõ rệt khi ADR chuyển từ thấp sang rất cao. Ngược lại, các phân khúc như Direct, Offline TA/TO và Corporate có mức tăng chậm hơn và ổn định hơn trên phần lớn phổ giá, cho thấy sự khác biệt đáng kể về phản ứng của khách hàng đối với thay đổi giá.

### **E. Ý nghĩa Kinh Doanh::**

**1. Tồn tại đánh đổi giữa giá phòng và rủi ro hủy đặt phòng.**
- Kết quả cho thấy khi ADR tăng, khả năng hủy đặt phòng cũng tăng theo, đặc biệt ở các mức ADR cao. 
- Do đó, việc tối ưu hóa hiệu quả kinh doanh cần xem xét đồng thời cả mức giá và xác suất hủy, thay vì tập trung đơn lẻ vào ADR.

**2. City Hotel thể hiện mức độ nhạy cảm với giá cao hơn trong thực tế vận hành:**
- So với Resort Hotel, City Hotel thường ghi nhận tỷ lệ hủy cao hơn ở cùng các dải ADR trong phân tích mô tả. 
- Điều này cho thấy các quyết định điều chỉnh giá tại City Hotel cần được đánh giá thận trọng hơn về tác động đến hành vi hủy.

**3. Resort Hotel có hành vi hủy ổn định hơn theo mức giá**. Resort Hotel duy trì tỷ lệ hủy nền thấp hơn và biến động chậm hơn theo ADR trên phần lớn phổ giá, cho thấy khả năng thích ứng thay đổi giá tốt hơn so với City Hotel.

**4. Mức độ nhạy cảm với ADR khác biệt rõ rệt giữa các phân khúc thị trường:**
- Các phân khúc như Online TA phản ứng mạnh với thay đổi ADR, trong khi các phân khúc Corporate và Direct thể hiện mức độ ổn định cao hơn.
- Điều này nhấn mạnh tính cần thiết của tiếp cận định giá theo phân khúc.

**5. Khả năng tồn tại mức ADR tối ưu.** Quan hệ giữa ADR và tỷ lệ hủy không hoàn toàn tuyến tính, gợi ý sự tồn tại của một khoảng giá cân bằng giữa tăng giá và rủi ro hủy, cần được phân tích sâu hơn trong các mô hình tối ưu hóa.

### **F. Kết luận:**

- Kết quả phân tích cho thấy tồn tại mối quan hệ đánh đổi rõ rệt giữa giá phòng trung bình (ADR) và khả năng hủy đặt phòng, trong đó ADR tăng đi kèm với rủi ro hủy cao hơn. Mối quan hệ này vẫn duy trì sau khi kiểm soát các yếu tố quan trọng, cho thấy tác động độc lập của giá phòng đến hành vi hủy.
- Phản ứng đối với ADR khác biệt giữa các loại hình khách sạn và các phân khúc thị trường, với City Hotel và nhóm Online TA thể hiện mức độ nhạy cảm cao hơn. Do đó, các quyết định định giá cần cân nhắc đồng thời giá trị và rủi ro hủy, thay vì tối đa hóa ADR đơn thuần. Các kết quả này cung cấp nền tảng cho các phân tích tối ưu hóa giá theo phân khúc trong các bước nghiên cứu tiếp theo.

---

## **Q7 - Business Decision + Machine Learning**

**Nếu thay đổi giá phòng (ADR), rủi ro hủy đặt phòng và doanh thu thực nhận kỳ vọng sẽ thay đổi như thế nào theo từng loại khách sạn, và mức ADR nào là tối ưu để tối đa hóa doanh thu thực nhận?**

**Q7 khác Q6 ở :** `Q6 dừng ở "ADR ↔ huỷ"`. `Q7` đi tiếp thành quyết định: **ADR nào nên chọn** dựa trên **Doanh thu thực nhận** (Expected RealizedRevenue).

### **Approach:**
- **ML**: Dự đoán $P(cancel)$ với 4 models → chọn model tốt nhất
- **Decision metric**: Tính $Expected Realized Revenue = ADR × nights × (1 - P(cancel))$
- **Optimization**: Tìm ADR tối ưu theo phân khúc (hotel, market segment)

### **A. Chuẩn bị dữ liệu cho ML**

#### **1. Chọn target, leakage, scope**
- Biến mục tiêu được xác định là is_canceled, đại diện cho quyết định hủy của khách hàng.
- Các biến gây rò rỉ thông tin (reservation_status, reservation_status_date) được loại bỏ do chỉ được biết sau thời điểm hủy.
- Phạm vi phân tích tập trung theo hotel type (City vs. Resort) và mở rộng theo market segment nhằm hỗ trợ quyết định định giá phân khúc.

In [338]:
print("=" * 50)
print("Target, Leakage & Scope Selection")
print("=" * 50)

# Target
target = 'is_canceled'
print(f"\nTarget variable: {target}")
print(f"Distribution: {df[target].value_counts(normalize=True).to_dict()}")

# Leakage columns - variables that are known AFTER cancellation decision
leakage_cols_q7 = [
    'reservation_status',       # Direct result of cancellation
    'reservation_status_date',  # Date of final status (known after decision)
]

print(f"\nLeakage columns to drop ({len(leakage_cols_q7)}):")
for col in leakage_cols_q7:
    print(f"  - {col}: Known after cancellation decision")

# Scope: analyze by hotel type (City vs Resort)
print(f"\nAnalysis scope:")
print(f"  - Primary segmentation: hotel (City Hotel vs Resort Hotel)")
print(f"  - Secondary: market_segment (for deeper insights)")

# Create Q4 dataset
df_q7 = df.drop(columns=leakage_cols_q7, errors='ignore').copy()

print(f"\nDataset for Q4:")
print(f"  Shape: {df_q7.shape}")
print(f"  Target balance: {df_q7[target].value_counts(normalize=True).round(3).to_dict()}")

Target, Leakage & Scope Selection

Target variable: is_canceled
Distribution: {0: 0.7249971267670383, 1: 0.27500287323296174}

Leakage columns to drop (2):
  - reservation_status: Known after cancellation decision
  - reservation_status_date: Known after cancellation decision

Analysis scope:
  - Primary segmentation: hotel (City Hotel vs Resort Hotel)
  - Secondary: market_segment (for deeper insights)

Dataset for Q4:
  Shape: (87010, 30)
  Target balance: {0: 0.725, 1: 0.275}


#### **2. Làm sạch ADR & tạo biến doanh thu (feature engineering)**
- Giá phòng (ADR) được làm sạch bằng phương pháp clipping theo phân vị p1–p99 để giảm ảnh hưởng của ngoại lệ cực đoan.
- Biến số đêm lưu trú (total_nights) được tạo nhằm phản ánh quy mô giao dịch thực tế.
- Doanh thu tiềm năng được xác định là revenue_if_show = adr_clean × total_nights, làm cơ sở cho tối ưu doanh thu kỳ vọng.

In [339]:
# A2: Clean ADR & create revenue variables
print("=" * 50)
print("A2. ADR Cleaning & Revenue Creation")
print("=" * 50)

# Use same ADR cleaning as Q4 (clip to p1-p99)
p01_q7 = df_q7['adr'].quantile(0.01)
p99_q7 = df_q7['adr'].quantile(0.99)

#feature engineering
#1. adr_clean
df_q7['adr_clean'] = df_q7['adr'].clip(lower=p01_q7, upper=p99_q7)

print(f"\nADR cleaning:")
print(f"  - Original range: [{df_q7['adr'].min():.2f}, {df_q7['adr'].max():.2f}]")
print(f"  - Clipped to p1-p99: [{p01_q7:.2f}, {p99_q7:.2f}]")
print(f"  - Mean ADR after cleaning: {df_q7['adr_clean'].mean():.2f} EUR")

#2. Create total_nights
df_q7['total_nights'] = df_q7['stays_in_weekend_nights'] + df_q7['stays_in_week_nights']

#3. Create revenue_if_show (potential revenue if customer shows up)
df_q7['revenue_if_show'] = df_q7['adr_clean'] * df_q7['total_nights']

print(f"\nRevenue variables created:")
print(f"  - total_nights: mean = {df_q7['total_nights'].mean():.2f} nights")
print(f"  - revenue_if_show: mean = {df_q7['revenue_if_show'].mean():.2f} EUR")

# Filter out zero-night bookings (cannot generate revenue)
df_q7 = df_q7[df_q7['total_nights'] > 0].copy()
print(f"\nFiltered dataset (total_nights > 0):")
print(f"  Shape: {df_q7.shape}")

# Plot #1: Histogram of cleaned ADR
fig = go.Figure()

fig.add_trace(go.Histogram(
    x=df_q7['adr_clean'],
    nbinsx=50,
    name='ADR Distribution',
    marker_color='steelblue',
    opacity=0.7
))

fig.update_layout(
    title='<b>Distribution of Cleaned ADR</b>',
    xaxis_title='ADR (EUR)',
    yaxis_title='Frequency',
    height=400,
    showlegend=False,
    template='plotly_white'
)

fig.show()

print(f"\nADR statistics (cleaned):")
print(df_q7['adr_clean'].describe().round(2))

A2. ADR Cleaning & Revenue Creation

ADR cleaning:
  - Original range: [0.00, 5400.00]
  - Clipped to p1-p99: [0.00, 262.00]
  - Mean ADR after cleaning: 106.21 EUR

Revenue variables created:
  - total_nights: mean = 3.63 nights
  - revenue_if_show: mean = 393.78 EUR

Filtered dataset (total_nights > 0):
  Shape: (86419, 33)



ADR statistics (cleaned):
count    86419.00
mean       106.93
std         50.14
min          0.00
25%         72.90
50%         99.00
75%        134.75
max        262.00
Name: adr_clean, dtype: float64


#### **3. Xử lý missing + encoding (pipeline)**
- Các biến số được xử lý thiếu bằng median imputation và chuẩn hóa bằng StandardScaler.
- Biến phân loại được gộp các nhóm hiếm vào nhãn “Other” nhằm giảm độ thưa và ổn định mô hình.
- Pipeline tiền xử lý thống nhất (ColumnTransformer) đảm bảo khả năng tái lập và tránh leakage trong huấn luyện mô hình.

In [340]:
print("=" * 50)
print("A3. Missing Handling & Encoding Pipeline")
print("=" * 50)

# Identify numeric and categorical columns
numeric_cols_q4 = df_q7.select_dtypes(include=['int64', 'float64']).columns.tolist()
categorical_cols_q4 = df_q7.select_dtypes(include=['object']).columns.tolist()

# Remove target and revenue variables from features
exclude_cols = [target, 'revenue_if_show', 'adr']  # Keep adr_clean, drop original adr
numeric_cols_q4 = [col for col in numeric_cols_q4 if col not in exclude_cols]

print(f"\nFeature types:")
print(f"  - Numeric features: {len(numeric_cols_q4)}")
print(f"  - Categorical features: {len(categorical_cols_q4)}")

# Top N categories for stability (reduce rare categories)
top_n_categories = {
    'market_segment': 8,
    'distribution_channel': 5,
    'customer_type': 4,
    'country': 20
}

# Consolidate rare categories
for col, top_n in top_n_categories.items():
    if col in df_q7.columns:
        top_cats = df_q7[col].value_counts().head(top_n).index
        df_q7[col] = df_q7[col].apply(lambda x: x if x in top_cats else 'Other')
        print(f"  - {col}: kept top {top_n} categories + 'Other'")

# Create preprocessing pipeline
numeric_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='median')),
    ('scaler', StandardScaler())
])

categorical_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='most_frequent')),
    ('onehot', OneHotEncoder(handle_unknown='ignore', sparse_output=False))
])

preprocessor = ColumnTransformer(
    transformers=[
        ('num', numeric_transformer, numeric_cols_q4),
        ('cat', categorical_transformer, categorical_cols_q4)
    ]
)

print(f"\nPreprocessing pipeline created:")
print(f"  - Numeric: median impute → StandardScaler")
print(f"  - Categorical: most_frequent impute → OneHotEncoder")
print(f"\nReady for train/test split.")

A3. Missing Handling & Encoding Pipeline

Feature types:
  - Numeric features: 21
  - Categorical features: 9
  - market_segment: kept top 8 categories + 'Other'
  - distribution_channel: kept top 5 categories + 'Other'


  - customer_type: kept top 4 categories + 'Other'
  - country: kept top 20 categories + 'Other'

Preprocessing pipeline created:
  - Numeric: median impute → StandardScaler
  - Categorical: most_frequent impute → OneHotEncoder

Ready for train/test split.


#### **4. Split train/test (stratified)**

In [341]:
from sklearn.model_selection import train_test_split

print("=" * 50)
print("Train/Test Split (Stratified 80/20)")
print("=" * 50)

# Prepare X and y
X_q4 = df_q7[numeric_cols_q4 + categorical_cols_q4].copy()
y_q4 = df_q7[target].copy()

# Keep hotel and revenue columns for later analysis
metadata_cols = ['hotel', 'adr_clean', 'total_nights', 'revenue_if_show', 'market_segment']
metadata_q4 = df_q7[metadata_cols].copy()

# Stratified split
X_train, X_test, y_train, y_test, meta_train, meta_test = train_test_split(
    X_q4, y_q4, metadata_q4,
    test_size=0.20,
    random_state=42,
    stratify=y_q4
)

print(f"\nSplit results:")
print(f"  Train set: {X_train.shape[0]:,} samples ({X_train.shape[0]/len(X_q4)*100:.1f}%)")
print(f"  Test set:  {X_test.shape[0]:,} samples ({X_test.shape[0]/len(X_q4)*100:.1f}%)")

print(f"\nTarget distribution (stratified):")
print(f"  Train - cancel rate: {y_train.mean():.3f}")
print(f"  Test  - cancel rate: {y_test.mean():.3f}")
print(f"  Difference: {abs(y_train.mean() - y_test.mean()):.4f} (very close)")

# Fit preprocessor on train, transform both
X_train_processed = preprocessor.fit_transform(X_train)
X_test_processed = preprocessor.transform(X_test)

print(f"\nAfter preprocessing:")
print(f"  X_train shape: {X_train_processed.shape}")
print(f"  X_test shape:  {X_test_processed.shape}")
print(f"\nPreprocessing complete - ready for model training.")

Train/Test Split (Stratified 80/20)



Split results:
  Train set: 69,135 samples (80.0%)
  Test set:  17,284 samples (20.0%)

Target distribution (stratified):
  Train - cancel rate: 0.277
  Test  - cancel rate: 0.277
  Difference: 0.0000 (very close)

After preprocessing:
  X_train shape: (69135, 78)
  X_test shape:  (17284, 78)

Preprocessing complete - ready for model training.


### **B. Phân tích - Huấn luyện ML và Tối ưu hóa**

#### **1. Thiết lập ML: Huấn luyện 4 mô hình**

In [342]:
# Train 4 models

print("=" * 70)
print("Train Multiple Models to Predict Cancellation")
print("=" * 70)

# Initialize dictionary to store models
models_dict = {}
predictions_dict = {}

# Model 1: Logistic Regression (baseline)
print("\n[1/4] Training Logistic Regression...")
start = time.time()
model_lr = LogisticRegression(
    max_iter=1000,
    class_weight='balanced',  # Handle class imbalance
    random_state=42,
    solver='lbfgs'
)
model_lr.fit(X_train_processed, y_train)
time_lr = time.time() - start
models_dict['Logistic Regression'] = model_lr
predictions_dict['Logistic Regression'] = {
    'proba': model_lr.predict_proba(X_test_processed)[:, 1],
    'pred': model_lr.predict(X_test_processed),
    'time': time_lr
}
print(f"  Training time: {time_lr:.2f}s")

# Model 2: Random Forest (ensemble, handles non-linearity well)
print("\n[2/4] Training Random Forest Classifier...")
start = time.time()
model_rf = RandomForestClassifier(
    n_estimators=100,
    max_depth=10,
    min_samples_split=10,
    random_state=42,
    n_jobs=-1,
    class_weight='balanced'
)
model_rf.fit(X_train_processed, y_train)
time_rf = time.time() - start
models_dict['Random Forest'] = model_rf
predictions_dict['Random Forest'] = {
    'proba': model_rf.predict_proba(X_test_processed)[:, 1],
    'pred': model_rf.predict(X_test_processed),
    'time': time_rf
}
print(f"  Training time: {time_rf:.2f}s")

# Model 3: Gradient Boosting (boosting, captures complex interactions)
print("\n[3/4] Training Gradient Boosting Classifier...")
start = time.time()
model_gb = GradientBoostingClassifier(
    n_estimators=100,
    max_depth=5,
    learning_rate=0.1,
    random_state=42,
    subsample=0.8
)
model_gb.fit(X_train_processed, y_train)
time_gb = time.time() - start
models_dict['Gradient Boosting'] = model_gb
predictions_dict['Gradient Boosting'] = {
    'proba': model_gb.predict_proba(X_test_processed)[:, 1],
    'pred': model_gb.predict(X_test_processed),
    'time': time_gb
}
print(f"  Training time: {time_gb:.2f}s")

# Model 4: HistGradient Boosting (faster than GB, good for large data)
print("\n[4/4] Training Histogram-based Gradient Boosting...")
start = time.time()
model_hgb = HistGradientBoostingClassifier(
    max_iter=100,
    max_depth=10,
    learning_rate=0.1,
    random_state=42
)
model_hgb.fit(X_train_processed, y_train)
time_hgb = time.time() - start
models_dict['Hist Gradient Boosting'] = model_hgb
predictions_dict['Hist Gradient Boosting'] = {
    'proba': model_hgb.predict_proba(X_test_processed)[:, 1],
    'pred': model_hgb.predict(X_test_processed),
    'time': time_hgb
}
print(f"  Training time: {time_hgb:.2f}s")

print(f"\nCompleted training {len(models_dict)} models!")
print(f"Total time: {time_lr + time_rf + time_gb + time_hgb:.2f}s")

Train Multiple Models to Predict Cancellation

[1/4] Training Logistic Regression...
  Training time: 0.95s

[2/4] Training Random Forest Classifier...
  Training time: 1.14s

[3/4] Training Gradient Boosting Classifier...
  Training time: 26.15s

[4/4] Training Histogram-based Gradient Boosting...
  Training time: 2.55s

Completed training 4 models!
Total time: 30.78s


In [343]:
# Evaluate and compare all models
print("=" * 70)
print("Model Performance Comparison")
print("=" * 70)

# Calculate metrics for all models
metrics_comparison = []

for model_name, preds in predictions_dict.items():
    y_proba = preds['proba']
    y_pred = preds['pred']
    train_time = preds['time']
    
    # PR-AUC (preferred metric for imbalanced data)
    precision_vals, recall_vals, _ = precision_recall_curve(y_test, y_proba)
    pr_auc = auc(recall_vals, precision_vals)
    
    # ROC-AUC
    roc_auc = roc_auc_score(y_test, y_proba)
    
    # Classification metrics at threshold=0.5
    precision = precision_score(y_test, y_pred)
    recall = recall_score(y_test, y_pred)
    f1 = f1_score(y_test, y_pred)
    
    metrics_comparison.append({
        'Model': model_name,
        'PR-AUC': pr_auc,
        'ROC-AUC': roc_auc,
        'Precision@0.5': precision,
        'Recall@0.5': recall,
        'F1@0.5': f1,
        'Time (s)': train_time
    })

metrics_df = pd.DataFrame(metrics_comparison)
metrics_df = metrics_df.sort_values('PR-AUC', ascending=False)

print("\nDetailed Comparison Table:")
print(metrics_df.to_string(index=False))

# Identify best model
best_model_name = metrics_df.iloc[0]['Model']
best_pr_auc = metrics_df.iloc[0]['PR-AUC']

print(f"\n{'='*70}")
print(f"BEST MODEL: {best_model_name}")
print(f"PR-AUC: {best_pr_auc:.4f}")
print(f"{'='*70}")

# Save best model for use
best_model = models_dict[best_model_name]
best_proba = predictions_dict[best_model_name]['proba']

Model Performance Comparison

Detailed Comparison Table:
                 Model   PR-AUC  ROC-AUC  Precision@0.5  Recall@0.5   F1@0.5  Time (s)
Hist Gradient Boosting 0.800596 0.913952       0.753821    0.670571 0.709763  2.547571
     Gradient Boosting 0.788597 0.907386       0.755880    0.638569 0.692290 26.145532
         Random Forest 0.743036 0.884064       0.540562    0.873876 0.667946  1.136443
   Logistic Regression 0.651260 0.837846       0.526595    0.788956 0.631614  0.954202

BEST MODEL: Hist Gradient Boosting
PR-AUC: 0.8006


#### **Biểu đồ Precision-Recall so sánh 4 mô hình**

In [344]:
fig = go.Figure()

# Colors for each model
colors = {
    'Logistic Regression': 'steelblue',
    'Random Forest': 'green',
    'Gradient Boosting': 'orangered',
    'Hist Gradient Boosting': 'purple'
}

# Draw PR curve for each model
for model_name, preds in predictions_dict.items():
    y_proba = preds['proba']
    precision_vals, recall_vals, _ = precision_recall_curve(y_test, y_proba)
    pr_auc = auc(recall_vals, precision_vals)
    
    fig.add_trace(go.Scatter(
        x=recall_vals,
        y=precision_vals,
        mode='lines',
        name=f'{model_name} (AUC={pr_auc:.3f})',
        line=dict(color=colors.get(model_name, 'gray'), width=2)
    ))

# Baseline (random classifier)
baseline_precision = y_test.mean()
fig.add_trace(go.Scatter(
    x=[0, 1],
    y=[baseline_precision, baseline_precision],
    mode='lines',
    name=f'Baseline (random, {baseline_precision:.3f})',
    line=dict(color='gray', width=1, dash='dash')
))

fig.update_layout(
    title='<b>Precision-Recall Curve - Compare 4 Models</b>',
    xaxis_title='Recall (Sensitivity)',
    yaxis_title='Precision (Accuracy)',
    height=500,
    template='plotly_white',
    legend=dict(x=0.02, y=0.02, bgcolor='rgba(255,255,255,0.8)')
)

fig.show()

print("\nPR-AUC Explanation:")
for model_name in metrics_df['Model']:
    pr_auc_val = metrics_df[metrics_df['Model'] == model_name]['PR-AUC'].values[0]
    print(f"  - {model_name}: {pr_auc_val:.3f}")
print(f"\nHigher PR-AUC = Better cancellation detection in imbalanced data")



PR-AUC Explanation:
  - Hist Gradient Boosting: 0.801
  - Gradient Boosting: 0.789
  - Random Forest: 0.743
  - Logistic Regression: 0.651

Higher PR-AUC = Better cancellation detection in imbalanced data


Đường PR cho thấy HGB duy trì precision cao hơn trên hầu hết miền recall, đặc biệt ở vùng recall trung bình–cao (quan trọng với revenue optimization).
Logistic Regression suy giảm precision nhanh khi recall tăng, phản ánh hạn chế trong việc mô hình hóa quan hệ phi tuyến.
Khoảng cách rõ rệt với baseline (random) xác nhận mô hình học được tín hiệu thực.

Kết luận bước B2
HGB không chỉ tốt về chỉ số tổng hợp (PR-AUC) mà còn ổn định hơn theo nhiều ngưỡng quyết định, phù hợp cho bài toán ra quyết định giá.

**Chart tổng kết: So sánh toàn diện các mô hình**

In [345]:
# Prepare data
models_names = metrics_df['Model'].tolist()
pr_aucs = metrics_df['PR-AUC'].tolist()
roc_aucs = metrics_df['ROC-AUC'].tolist()
f1_scores = metrics_df['F1@0.5'].tolist()
train_times = metrics_df['Time (s)'].tolist()

# Create 2x2 subplot
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=(
        'PR-AUC (Main Metric)', 
        'ROC-AUC',
        'F1-Score @ threshold 0.5',
        'Training Time (s)'
    ),
    vertical_spacing=0.25,
    horizontal_spacing=0.18
)

# Color for each model
model_colors = ['steelblue', 'green', 'orangered', 'purple']

# 1. PR-AUC
fig.add_trace(
    go.Bar(
        x=models_names,
        y=pr_aucs,
        name='PR-AUC',
        marker_color=model_colors,
        text=[f'{v:.3f}' for v in pr_aucs],
        textposition='outside',
        showlegend=False
    ),
    row=1, col=1
)

# 2. ROC-AUC
fig.add_trace(
    go.Bar(
        x=models_names,
        y=roc_aucs,
        name='ROC-AUC',
        marker_color=model_colors,
        text=[f'{v:.3f}' for v in roc_aucs],
        textposition='outside',
        showlegend=False
    ),
    row=1, col=2
)

# 3. F1-Score
fig.add_trace(
    go.Bar(
        x=models_names,
        y=f1_scores,
        name='F1-Score',
        marker_color=model_colors,
        text=[f'{v:.3f}' for v in f1_scores],
        textposition='outside',
        showlegend=False
    ),
    row=2, col=1
)

# 4. Training Time
fig.add_trace(
    go.Bar(
        x=models_names,
        y=train_times,
        name='Training Time',
        marker_color=model_colors,
        text=[f'{v:.1f}s' for v in train_times],
        textposition='outside',
        showlegend=False
    ),
    row=2, col=2
)

# Update axes
fig.update_xaxes(tickangle=-45)
fig.update_yaxes(range=[0, 1], row=1, col=1)
fig.update_yaxes(range=[0, 1], row=1, col=2)
fig.update_yaxes(range=[0, 1], row=2, col=1)

# Layout
fig.update_layout(
    title_text='<b>Summary Comparison of 4 ML Models - All Metrics</b>',
    height=800,
    template='plotly_white',
    showlegend=False,
    margin=dict(t=100, b=80, l=60, r=60)
)

fig.show()

print("\nOverall Observations:")
print(f"  Best model (PR-AUC):        {best_model_name}")
print(f"  Fastest model:              {metrics_df.iloc[-1]['Model']}")



Overall Observations:
  Best model (PR-AUC):        Hist Gradient Boosting
  Fastest model:              Logistic Regression


- Biểu đồ cho thấy Hist Gradient Boosting (HGB) đạt PR-AUC cao nhất (0.801), vượt trội trong bối cảnh dữ liệu mất cân bằng.
- Logistic Regression có hiệu năng thấp nhất nhưng thời gian huấn luyện nhanh nhất.
- Gradient Boosting và Random Forest nằm ở mức trung gian, với trade-off rõ ràng giữa hiệu năng và chi phí tính toán.

In [346]:
# Confusion matrix for best model
print("=" * 70)
print(f"Confusion Matrix - {best_model_name}")
print("=" * 70)

# Get predictions from the best model
y_pred = predictions_dict[best_model_name]['pred']

cm = confusion_matrix(y_test, y_pred)

print("\nPredicted         Not Cancel  Cancel")
print(f"Actual Not Cancel  {cm[0,0]:>6}  {cm[0,1]:>6}")
print(f"       Cancel      {cm[1,0]:>6}  {cm[1,1]:>6}")

print("\nClassification Report:")
print(classification_report(y_test, y_pred, target_names=['Not Cancel', 'Cancel']))


Confusion Matrix - Hist Gradient Boosting

Predicted         Not Cancel  Cancel
Actual Not Cancel   11456    1047
       Cancel        1575    3206

Classification Report:
              precision    recall  f1-score   support

  Not Cancel       0.88      0.92      0.90     12503
      Cancel       0.75      0.67      0.71      4781

    accuracy                           0.85     17284
   macro avg       0.82      0.79      0.80     17284
weighted avg       0.84      0.85      0.85     17284



#### **2. Lựa chọn mô hình và kiểm tra hiệu chuẩn xác suất:**

In [347]:
# B2: Check probability calibration
from sklearn.calibration import calibration_curve

print("=" * 70)
print("B2. Check Probability Calibration")
print("=" * 70)

# Plot #3: Calibration curve for all models
fig = go.Figure()

# Perfect calibration line
fig.add_trace(go.Scatter(
    x=[0, 1],
    y=[0, 1],
    mode='lines',
    name='Perfect Calibration',
    line=dict(color='gray', width=2, dash='dash')
))

# Calibration curve for each model
model_colors = {
    'Logistic Regression': 'steelblue',
    'Random Forest': 'green',
    'Gradient Boosting': 'orangered',
    'Hist Gradient Boosting': 'purple'
}

for model_name, preds in predictions_dict.items():
    y_proba = preds['proba']
    prob_true, prob_pred = calibration_curve(y_test, y_proba, n_bins=10, strategy='uniform')
    
    fig.add_trace(go.Scatter(
        x=prob_pred,
        y=prob_true,
        mode='lines+markers',
        name=model_name,
        line=dict(color=model_colors.get(model_name, 'gray'), width=2),
        marker=dict(size=8)
    ))

fig.update_layout(
    title='<b>Probability Calibration Curve - 4 Models</b>',
    xaxis_title='Predicted Probability',
    yaxis_title='Actual Positive Class Fraction',
    height=500,
    template='plotly_white',
    legend=dict(x=0.02, y=0.98, bgcolor='rgba(255,255,255,0.8)')
)

fig.show()

B2. Check Probability Calibration


**Nhận xét:**

- Hist Gradient Boosting và Gradient Boosting bám rất sát đường chéo → xác suất dự đoán đáng tin cậy.
- Random Forest lệch ở một số vùng → xác suất chưa ổn định.
- Logistic Regression thường đánh giá thấp rủi ro hủy ở mức xác suất cao.

**Kết luận:**
- Vì dùng xác suất hủy để tính doanh thu kỳ vọng, nên calibration quan trọng hơn accuracy.
- Hist Gradient Boosting là lựa chọn phù hợp cho bước tối ưu doanh thu.

#### **3. Tính toán doanh thu thực nhận kỳ vọng (Expected Realized Revenue)**

In [348]:
df_test_results = meta_test.copy()
df_test_results['actual_cancel'] = y_test.values
df_test_results['p_cancel_pred'] = best_proba

# E[Revenue] = revenue_if_show × (1 - p_cancel)
df_test_results['expected_revenue'] = (
    df_test_results['revenue_if_show'] * (1 - df_test_results['p_cancel_pred'])
)

df_test_results['actual_revenue'] = df_test_results['revenue_if_show'] * (1 - df_test_results['actual_cancel'])

print("\nExpected Revenue Formula:")
print("  E[Revenue_i] = revenue_if_show_i × (1 - p_cancel_pred_i)")
print("  where revenue_if_show_i = adr_clean_i × total_nights_i")

print(f"\nTest Set Statistics:")
print(f"  Avg revenue if no cancel:       {df_test_results['revenue_if_show'].mean():.2f} EUR")
print(f"  Avg predicted cancel probability: {df_test_results['p_cancel_pred'].mean():.3f}")
print(f"  Avg expected revenue:             {df_test_results['expected_revenue'].mean():.2f} EUR")
print(f"  Avg actual revenue:               {df_test_results['actual_revenue'].mean():.2f} EUR")

revenue_loss_pct = (1 - df_test_results['expected_revenue'].sum() / df_test_results['revenue_if_show'].sum()) * 100
print(f"\nExpected revenue loss rate due to cancellations: {revenue_loss_pct:.1f}%")

print("\nData ready for ADR optimization step.")



Expected Revenue Formula:
  E[Revenue_i] = revenue_if_show_i × (1 - p_cancel_pred_i)
  where revenue_if_show_i = adr_clean_i × total_nights_i

Test Set Statistics:
  Avg revenue if no cancel:       395.65 EUR
  Avg predicted cancel probability: 0.277
  Avg expected revenue:             264.59 EUR
  Avg actual revenue:               264.10 EUR

Expected revenue loss rate due to cancellations: 33.1%

Data ready for ADR optimization step.


#### **4. Tìm mức ADR tối ưu theo phân khúc (cốt lõi của Q7)**

In [349]:
# Create ADR bins (10 quantiles for detailed analysis)
df_test_results['adr_bin'] = pd.qcut(
    df_test_results['adr_clean'], 
    q=10, 
    duplicates='drop'
)

# Get bin labels (median ADR in each bin)
df_test_results['adr_bin_label'] = df_test_results.groupby('adr_bin')['adr_clean'].transform('median')

print(f"\nCreated {df_test_results['adr_bin'].nunique()} ADR bins")

# Aggregate by hotel and ADR bin
optimization_results = df_test_results.groupby(['hotel', 'adr_bin_label']).agg({
    'adr_clean': ['count', 'mean'],
    'p_cancel_pred': 'mean',
    'expected_revenue': 'mean',
    'revenue_if_show': 'mean'
}).round(2)

optimization_results.columns = ['count', 'mean_adr', 'mean_p_cancel', 'mean_expected_revenue', 'mean_revenue_if_show']
optimization_results = optimization_results.reset_index()

print("\nOptimization Results Preview:")
print(optimization_results.head(10))

# Find optimal ADR for each hotel
optimal_adr_q4 = {}
for hotel_type in ['City Hotel', 'Resort Hotel']:
    hotel_data = optimization_results[optimization_results['hotel'] == hotel_type]
    
    # Filter bins with sufficient samples (at least 20 bookings)
    hotel_data_filtered = hotel_data[hotel_data['count'] >= 20]
    
    if len(hotel_data_filtered) > 0:
        optimal_row = hotel_data_filtered.loc[hotel_data_filtered['mean_expected_revenue'].idxmax()]
        optimal_adr_q4[hotel_type] = {
            'optimal_adr_bin': optimal_row['adr_bin_label'],
            'optimal_expected_revenue': optimal_row['mean_expected_revenue'],
            'optimal_p_cancel': optimal_row['mean_p_cancel'],
            'optimal_count': optimal_row['count']
        }
    
print("\nOptimal ADR by Hotel Type:")
for hotel_type, results in optimal_adr_q4.items():
    print(f"\n{hotel_type}:")
    print(f"  Optimal ADR bin (median):         {results['optimal_adr_bin']:.2f} EUR")
    print(f"  Expected revenue at optimal:      {results['optimal_expected_revenue']:.2f} EUR")
    print(f"  Predicted cancel rate:            {results['optimal_p_cancel']:.1%}")
    print(f"  Sample size:                      {results['optimal_count']:.0f} bookings")



Created 10 ADR bins

Optimization Results Preview:
        hotel  adr_bin_label  count  mean_adr  mean_p_cancel  \
0  City Hotel         38.400    238     11.41           0.18   
1  City Hotel         59.400    616     61.46           0.23   
2  City Hotel         72.250   1025     72.66           0.25   
3  City Hotel         82.035   1216     82.95           0.27   
4  City Hotel         94.000   1469     93.62           0.29   
5  City Hotel        106.000   1243    105.70           0.33   
6  City Hotel        119.000   1361    119.21           0.33   
7  City Hotel        135.000   1330    135.12           0.35   
8  City Hotel        157.500   1156    157.10           0.33   
9  City Hotel        205.000    803    204.06           0.35   

   mean_expected_revenue  mean_revenue_if_show  
0                  31.32                 41.52  
1                 138.41                181.16  
2                 177.95                250.74  
3                 181.93                257.68 

**Nhận xét:**
- Khi ADR tăng, xác suất hủy cũng tăng.

- Tuy nhiên, doanh thu kỳ vọng vẫn có thể tăng nếu mức tăng ADR lớn hơn phần doanh thu mất do hủy.

- Trong dữ liệu này, ADR ~205 EUR cho doanh thu kỳ vọng cao nhất ở cả City và Resort.

Điều này cho thấy: giá cao không xấu nếu mức tăng giá “đáng” hơn rủi ro hủy.

**Plot: Doanh thu kỳ vọng theo mức ADR (City vs Resort)**

In [350]:
fig = go.Figure()

for hotel_type, color in [('City Hotel', 'steelblue'), ('Resort Hotel', 'coral')]:
    hotel_data = optimization_results[optimization_results['hotel'] == hotel_type]
    
    fig.add_trace(go.Scatter(
        x=hotel_data['adr_bin_label'],
        y=hotel_data['mean_expected_revenue'],
        mode='lines+markers',
        name=hotel_type,
        line=dict(color=color, width=3),
        marker=dict(size=10)
    ))
    
    # Mark optimal point
    if hotel_type in optimal_adr_q4:
        optimal = optimal_adr_q4[hotel_type]
        fig.add_trace(go.Scatter(
            x=[optimal['optimal_adr_bin']],
            y=[optimal['optimal_expected_revenue']],
            mode='markers',
            name=f'{hotel_type} (Optimal)',
            marker=dict(
                size=20, 
                color=color, 
                symbol='star',
                line=dict(color='black', width=2)
            ),
            showlegend=True
        ))

fig.update_layout(
    title='<b>Expected Revenue by ADR Level (City vs Resort)</b>',
    xaxis_title='ADR (EUR)',
    yaxis_title='Average Expected Revenue (EUR)',
    height=500,
    template='plotly_white',
    legend=dict(x=0.02, y=0.98, bgcolor='rgba(255,255,255,0.8)'),
    hovermode='x unified'
)

fig.show()


**Nhận xét:**

- Đường cong có điểm đỉnh (sweet spot).

- Sau điểm này, tăng ADR thêm không còn hiệu quả vì rủi ro hủy tăng nhanh hơn lợi ích giá.

- Resort luôn có expected revenue cao hơn City tại cùng mức ADR → khách Resort ổn định hơn.

**Kết luận:** City cần thận trọng hơn khi tăng giá; Resort có “room” để premium pricing

**Plot: Xác suất hủy dự đoán theo ADR (giải thích đường cong doanh thu)**

In [351]:
fig = go.Figure()

for hotel_type, color in [('City Hotel', 'steelblue'), ('Resort Hotel', 'coral')]:
    hotel_data = optimization_results[optimization_results['hotel'] == hotel_type]
    
    fig.add_trace(go.Scatter(
        x=hotel_data['adr_bin_label'],
        y=hotel_data['mean_p_cancel'] * 100,  # Convert to percentage
        mode='lines+markers',
        name=hotel_type,
        line=dict(color=color, width=3),
        marker=dict(size=10)
    ))

fig.update_layout(
    title='<b>Predicted Cancel Probability by ADR</b>',
    xaxis_title='ADR (EUR)',
    yaxis_title='Average Predicted Cancel Probability (%)',
    height=450,
    template='plotly_white',
    legend=dict(x=0.02, y=0.98, bgcolor='rgba(255,255,255,0.8)'),
    hovermode='x unified'
)

fig.show()


**Nhận xét:**

- Xác suất hủy tăng đều theo ADR ở cả hai loại khách sạn.
- City có rủi ro hủy cao hơn Resort ở mức ADR thấp–trung bình.
- Ở ADR rất cao, rủi ro của hai loại gần tương đương.

**Kết luận:** Điều này giải thích vì sao City “nhạy giá” hơn Resor

**Heatmap theo phân khúc thị trường**

In [352]:
df_test_results['adr_bin_simple'] = pd.qcut(
    df_test_results['adr_clean'], 
    q=5, 
    labels=['Very Low', 'Low', 'Medium', 'High', 'Very High'],
    duplicates='drop'
)

segment_heatmap = df_test_results.groupby(['market_segment', 'adr_bin_simple']).agg({
    'expected_revenue': 'mean'
}).reset_index()

segment_pivot = segment_heatmap.pivot(
    index='market_segment',
    columns='adr_bin_simple',
    values='expected_revenue'
)

top_segments_q4 = df_test_results['market_segment'].value_counts().head(6).index
segment_pivot_filtered = segment_pivot.loc[segment_pivot.index.isin(top_segments_q4)]

fig = go.Figure(data=go.Heatmap(
    z=segment_pivot_filtered.values,
    x=segment_pivot_filtered.columns,
    y=segment_pivot_filtered.index,
    colorscale='RdYlGn',
    text=segment_pivot_filtered.values.round(1),
    texttemplate='%{text}',
    textfont={"size": 10},
    colorbar=dict(title='Expected<br>Revenue (EUR)')
))

fig.update_layout(
    title='<b>Optional: Expected Revenue by Segment × ADR Level</b>',
    xaxis_title='ADR Level',
    yaxis_title='Market Segment',
    height=450,
    template='plotly_white'
)

fig.show()

print("\nOptimal ADR by Segment:")
for segment in top_segments_q4[:3]:  
    seg_data = segment_pivot_filtered.loc[segment]
    optimal_adr_level = seg_data.idxmax()
    optimal_revenue = seg_data.max()
    print(f"  {segment}: {optimal_adr_level} (revenue={optimal_revenue:.2f} EUR)")



Optimal ADR by Segment:
  Online TA: Very High (revenue=379.79 EUR)
  Offline TA/TO: Very High (revenue=786.92 EUR)
  Direct: Very High (revenue=592.76 EUR)


- Online TA: doanh thu tăng mạnh ở ADR cao nhưng đi kèm rủi ro hủy cao.

- Direct / Offline TA/TO: doanh thu rất tốt ở ADR cao → kênh ổn định.

- Corporate: tăng trưởng chậm → ít nhạy với giá.

Không nên dùng một mức giá cho tất cả phân khúc.

### **C. Kết quả & Giải thích**

#### **1. Tóm tắt lựa chọn mô hình**

1. **Hiệu suất**: Hist Gradient Boosting đạt PR-AUC cao nhất (0.801), cho thấy khả năng phát hiện hủy phòng tốt hơn các mô hình khác trong dữ liệu mất cân bằng (tỷ lệ hủy = 27.5%)

2. **Phi tuyến và tương tác**: HistGB bắt được quan hệ phi tuyến và tương tác phức tạp giữa ADR, lead_time, deposit_type, và các biến khác - điều mà Logistic Regression không làm được

3. **Hiệu quả**: Thời gian huấn luyện (~4s) nhanh hơn đáng kể so với Gradient Boosting thông thường (~25s) nhờ sử dụng histogram-based approach

4. **Hiệu chuẩn**: Mặc dù ensemble methods có thể cần hiệu chuẩn, HistGB cho xác suất dự đoán khá hợp lý

5. **Bối cảnh kinh doanh**: Vì cần dự đoán chính xác P(cancel) để tính expected revenue, mô hình với PR-AUC cao nhất được ưu tiên hơn.

#### **2. Mức ADR tối ưu**

In [353]:
print("=" * 70)
print("ANSWER TO Q7: OPTIMAL ADR BY HOTEL TYPE")
print("=" * 70)

for hotel_type in ['City Hotel', 'Resort Hotel']:
    if hotel_type in optimal_adr_q4:
        results = optimal_adr_q4[hotel_type]
        print(f"\n{hotel_type.upper()}:")
        print(f"  Optimal ADR bin (median):         {results['optimal_adr_bin']:.2f} EUR")
        print(f"  Expected revenue at optimal:      {results['optimal_expected_revenue']:.2f} EUR")
        print(f"  Predicted cancel rate:            {results['optimal_p_cancel']:.1%}")
        print(f"  Sample size:                      {results['optimal_count']:.0f} bookings")

# Show top 3 market segments
print("\n" + "=" * 70)
print("OPTIMAL ADR BY MARKET SEGMENT (Top 3 by Volume)")
print("=" * 70)

segment_optimization = df_test_results.groupby(['market_segment', 'adr_bin_simple']).agg({
    'expected_revenue': 'mean',
    'p_cancel_pred': 'mean',
    'adr_clean': ['count', 'mean']
}).reset_index()

segment_optimization.columns = ['market_segment', 'adr_level', 'mean_expected_revenue', 
                                 'mean_p_cancel', 'count', 'mean_adr']

for segment in top_segments_q4[:3]:
    seg_data = segment_optimization[segment_optimization['market_segment'] == segment]
    seg_data_filtered = seg_data[seg_data['count'] >= 10]
    
    if len(seg_data_filtered) > 0:
        optimal_seg = seg_data_filtered.loc[seg_data_filtered['mean_expected_revenue'].idxmax()]
        print(f"\n{segment}:")
        print(f"  Optimal ADR level:            {optimal_seg['adr_level']}")
        print(f"  Expected revenue:             {optimal_seg['mean_expected_revenue']:.2f} EUR")
        print(f"  Predicted cancel rate:        {optimal_seg['mean_p_cancel']:.1%}")

print("\n" + "=" * 70)


ANSWER TO Q7: OPTIMAL ADR BY HOTEL TYPE

CITY HOTEL:
  Optimal ADR bin (median):         205.00 EUR
  Expected revenue at optimal:      369.08 EUR
  Predicted cancel rate:            35.0%
  Sample size:                      803 bookings

RESORT HOTEL:
  Optimal ADR bin (median):         205.00 EUR
  Expected revenue at optimal:      632.98 EUR
  Predicted cancel rate:            37.0%
  Sample size:                      926 bookings

OPTIMAL ADR BY MARKET SEGMENT (Top 3 by Volume)

Online TA:
  Optimal ADR level:            Very High
  Expected revenue:             379.79 EUR
  Predicted cancel rate:        40.0%

Offline TA/TO:
  Optimal ADR level:            Very High
  Expected revenue:             786.92 EUR
  Predicted cancel rate:        22.9%

Direct:
  Optimal ADR level:            Very High
  Expected revenue:             592.76 EUR
  Predicted cancel rate:        15.9%



Kết quả tối ưu hóa dựa trên Expected Realized Revenue cho thấy cả hai loại khách sạn đạt doanh thu kỳ vọng cao nhất tại mức ADR cao (median ≈ 205 EUR). Tuy nhiên, mức doanh thu kỳ vọng và rủi ro hủy khác nhau đáng kể giữa hai loại.

- City Hotel đạt doanh thu kỳ vọng tối ưu khoảng 369.08 EUR, đi kèm xác suất hủy dự đoán 35.0%.
- Resort Hotel đạt doanh thu kỳ vọng cao hơn, khoảng 632.98 EUR, với xác suất hủy dự đoán 37.0%.

Sự khác biệt này phản ánh đặc điểm hành vi và giá trị lưu trú trung bình khác nhau giữa hai phân khúc khách sạn, ngay cả khi mức ADR tối ưu danh nghĩa tương đồng.

### **D. Ý nghĩa kinh doanh:**

**1. Trade-off giữa giá và hủy là rõ ràng và có thể định lượng:**
Tăng ADR làm tăng doanh thu tiềm năng nhưng đồng thời làm tăng xác suất hủy; do đó, tối ưu hóa cần dựa trên doanh thu thực nhận kỳ vọng, không phải ADR danh nghĩa.

**2. Chiến lược giá cần phân biệt theo loại khách sạn:**
City Hotel nhạy cảm với giá hơn, trong khi Resort Hotel có dư địa áp dụng mức giá cao nhờ giá trị lưu trú lớn hơn.

**3. Pricing theo phân khúc thị trường là bắt buộc:**
Các kênh như Online TA, Direct và Offline TA/TO phản ứng rất khác nhau với mức giá, đòi hỏi chính sách ADR và điều kiện hủy khác biệt.

**4. Kiểm soát rủi ro hủy là yếu tố song hành với tăng giá:**
Các công cụ như chính sách đặt cọc, điều khoản hủy linh hoạt hoặc quản lý lead time (đã xác định ở Q5) cần được sử dụng để hỗ trợ chiến lược giá cao.

**5. Ra quyết định dựa trên mô hình dữ liệu vượt trội hơn trực giác:**
Mô hình Hist Gradient Boosting (PR-AUC = 0.801) cho phép ước lượng xác suất hủy đủ chính xác để phục vụ bài toán tối ưu doanh thu.

### **E. Hạn chế:**

- Phân tích dựa trên dữ liệu quan sát lịch sử, do đó không khẳng định quan hệ nhân quả tuyệt đối.
- Thiếu các biến ngữ cảnh quan trọng như giá đối thủ, sự kiện đặc biệt, và yếu tố kinh tế vĩ mô.
- Xác suất dự đoán, dù đã kiểm tra calibration, vẫn có thể cần hiệu chỉnh thêm trước khi triển khai thực tế.
- Mức ADR tối ưu có thể thay đổi theo mùa và thời gian, trong khi mô hình hiện tại mang tính tĩnh.
- Phân tích chưa đi sâu theo loại phòng hoặc gói dịch vụ cụ thể.

### **F. Kết luận:**

Kết quả cho thấy tối ưu hóa doanh thu khách sạn không đồng nghĩa với việc tối đa hóa ADR, mà là bài toán cân bằng giữa mức giá và rủi ro hủy phòng. Việc kết hợp mô hình dự đoán xác suất hủy với hàm doanh thu kỳ vọng cho phép xác định ADR tối ưu theo từng loại khách sạn và phân khúc thị trường, cung cấp cơ sở định lượng vững chắc cho các quyết định pricing chiến lược.

---

## Q8 - Tác Động Kinh Doanh/Vận Hành (What-if Analysis)

**Nếu áp dụng mức ADR tối ưu (từ Q7) cho từng loại khách sạn, doanh thu thực nhận kỳ vọng và tỷ lệ hủy kỳ vọng sẽ thay đổi như thế nào so với mức giá hiện tại?**


### **A. Chuẩn bị dữ liệu mô phỏng**

#### Quy trình:
1. **Inputs từ Q7**: Lấy dữ liệu test, optimal ADR, model tốt nhất
2. **Định nghĩa ADR tối ưu**: Sử dụng giá trị trung vị từ bin tối ưu ở Q4
3. **Tạo 2 kịch bản**:
   - **Current scenario**: Giá hiện tại (adr_clean)
   - **Optimized scenario**: Áp dụng ADR tối ưu
4. **Cập nhật xác suất hủy**: Predict lại p_cancel với ADR mới (Cách 2 - thực tế hơn)

### Lưu ý:
- Cập nhật p_cancel theo ADR mới (phản ánh trade-off Q6/Q7)
- Giả định: Các biến khác không đổi, chỉ thay ADR

In [354]:
print("=" * 80)
print("1. PREPARE TEST DATA WITH PREDICTIONS")
print("=" * 80)

# Get test data and metadata
df_q8 = df_test_results.copy()

# Add predictions from best model (Hist Gradient Boosting)
df_q8['p_cancel_current'] = best_proba

# Add necessary variables
df_q8['adr_current'] = df_q8['adr_clean']
df_q8['revenue_if_show_current'] = df_q8['adr_clean'] * df_q8['total_nights']
df_q8['expected_rev_current'] = df_q8['revenue_if_show_current'] * (1 - df_q8['p_cancel_current'])

print(f"\nNumber of bookings to evaluate: {len(df_q8):,}")
print(f"Total current expected revenue: {df_q8['expected_rev_current'].sum():,.2f} EUR")
print(f"Overall current expected cancel rate: {df_q8['p_cancel_current'].mean():.4f}")
print("\nDistribution by hotel:")
print(df_q8.groupby('hotel').agg({
    'expected_rev_current': 'sum',
    'p_cancel_current': 'mean'
}).round(2))


1. PREPARE TEST DATA WITH PREDICTIONS

Number of bookings to evaluate: 17,284
Total current expected revenue: 4,573,168.67 EUR
Overall current expected cancel rate: 0.2769

Distribution by hotel:
              expected_rev_current  p_cancel_current
hotel                                               
City Hotel              2411042.27              0.30
Resort Hotel            2162126.40              0.23


In [355]:
print("\n" + "=" * 80)
print("2. DEFINE OPTIMAL ADR FOR EACH HOTEL")
print("=" * 80)

# From Q4, we already have optimal ADR bin for each hotel
# Use that value as the optimal ADR to apply

optimal_adr_values = {}

for hotel in ['City Hotel', 'Resort Hotel']:
    # Get optimal ADR bin from Q4 (this is the median value of the optimal bin)
    optimal_value = optimal_adr_q4[hotel]['optimal_adr_bin']
    optimal_expected_rev = optimal_adr_q4[hotel]['optimal_expected_revenue']
    optimal_p_cancel = optimal_adr_q4[hotel]['optimal_p_cancel']
    optimal_count = optimal_adr_q4[hotel]['optimal_count']
    
    optimal_adr_values[hotel] = optimal_value
    
    print(f"\n{hotel}:")
    print(f"  Optimal ADR (from Q4): {optimal_value:.2f} EUR")
    print(f"  Expected revenue at optimal: {optimal_expected_rev:.2f} EUR/booking")
    print(f"  Cancel probability: {optimal_p_cancel:.4f}")
    print(f"  Number of bookings in optimal bin: {optimal_count:.0f}")

print("\n" + "=" * 80)
print("OPTIMAL ADR SUMMARY TABLE")
print("=" * 80)
for hotel, adr in optimal_adr_values.items():
    print(f"{hotel:20s}: {adr:>8.2f} EUR")



2. DEFINE OPTIMAL ADR FOR EACH HOTEL

City Hotel:
  Optimal ADR (from Q4): 205.00 EUR
  Expected revenue at optimal: 369.08 EUR/booking
  Cancel probability: 0.3500
  Number of bookings in optimal bin: 803

Resort Hotel:
  Optimal ADR (from Q4): 205.00 EUR
  Expected revenue at optimal: 632.98 EUR/booking
  Cancel probability: 0.3700
  Number of bookings in optimal bin: 926

OPTIMAL ADR SUMMARY TABLE
City Hotel          :   205.00 EUR
Resort Hotel        :   205.00 EUR


In [356]:
print("\n" + "=" * 80)
print("3. CREATE OPTIMIZED SCENARIO")
print("=" * 80)

# Apply optimal ADR for each hotel
df_q8['adr_optimized'] = df_q8['hotel'].map(optimal_adr_values)

# Calculate revenue if show with new ADR
df_q8['revenue_if_show_optimized'] = df_q8['adr_optimized'] * df_q8['total_nights']

# Create copy of features to predict with new ADR
X_test_optimized = X_test.copy()
X_test_optimized['adr_clean'] = df_q8['adr_optimized'].values

# Get feature list from Q4
all_features_q4 = numeric_cols_q4 + categorical_cols_q4

# Transform features with new ADR
X_test_optimized_processed = preprocessor.transform(X_test_optimized[all_features_q4])

# Predict cancel probability with new ADR (Method 2 - update risk)
print("\nPredicting cancel probability with optimal ADR...")
df_q8['p_cancel_optimized'] = best_model.predict_proba(X_test_optimized_processed)[:, 1]

# Calculate expected revenue with new ADR and risk
df_q8['expected_rev_optimized'] = df_q8['revenue_if_show_optimized'] * (1 - df_q8['p_cancel_optimized'])

# Calculate delta (change)
df_q8['delta_cancel_prob'] = df_q8['p_cancel_optimized'] - df_q8['p_cancel_current']
df_q8['uplift_revenue'] = df_q8['expected_rev_optimized'] - df_q8['expected_rev_current']
df_q8['uplift_revenue_pct'] = (df_q8['uplift_revenue'] / df_q8['expected_rev_current']) * 100

print("\nOptimized scenario created successfully!")
print(f"\nAverage changes:")
print(f"  ADR: {df_q8['adr_current'].mean():.2f} → {df_q8['adr_optimized'].mean():.2f} EUR")
print(f"  Δ Cancel prob: {df_q8['delta_cancel_prob'].mean():.4f}")
print(f"  Δ Revenue: {df_q8['uplift_revenue'].mean():.2f} EUR/booking")



3. CREATE OPTIMIZED SCENARIO

Predicting cancel probability with optimal ADR...

Optimized scenario created successfully!

Average changes:
  ADR: 106.80 → 205.00 EUR
  Δ Cancel prob: 0.0202
  Δ Revenue: 243.89 EUR/booking


### **B. Phân tích tác động**

### Nội dung phân tích:
1. **Đo uplift tổng thể & theo hotel**: Tổng doanh thu, tỷ lệ hủy kỳ vọng
2. **Ai tạo ra uplift?**: Phân tích đóng góp theo market segment
3. **Risk trade-off**: Uplift vs thay đổi rủi ro hủy

In [357]:
print("=" * 80)
print("1. OVERALL & HOTEL-LEVEL UPLIFT")
print("=" * 80)

# Calculate overall metrics
total_rev_current = df_q8['expected_rev_current'].sum()
total_rev_optimized = df_q8['expected_rev_optimized'].sum()
total_uplift = total_rev_optimized - total_rev_current
total_uplift_pct = (total_uplift / total_rev_current) * 100

cancel_prob_current = df_q8['p_cancel_current'].mean()
cancel_prob_optimized = df_q8['p_cancel_optimized'].mean()
delta_cancel = cancel_prob_optimized - cancel_prob_current

print("\nOVERALL (Overall)")
print(f"{'Metric':<40s} {'Current':>15s} {'Optimized':>15s} {'Change':>15s}")
print("=" * 80)
print(f"{'Total expected revenue (EUR)':<40s} {total_rev_current:>15,.2f} {total_rev_optimized:>15,.2f} {total_uplift:>15,.2f}")
print(f"{'Uplift %':<40s} {'-':>15s} {'-':>15s} {total_uplift_pct:>14.2f}%")
print(f"{'Expected cancel rate (prob)':<40s} {cancel_prob_current:>15.4f} {cancel_prob_optimized:>15.4f} {delta_cancel:>15.4f}")

# Calculate by hotel
hotel_summary = df_q8.groupby('hotel').agg({
    'expected_rev_current': 'sum',
    'expected_rev_optimized': 'sum',
    'p_cancel_current': 'mean',
    'p_cancel_optimized': 'mean',
    'adr_current': 'count'  # count bookings
}).reset_index()

hotel_summary.columns = ['hotel', 'rev_current', 'rev_optimized', 'cancel_current', 'cancel_optimized', 'count']
hotel_summary['uplift'] = hotel_summary['rev_optimized'] - hotel_summary['rev_current']
hotel_summary['uplift_pct'] = (hotel_summary['uplift'] / hotel_summary['rev_current']) * 100
hotel_summary['delta_cancel'] = hotel_summary['cancel_optimized'] - hotel_summary['cancel_current']

print("\n\nBY HOTEL")
print("=" * 80)
for _, row in hotel_summary.iterrows():
    print(f"\n{row['hotel']} (n={row['count']:,})")
    print(f"  Expected revenue: {row['rev_current']:,.2f} → {row['rev_optimized']:,.2f} EUR")
    print(f"  Uplift: {row['uplift']:+,.2f} EUR ({row['uplift_pct']:+.2f}%)")
    print(f"  Cancel prob: {row['cancel_current']:.4f} → {row['cancel_optimized']:.4f} (Δ {row['delta_cancel']:+.4f})")

# Save for visualization
uplift_summary_hotel = hotel_summary.copy()


1. OVERALL & HOTEL-LEVEL UPLIFT

OVERALL (Overall)
Metric                                           Current       Optimized          Change
Total expected revenue (EUR)                4,573,168.67    8,788,602.19    4,215,433.53
Uplift %                                               -               -          92.18%
Expected cancel rate (prob)                       0.2769          0.2970          0.0202


BY HOTEL

City Hotel (n=10,457)
  Expected revenue: 2,411,042.27 → 4,349,373.57 EUR
  Uplift: +1,938,331.30 EUR (+80.39%)
  Cancel prob: 0.3048 → 0.3258 (Δ +0.0210)

Resort Hotel (n=6,827)
  Expected revenue: 2,162,126.40 → 4,439,228.62 EUR
  Uplift: +2,277,102.22 EUR (+105.32%)
  Cancel prob: 0.2341 → 0.2530 (Δ +0.0189)


Việc áp dụng ADR tối ưu làm expected realized revenue tăng từ 4.57M EUR lên 8.79M EUR, tương đương +4.22M EUR (+92.18%). Tỷ lệ hủy kỳ vọng tăng nhẹ từ 0.2769 lên 0.2970 (+2.02 điểm %). Kết quả cho thấy lợi ích doanh thu vượt trội so với mức gia tăng rủi ro hủy.

**1. City Hotel**
- Đối với City Hotel, doanh thu kỳ vọng tăng từ 2.41M lên 4.35M EUR (+1.94M EUR; +80.39%). Xác suất hủy tăng từ 0.3048 lên 0.3258 (+2.10 điểm %). 
- Điều này cho thấy City Hotel hưởng lợi đáng kể từ chiến lược giá tối ưu, nhưng cần đi kèm các biện pháp kiểm soát rủi ro hủy.

**2. Resort Hotel**
- Resort Hotel ghi nhận mức cải thiện mạnh hơn, với doanh thu kỳ vọng tăng từ 2.16M lên 4.44M EUR (+2.28M EUR; +105.32%), trong khi xác suất hủy chỉ tăng từ 0.2341 lên 0.2530 (+1.89 điểm %). 
- Điều này phản ánh Resort Hotel ít nhạy cảm với rủi ro hủy hơn, do đó phù hợp để triển khai chiến lược ADR tối ưu sớm hơn.

**3. Nhận xét**

Kết quả xác nhận rằng tối ưu hóa giá dựa trên expected realized revenue mang lại uplift doanh thu rất lớn ở cả hai loại khách sạn, với mức tăng rủi ro hủy tương đối nhỏ. So sánh giữa hai loại cho thấy Resort Hotel có tỷ lệ risk–return tốt hơn, trong khi City Hotel cần chính sách bổ trợ (deposit, lead-time control) để cân bằng trade-ofKết quả tổng (Overall). Khi chuyển từ giá hiện tại sang ADR tối ưu, expected realized revenue tăng từ 4.57M EUR → 8.79M EUR (+4.22M EUR; +92.18%). Tuy nhiên xác suất hủy dự đoán tăng nhẹ từ 0.2769 → 0.2970 (+0.0202, ~+2.0 điểm %).

In [358]:
# "Who creates uplift?" — Analyze contribution by market segment
print("\n" + "=" * 80)
print("UPLIFT CONTRIBUTION BY MARKET SEGMENT")
print("=" * 80)

# Get top segments by volume (from Q4)
segment_analysis = df_q8.groupby('market_segment').agg({
    'uplift_revenue': ['sum', 'mean'],
    'delta_cancel_prob': 'mean',
    'adr_current': 'count'
}).reset_index()

segment_analysis.columns = ['market_segment', 'uplift_total', 'uplift_per_booking', 'delta_cancel', 'count']
segment_analysis['uplift_pct_contribution'] = (segment_analysis['uplift_total'] / total_uplift) * 100

# Sort by total uplift
segment_analysis_sorted = segment_analysis.sort_values('uplift_total', ascending=False)

print("\nTOP SEGMENTS BY TOTAL UPLIFT (Sorted by Total Uplift)")
print("=" * 100)
print(f"{'Market Segment':<25s} {'Count':>8s} {'Total Uplift':>15s} {'Per Booking':>15s} {'% Contribution':>12s} {'Δ Cancel':>12s}")
print("=" * 100)

for _, row in segment_analysis_sorted.head(10).iterrows():
    print(f"{row['market_segment']:<25s} "
          f"{row['count']:>8,} "
          f"{row['uplift_total']:>15,.2f} "
          f"{row['uplift_per_booking']:>15,.2f} "
          f"{row['uplift_pct_contribution']:>11.2f}% "
          f"{row['delta_cancel']:>12.4f}")

# Identify key insights
top_volume_segment = segment_analysis_sorted.iloc[0]
top_per_booking_segment = segment_analysis_sorted.sort_values('uplift_per_booking', ascending=False).iloc[0]

print("\n\nKEY INSIGHTS:")
print(f"  Highest total uplift segment (volume): {top_volume_segment['market_segment']}")
print(f"    - Total uplift: {top_volume_segment['uplift_total']:,.2f} EUR ({top_volume_segment['uplift_pct_contribution']:.1f}% of total uplift)")
print(f"    - Count: {top_volume_segment['count']:,} bookings")
print(f"\n  Highest uplift per booking segment: {top_per_booking_segment['market_segment']}")
print(f"    - Uplift per booking: {top_per_booking_segment['uplift_per_booking']:,.2f} EUR")
print(f"    - Count: {top_per_booking_segment['count']:,} bookings")

# Save for visualization
uplift_summary_segment = segment_analysis_sorted.copy()



UPLIFT CONTRIBUTION BY MARKET SEGMENT

TOP SEGMENTS BY TOTAL UPLIFT (Sorted by Total Uplift)
Market Segment               Count    Total Uplift     Per Booking % Contribution     Δ Cancel
Online TA                   10,210    1,776,791.50          174.02       42.15%       0.0251
Offline TA/TO                2,772    1,378,955.09          497.46       32.71%       0.0084
Direct                       2,305      461,652.02          200.28       10.95%       0.0191
Groups                         990      357,045.10          360.65        8.47%       0.0007
Corporate                      815      186,966.87          229.41        4.44%       0.0247
Other                          192       54,022.94          281.37        1.28%       0.0203


KEY INSIGHTS:
  Highest total uplift segment (volume): Online TA
    - Total uplift: 1,776,791.50 EUR (42.1% of total uplift)
    - Count: 10,210 bookings

  Highest uplift per booking segment: Offline TA/TO
    - Uplift per booking: 497.46 EUR
    - 

**Nhận xét:**
- Online TA là phân khúc đóng góp lớn nhất về tổng uplift, đạt 1.78M EUR, tương đương 42.15% tổng uplift, chủ yếu do quy mô booking rất lớn (10,210 bookings). Tuy nhiên, mức uplift trên mỗi booking ở mức trung bình (174 EUR) và đi kèm mức tăng xác suất hủy cao nhất (+2.51 điểm %).

- Ngược lại, Offline TA/TO tạo ra uplift trên mỗi booking cao nhất (~497 EUR/booking) với đóng góp tổng thể 32.71%, trong khi mức tăng rủi ro hủy thấp (+0.84 điểm %). Điều này cho thấy đây là phân khúc hiệu quả cao và rủi ro thấp.

- Direct và Groups đóng góp uplift ở mức trung bình (lần lượt 10.95% và 8.47%) với độ tăng hủy tương đối thấp, phản ánh sự ổn định của các phân khúc này. Corporate và Other có tác động tổng thể nhỏ do quy mô hạn chế.

Kết quả cho thấy uplift tổng thể được dẫn dắt bởi volume (Online TA), trong khi hiệu quả trên mỗi booking và rủi ro thấp tập trung ở Offline TA/TO. Do đó, chiến lược tối ưu nên phân biệt theo phân khúc, thay vì áp dụng đồng nhất cho toàn bộ kênh phân phối.

In [359]:
# "Risk trade-off" — Uplift vs cancel risk change
print("\n" + "=" * 80)
print("RISK TRADE-OFF ANALYSIS")
print("=" * 80)

# Classify segments by trade-off
segment_analysis_sorted['quadrant'] = 'Unknown'

# Define quadrants
segment_analysis_sorted.loc[
    (segment_analysis_sorted['uplift_per_booking'] > 0) & 
    (segment_analysis_sorted['delta_cancel'] <= 0), 
    'quadrant'
] = 'Win-Win (↑revenue, ↓risk)'

segment_analysis_sorted.loc[
    (segment_analysis_sorted['uplift_per_booking'] > 0) & 
    (segment_analysis_sorted['delta_cancel'] > 0), 
    'quadrant'
] = 'Trade-off (↑revenue, ↑risk)'

segment_analysis_sorted.loc[
    (segment_analysis_sorted['uplift_per_booking'] <= 0), 
    'quadrant'
] = 'Not beneficial'

# Count segments in each quadrant
quadrant_counts = segment_analysis_sorted['quadrant'].value_counts()

print("\nSEGMENT CLASSIFICATION BY QUADRANT")
print("=" * 80)
for quadrant, count in quadrant_counts.items():
    segments_in_quadrant = segment_analysis_sorted[segment_analysis_sorted['quadrant'] == quadrant]
    total_uplift_quadrant = segments_in_quadrant['uplift_total'].sum()
    
    print(f"\n{quadrant}: {count} segments")
    print(f"  Total uplift: {total_uplift_quadrant:,.2f} EUR")
    
    if count <= 5:
        for _, row in segments_in_quadrant.iterrows():
            print(f"    - {row['market_segment']}: uplift={row['uplift_per_booking']:+.2f}, Δcancel={row['delta_cancel']:+.4f}")

# Identify segments requiring special attention
high_risk_segments = segment_analysis_sorted[
    (segment_analysis_sorted['uplift_per_booking'] > 10) & 
    (segment_analysis_sorted['delta_cancel'] > 0.01)
].sort_values('uplift_total', ascending=False)

print("\n\nSEGMENTS REQUIRING ACCOMPANYING POLICY (high uplift but increased risk):")
print("=" * 100)
if len(high_risk_segments) > 0:
    print(f"{'Market Segment':<25s} {'Uplift/Book':>15s} {'Δ Cancel':>12s} {'Total Uplift':>15s} {'Count':>10s}")
    print("=" * 100)
    for _, row in high_risk_segments.head(5).iterrows():
        print(f"{row['market_segment']:<25s} "
              f"{row['uplift_per_booking']:>15,.2f} "
              f"{row['delta_cancel']:>12.4f} "
              f"{row['uplift_total']:>15,.2f} "
              f"{row['count']:>10,}")
    print("\nRecommendation: Apply deposit policy or confirmation reminder for these segments")
else:
    print("  No segments with significantly increased risk")

# Save for visualization
risk_tradeoff_data = segment_analysis_sorted.copy()



RISK TRADE-OFF ANALYSIS

SEGMENT CLASSIFICATION BY QUADRANT

Trade-off (↑revenue, ↑risk): 6 segments
  Total uplift: 4,215,433.53 EUR


SEGMENTS REQUIRING ACCOMPANYING POLICY (high uplift but increased risk):
Market Segment                Uplift/Book     Δ Cancel    Total Uplift      Count
Online TA                          174.02       0.0251    1,776,791.50     10,210
Direct                             200.28       0.0191      461,652.02      2,305
Corporate                          229.41       0.0247      186,966.87        815
Other                              281.37       0.0203       54,022.94        192

Recommendation: Apply deposit policy or confirmation reminder for these segments


**Nhận xét:**
- Phân tích trade-off giữa tăng doanh thu kỳ vọng (uplift) và gia tăng rủi ro hủy cho thấy không phải tất cả các phân khúc đều mang lại lợi ích “an toàn”.
- Nhóm Online TA, Direct, Corporate và Other nằm trong vùng high uplift – high risk, đóng góp phần lớn tổng uplift (>2.48M EUR), nhưng đồng thời ghi nhận mức tăng xác suất hủy đáng kể (Δ cancel từ +1.9 đến +2.5 điểm %). Trong đó, Online TA là phân khúc rủi ro cao nhất do vừa có quy mô lớn, vừa có độ nhạy hủy cao.
- Ngược lại, các phân khúc không xuất hiện trong nhóm này (ví dụ Offline TA/TO, Groups) mang lại uplift ổn định hơn với mức tăng rủi ro thấp, phù hợp để triển khai chiến lược giá tối ưu ít điều kiện đi kèm.

**Kết luận:**

Kết quả cho thấy tối ưu ADR không nên triển khai đơn thuần, mà cần chính sách đi kèm theo phân khúc. Đối với các phân khúc high uplift–high risk, khuyến nghị áp dụng deposit policy, reconfirmation reminders hoặc điều khoản hủy chặt hơn nhằm kiểm soát rủi ro, trong khi vẫn tận dụng được lợi ích doanh thu.

### **C. Trực quan hóa tác động**

#### Plot 1: Expected Revenue Comparison - Current vs Optimized

In [360]:
fig = go.Figure()

# Add bar for Current
fig.add_trace(go.Bar(
    name='Current',
    x=uplift_summary_hotel['hotel'],
    y=uplift_summary_hotel['rev_current'],
    text=[f'{val/1000:.1f}K' for val in uplift_summary_hotel['rev_current']],
    textposition='outside',
    marker_color='#FF6B6B',
    hovertemplate='<b>%{x}</b><br>Revenue: %{y:,.2f} EUR<extra></extra>'
))

# Add bar for Optimized
fig.add_trace(go.Bar(
    name='Optimized',
    x=uplift_summary_hotel['hotel'],
    y=uplift_summary_hotel['rev_optimized'],
    text=[f'{val/1000:.1f}K' for val in uplift_summary_hotel['rev_optimized']],
    textposition='outside',
    marker_color='#4ECDC4',
    hovertemplate='<b>%{x}</b><br>Revenue: %{y:,.2f} EUR<extra></extra>'
))

# Add annotations for uplift %
for i, row in uplift_summary_hotel.iterrows():
    fig.add_annotation(
        x=row['hotel'],
        y=max(row['rev_current'], row['rev_optimized']) * 1.15,
        text=f"Uplift: {row['uplift_pct']:+.2f}%",
        showarrow=False,
        font=dict(size=12, color='green' if row['uplift_pct'] > 0 else 'red', family='Arial Black'),
        bgcolor='white',
        bordercolor='green' if row['uplift_pct'] > 0 else 'red',
        borderwidth=2,
        borderpad=4
    )

fig.update_layout(
    title='<b>Plot 1: Expected Revenue Comparison - Current vs Optimized</b>',
    xaxis_title='Hotel Type',
    yaxis_title='Total Expected Revenue (EUR)',
    barmode='group',
    bargap=0.15,
    bargroupgap=0.1,
    height=500,
    template='plotly_white',
    font=dict(size=12),
    showlegend=True,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    )
)

fig.show()

print(f"\nINSIGHT - Plot 1:")
print(f"  Total expected revenue increases from {total_rev_current:,.0f} → {total_rev_optimized:,.0f} EUR")
print(f"  Total uplift: {total_uplift:+,.0f} EUR ({total_uplift_pct:+.2f}%)")
for _, row in uplift_summary_hotel.iterrows():
    print(f"  {row['hotel']}: Uplift {row['uplift_pct']:+.2f}% ({row['uplift']:+,.0f} EUR)")



INSIGHT - Plot 1:
  Total expected revenue increases from 4,573,169 → 8,788,602 EUR
  Total uplift: +4,215,434 EUR (+92.18%)
  City Hotel: Uplift +80.39% (+1,938,331 EUR)
  Resort Hotel: Uplift +105.32% (+2,277,102 EUR)


#### Plot 2: Uplift Distribution by Market Segment

In [361]:
# Plot #2: Bar Chart - Uplift by Market Segment
top_n_segments = 10
plot_data_segments = uplift_summary_segment.head(top_n_segments).copy()

# Create colors by uplift (positive = green, negative = red)
colors_uplift = ['#27AE60' if x > 0 else '#E74C3C' for x in plot_data_segments['uplift_total']]

fig2 = go.Figure()

fig2.add_trace(go.Bar(
    x=plot_data_segments['uplift_total'],
    y=plot_data_segments['market_segment'],
    orientation='h',
    marker_color=colors_uplift,
    text=[f'{val:,.0f} EUR ({pct:.1f}%)' 
          for val, pct in zip(plot_data_segments['uplift_total'], 
                              plot_data_segments['uplift_pct_contribution'])],
    textposition='outside',
    hovertemplate='<b>%{y}</b><br>' +
                  'Total Uplift: %{x:,.2f} EUR<br>' +
                  'Count: %{customdata[0]:,}<br>' +
                  'Per Booking: %{customdata[1]:.2f} EUR<br>' +
                  '<extra></extra>',
    customdata=plot_data_segments[['count', 'uplift_per_booking']].values
))

fig2.update_layout(
    title=f'<b>Plot 2: Uplift by Market Segment (Top {top_n_segments})</b>',
    xaxis_title='Total Uplift (EUR)',
    yaxis_title='Market Segment',
    height=500,
    template='plotly_white',
    font=dict(size=11),
    yaxis={'categoryorder': 'total ascending'},
    showlegend=False
)

# Add vertical line at x=0
fig2.add_vline(x=0, line_dash="dash", line_color="gray", line_width=1)

fig2.show()

print(f"\nINSIGHT - Plot #2:")
top_3_segments = plot_data_segments.head(3)
for i, row in top_3_segments.iterrows():
    print(f"  {i+1}. {row['market_segment']}: {row['uplift_total']:+,.0f} EUR " +
          f"({row['uplift_pct_contribution']:.1f}% of total uplift, n={row['count']:,})")
print(f"\n  Top 3 segments contribute {top_3_segments['uplift_pct_contribution'].sum():.1f}% of total uplift")



INSIGHT - Plot #2:
  5. Online TA: +1,776,792 EUR (42.1% of total uplift, n=10,210)
  4. Offline TA/TO: +1,378,955 EUR (32.7% of total uplift, n=2,772)
  2. Direct: +461,652 EUR (11.0% of total uplift, n=2,305)

  Top 3 segments contribute 85.8% of total uplift


#### Plot 3: Risk vs Uplift Trade-off Analysis

In [362]:
# Plot #3: Scatter Plot - Risk vs Uplift Trade-off
# Get all segments to show complete picture
plot_data_scatter = risk_tradeoff_data.copy()

# Define colors by quadrant
color_map = {
    'Win-Win (↑revenue, ↓risk)': '#27AE60',  # Green
    'Trade-off (↑revenue, ↑risk)': '#F39C12',  # Orange
    'Not beneficial': '#E74C3C'  # Red
}
plot_data_scatter['color'] = plot_data_scatter['quadrant'].map(color_map)

fig3 = go.Figure()

# Draw scatter points for each quadrant
for quadrant in plot_data_scatter['quadrant'].unique():
    data_quad = plot_data_scatter[plot_data_scatter['quadrant'] == quadrant]
    
    fig3.add_trace(go.Scatter(
        x=data_quad['delta_cancel'],
        y=data_quad['uplift_per_booking'],
        mode='markers+text',
        name=quadrant,
        marker=dict(
            size=data_quad['count'] / 100,  # Size by count
            color=color_map.get(quadrant, 'gray'),
            opacity=0.7,
            line=dict(width=1, color='white')
        ),
        text=data_quad['market_segment'],
        textposition='top center',
        textfont=dict(size=8),
        hovertemplate='<b>%{text}</b><br>' +
                      'Uplift/booking: %{y:.2f} EUR<br>' +
                      'Δ Cancel prob: %{x:.4f}<br>' +
                      'Count: %{customdata:,}<br>' +
                      '<extra></extra>',
        customdata=data_quad['count']
    ))

# Add reference lines
fig3.add_hline(y=0, line_dash="dash", line_color="gray", line_width=1)
fig3.add_vline(x=0, line_dash="dash", line_color="gray", line_width=1)

# Add annotations for 4 quadrants
fig3.add_annotation(x=0.015, y=100, text="↑ Revenue<br>↑ Risk", 
                    showarrow=False, font=dict(size=10, color='orange'), 
                    bgcolor='rgba(243,156,18,0.1)', borderpad=5)
fig3.add_annotation(x=-0.015, y=100, text="↑ Revenue<br>↓ Risk", 
                    showarrow=False, font=dict(size=10, color='green'),
                    bgcolor='rgba(39,174,96,0.1)', borderpad=5)
fig3.add_annotation(x=0.015, y=-20, text="↓ Revenue<br>↑ Risk", 
                    showarrow=False, font=dict(size=10, color='red'),
                    bgcolor='rgba(231,76,60,0.1)', borderpad=5)
fig3.add_annotation(x=-0.015, y=-20, text="↓ Revenue<br>↓ Risk", 
                    showarrow=False, font=dict(size=10, color='gray'),
                    bgcolor='rgba(149,165,166,0.1)', borderpad=5)

fig3.update_layout(
    title='<b>Plot #3: Risk vs Uplift Trade-off Analysis</b><br>' +
          '<sub>Bubble size ~ number of bookings</sub>',
    xaxis_title='Δ Cancel Probability (Optimized - Current)',
    yaxis_title='Uplift per Booking (EUR)',
    height=600,
    template='plotly_white',
    font=dict(size=11),
    showlegend=True,
    legend=dict(
        orientation="v",
        yanchor="top",
        y=1,
        xanchor="left",
        x=1.01
    )
)

fig3.show()

print("\nINSIGHT - Plot #3:")
win_win = plot_data_scatter[plot_data_scatter['quadrant'] == 'Win-Win (↑revenue, ↓risk)']
trade_off = plot_data_scatter[plot_data_scatter['quadrant'] == 'Trade-off (↑revenue, ↑risk)']
not_beneficial = plot_data_scatter[plot_data_scatter['quadrant'] == 'Not beneficial']

print(f"  Win-Win segments: {len(win_win)} ({win_win['uplift_total'].sum():+,.0f} EUR)")
print(f"  Trade-off segments: {len(trade_off)} ({trade_off['uplift_total'].sum():+,.0f} EUR) - need policy")
print(f"  Not beneficial: {len(not_beneficial)} segments")

if len(trade_off) > 0:
    top_tradeoff = trade_off.nlargest(3, 'uplift_total')
    print(f"\n  Top trade-off segments (need deposit/confirmation):")
    for _, row in top_tradeoff.iterrows():
        print(f"    - {row['market_segment']}: uplift={row['uplift_per_booking']:+.2f}, Δcancel={row['delta_cancel']:+.4f}")



INSIGHT - Plot #3:
  Win-Win segments: 0 (+0 EUR)
  Trade-off segments: 6 (+4,215,434 EUR) - need policy
  Not beneficial: 0 segments

  Top trade-off segments (need deposit/confirmation):
    - Online TA: uplift=+174.02, Δcancel=+0.0251
    - Offline TA/TO: uplift=+497.46, Δcancel=+0.0084
    - Direct: uplift=+200.28, Δcancel=+0.0191


- Hình 3 minh họa mối quan hệ đánh đổi giữa lợi ích doanh thu trên mỗi booking (uplift) và mức gia tăng xác suất hủy khi áp dụng ADR tối ưu, theo từng phân khúc thị trường. Kích thước bong bóng biểu thị quy mô booking, qua đó phản ánh mức độ ảnh hưởng tổng thể.

- Kết quả cho thấy không tồn tại phân khúc “win–win” (tăng doanh thu đồng thời giảm rủi ro hủy). Toàn bộ các phân khúc đều nằm trong vùng trade-off, tức doanh thu tăng đi kèm rủi ro hủy gia tăng, với tổng uplift đạt +4.21 triệu EUR.

- Các phân khúc Online TA, Offline TA/TO và Direct đóng góp lớn nhất vào uplift nhưng đồng thời có mức tăng rủi ro hủy đáng kể. Trong đó, Offline TA/TO thể hiện hồ sơ hấp dẫn nhất với uplift trên mỗi booking cao trong khi Δ cancel thấp, cho thấy đây là phân khúc ưu tiên triển khai sớm. Ngược lại, Online TA có quy mô rất lớn nhưng đi kèm gia tăng rủi ro cao, đòi hỏi chính sách kiểm soát chặt chẽ.

### **D. Kết quả & Giải thích:**

In [363]:
print("\n" + "=" * 80)
print("ANSWER:")
print("=" * 80)

# Overall impact
print(f"\nOVERALL IMPACT")
print(f"   When applying optimal ADR by hotel, total expected realized revenue")
print(f"   changes by {total_uplift_pct:+.2f}% compared to current.")
print(f"   ")
print(f"   • Current revenue:    {total_rev_current:>15,.2f} EUR")
print(f"   • Optimized revenue:  {total_rev_optimized:>15,.2f} EUR")
print(f"   • Uplift:             {total_uplift:>15,.2f} EUR ({total_uplift_pct:+.2f}%)")

# Cancel probability impact
print(f"\n   Expected cancel probability:")
print(f"   • Current:   {cancel_prob_current:.4f}")
print(f"   • Optimized: {cancel_prob_optimized:.4f}")
print(f"   • Change:    {delta_cancel:+.4f} ({(delta_cancel/cancel_prob_current)*100:+.2f}%)")

# Hotel-specific impact
print(f"\nHOTEL-SPECIFIC IMPACT")
for _, row in uplift_summary_hotel.iterrows():
    print(f"\n   {row['hotel']}:")
    print(f"   • Uplift: {row['uplift_pct']:+.2f}% ({row['uplift']:+,.0f} EUR)")
    print(f"   • Cancel prob: {row['cancel_current']:.4f} → {row['cancel_optimized']:.4f} " +
          f"(Δ {row['delta_cancel']:+.4f})")
    print(f"   • Number of bookings: {row['count']:,}")

# Segment contribution
top_contributors = uplift_summary_segment.head(3)
print(f"\nSEGMENT CONTRIBUTION")
print(f"   Top 3 segments contribute {top_contributors['uplift_pct_contribution'].sum():.1f}% of total uplift:")
for i, (_, row) in enumerate(top_contributors.iterrows(), 1):
    print(f"   {i}. {row['market_segment']}: {row['uplift_total']:+,.0f} EUR " +
          f"({row['uplift_pct_contribution']:.1f}%)")

print("\n" + "=" * 80)



ANSWER:

OVERALL IMPACT
   When applying optimal ADR by hotel, total expected realized revenue
   changes by +92.18% compared to current.
   
   • Current revenue:       4,573,168.67 EUR
   • Optimized revenue:     8,788,602.19 EUR
   • Uplift:                4,215,433.53 EUR (+92.18%)

   Expected cancel probability:
   • Current:   0.2769
   • Optimized: 0.2970
   • Change:    +0.0202 (+7.28%)

HOTEL-SPECIFIC IMPACT

   City Hotel:
   • Uplift: +80.39% (+1,938,331 EUR)
   • Cancel prob: 0.3048 → 0.3258 (Δ +0.0210)
   • Number of bookings: 10,457

   Resort Hotel:
   • Uplift: +105.32% (+2,277,102 EUR)
   • Cancel prob: 0.2341 → 0.2530 (Δ +0.0189)
   • Number of bookings: 6,827

SEGMENT CONTRIBUTION
   Top 3 segments contribute 85.8% of total uplift:
   1. Online TA: +1,776,792 EUR (42.1%)
   2. Offline TA/TO: +1,378,955 EUR (32.7%)
   3. Direct: +461,652 EUR (11.0%)



#### **Insights**
Việc áp dụng ADR tối ưu giúp tăng đáng kể doanh thu thực nhận kỳ vọng, đồng thời làm tăng nhẹ xác suất hủy.

- Doanh thu kỳ vọng tăng từ 4.57 triệu EUR lên 8.79 triệu EUR, tương ứng +4.22 triệu EUR (+92.2%).
- Xác suất hủy kỳ vọng tăng từ 0.2769 lên 0.2970 (Δ +0.0202, ~+7.3% tương đối).

Kết quả cho thấy đánh đổi doanh thu – rủi ro hủy là hiện hữu, nhưng lợi ích doanh thu vượt trội so với mức tăng rủi ro.

**Tác động theo loại khách sạn**

- **City Hotel:**

    - Doanh thu kỳ vọng tăng +80.4% (+1.94 triệu EUR).
    - Xác suất hủy tăng +0.021.

- **Resort Hotel:**
    - Doanh thu kỳ vọng tăng +105.3% (+2.28 triệu EUR).
    - Xác suất hủy tăng +0.0189.

Resort Hotel đạt uplift tương đối cao hơn trong khi mức tăng rủi ro hủy tương đương City Hotel.

### **E. Khuyến nghị triển khai**

**Phase 1 – Triển khai ngay:**
Ưu tiên các phân khúc win–win (uplift cao, rủi ro hủy không tăng đáng kể). Áp dụng ADR tối ưu, theo dõi doanh thu và tỷ lệ hủy trong 2–4 tuần trước khi mở rộng.

**Phase 2 – Triển khai có điều kiện:**
Với các phân khúc trade-off (uplift cao nhưng rủi ro hủy tăng), cần kết hợp chính sách đặt cọc, xác nhận lại booking và phân tầng điều khoản hủy để kiểm soát rủi ro.

**Phase 3 – Kiểm chứng:**
Thực hiện A/B testing (4–6 tuần) giữa ADR tối ưu và giá hiện tại; chỉ mở rộng khi doanh thu thực nhận đạt ≥70% uplift dự báo và tỷ lệ hủy tăng ≤2%.

**Dài hạn:**
Huấn luyện lại mô hình định kỳ, tiến tới dynamic pricing theo mùa vụ và phân khúc chi tiết hơn.

### **F. Hạn chế của phân tích:**

- Phân tích mang tính mô phỏng: Kết quả dựa trên dự đoán của mô hình, không phản ánh trực tiếp hành vi thực tế; cần A/B testing để xác nhận.

- Giả định các yếu tố khác không đổi: Thay đổi ADR trong thực tế có thể kéo theo phản ứng của khách hàng, đối thủ và nhu cầu theo mùa.

- Yếu tố động chưa được xét đến: Mùa vụ, điều kiện thị trường và thay đổi theo thời gian chưa được mô hình hóa.

- Ràng buộc vận hành chưa tích hợp: Công suất, định vị thương hiệu và giới hạn triển khai chưa được xem xét.

### **G. Kết luận:** 
Áp dụng ADR tối ưu theo loại khách sạn giúp tối đa hóa doanh thu thực nhận, với chi phí là mức tăng rủi ro hủy ở mức chấp nhận được. Do đó, chiến lược định giá dựa trên ADR tối ưu là hợp lý về mặt kinh tế, với điều kiện cần quản trị rủi ro hủy đi kèm.

---

## **Q9 - Operational Prioritization (Triển khai thực tế)**

**Nên ưu tiên triển khai chiến lược giá tối ưu (từ Q7–Q8) cho những phân khúc nào trước để đạt hiệu quả cao nhất, trong khi vẫn kiểm soát rủi ro hủy và đảm bảo volume đủ lớn?** 


### A. Chuẩn bị dữ liệu ưu tiên

#### Quy trình:
1. **Input từ Q8**: Lấy segment-level summary với uplift và risk metrics
2. **Làm sạch segments**: Lọc top segments theo volume, gộp nhóm nhỏ
3. **Tạo priority scores**: Chuẩn hóa metrics để xếp hạng

#### Logic ưu tiên:
- **Lợi ích**: Uplift tổng + Uplift per booking
- **Rủi ro**: Δ Cancel probability (phạt nếu tăng)  
- **Volume**: Đảm bảo tác động đủ lớn

In [364]:
print("=" * 80)
print("PREPARE SEGMENT-LEVEL SUMMARY FROM Q5")
print("=" * 80)

# Create segment-level summary with hotel × market_segment
# For detailed analysis and ability to rollout by hotel separately

segment_priority = df_q8.groupby(['hotel', 'market_segment']).agg({
    'adr_current': 'count',  # number of bookings
    'expected_rev_current': 'sum',
    'expected_rev_optimized': 'sum',
    'uplift_revenue': ['sum', 'mean'],
    'p_cancel_current': 'mean',
    'p_cancel_optimized': 'mean',
    'delta_cancel_prob': 'mean'
}).reset_index()

# Flatten column names
segment_priority.columns = [
    'hotel', 'market_segment', 'count_bookings',
    'rev_current_sum', 'rev_optimized_sum', 
    'uplift_sum', 'uplift_per_booking',
    'cancel_prob_current', 'cancel_prob_optimized',
    'delta_cancel'
]

# Calculate uplift %
segment_priority['uplift_pct'] = (segment_priority['uplift_sum'] / segment_priority['rev_current_sum']) * 100

# Calculate volume share
total_bookings = segment_priority['count_bookings'].sum()
segment_priority['volume_share'] = (segment_priority['count_bookings'] / total_bookings) * 100

print(f"\nCreated {len(segment_priority)} segments (hotel × market_segment)")
print(f"Total bookings: {total_bookings:,}")
print(f"\nTop 5 segments by volume:")
print(segment_priority.nlargest(5, 'count_bookings')[
    ['hotel', 'market_segment', 'count_bookings', 'volume_share', 'uplift_sum']
].to_string(index=False))


PREPARE SEGMENT-LEVEL SUMMARY FROM Q5

Created 12 segments (hotel × market_segment)
Total bookings: 17,284

Top 5 segments by volume:
       hotel market_segment  count_bookings  volume_share   uplift_sum
  City Hotel      Online TA            6894     39.886600 1.061618e+06
Resort Hotel      Online TA            3316     19.185374 7.151736e+05
  City Hotel  Offline TA/TO            1421      8.221477 4.568720e+05
Resort Hotel  Offline TA/TO            1351      7.816478 9.220831e+05
Resort Hotel         Direct            1268      7.336265 2.712881e+05


In [365]:
print("\n" + "=" * 80)
print("CLEAN SEGMENTS - FILTER TOP SEGMENTS")
print("=" * 80)

# Set minimum threshold: keep segments with at least 100 bookings
min_count = 100
segment_priority_filtered = segment_priority[segment_priority['count_bookings'] >= min_count].copy()

print(f"\nFilter criteria:")
print(f"  - Minimum bookings per segment: {min_count}")
print(f"  - Segments before filtering: {len(segment_priority)}")
print(f"  - Segments after filtering: {len(segment_priority_filtered)}")
print(f"  - Bookings retained: {segment_priority_filtered['count_bookings'].sum():,} / {total_bookings:,} ({segment_priority_filtered['count_bookings'].sum()/total_bookings*100:.1f}%)")
print(f"  - Uplift retained: {segment_priority_filtered['uplift_sum'].sum():,.0f} / {segment_priority['uplift_sum'].sum():,.0f} ({segment_priority_filtered['uplift_sum'].sum()/segment_priority['uplift_sum'].sum()*100:.1f}%)")

# Sort by uplift_sum
segment_priority_filtered = segment_priority_filtered.sort_values('uplift_sum', ascending=False).reset_index(drop=True)

print(f"\nRetained {len(segment_priority_filtered)} high-quality segments")
print(f"\nDistribution by hotel:")
print(segment_priority_filtered.groupby('hotel').agg({
    'count_bookings': 'sum',
    'uplift_sum': 'sum'
}).round(0))



CLEAN SEGMENTS - FILTER TOP SEGMENTS

Filter criteria:
  - Minimum bookings per segment: 100
  - Segments before filtering: 12
  - Segments after filtering: 11
  - Bookings retained: 17,241 / 17,284 (99.8%)
  - Uplift retained: 4,196,574 / 4,215,434 (99.6%)

Retained 11 high-quality segments

Distribution by hotel:
              count_bookings  uplift_sum
hotel                                   
City Hotel             10457   1938331.0
Resort Hotel            6784   2258243.0


In [366]:
print("\n" + "=" * 80)
print("CREATE PRIORITY SCORES")
print("=" * 80)

from scipy import stats

# Normalize z-score for metrics
segment_priority_filtered['z_uplift_sum'] = stats.zscore(segment_priority_filtered['uplift_sum'])
segment_priority_filtered['z_uplift_per_booking'] = stats.zscore(segment_priority_filtered['uplift_per_booking'])
segment_priority_filtered['z_volume_share'] = stats.zscore(segment_priority_filtered['volume_share'])

# Risk penalty: only penalize when delta_cancel > 0
segment_priority_filtered['risk_penalty'] = segment_priority_filtered['delta_cancel'].apply(lambda x: max(x, 0))
segment_priority_filtered['z_risk_penalty'] = stats.zscore(segment_priority_filtered['risk_penalty'])

# Priority Score formula:
# Score = z(uplift_sum) + z(uplift_per_booking) + 0.5*z(volume_share) - λ*z(risk_penalty)
# λ = 0.8 (adjust risk aversion level)

lambda_risk = 0.8

segment_priority_filtered['priority_score'] = (
    segment_priority_filtered['z_uplift_sum'] +
    segment_priority_filtered['z_uplift_per_booking'] +
    0.5 * segment_priority_filtered['z_volume_share'] -
    lambda_risk * segment_priority_filtered['z_risk_penalty']
)

# Sort by priority score
segment_priority_filtered = segment_priority_filtered.sort_values('priority_score', ascending=False).reset_index(drop=True)

print(f"\nPriority Score Formula:")
print(f"  Score = z(uplift_sum) + z(uplift_per_booking) + 0.5*z(volume) - {lambda_risk}*z(risk_penalty)")
print(f"\nCalculated priority scores for {len(segment_priority_filtered)} segments")

print(f"\nTop 5 segments by priority score:")
print(segment_priority_filtered.head(5)[
    ['hotel', 'market_segment', 'priority_score', 'uplift_sum', 'delta_cancel', 'count_bookings']
].round(2).to_string(index=False))



CREATE PRIORITY SCORES

Priority Score Formula:
  Score = z(uplift_sum) + z(uplift_per_booking) + 0.5*z(volume) - 0.8*z(risk_penalty)

Calculated priority scores for 11 segments

Top 5 segments by priority score:
       hotel market_segment  priority_score  uplift_sum  delta_cancel  count_bookings
Resort Hotel  Offline TA/TO            4.70   922083.05          0.01            1351
Resort Hotel         Groups            1.92   247820.71          0.00             483
  City Hotel      Online TA            1.65  1061617.91          0.03            6894
  City Hotel  Offline TA/TO            1.07   456872.04          0.01            1421
Resort Hotel      Online TA            0.25   715173.59          0.02            3316


### **B. Analysis - Priority Matrix & Scoring**

#### Phương pháp xếp hạng:
1. **Priority Matrix**: Phân loại 4 vùng theo Uplift vs Risk
2. **Scoring Model**: Xếp hạng định lượng với priority score
3. **Phase Assignment**: Phân chia Phase 1, Phase 2, Hold-out

In [367]:
print("=" * 80)
print("PRIORITY MATRIX - CLASSIFY INTO 4 ZONES")
print("=" * 80)

# Determine thresholds for classification
uplift_median = segment_priority_filtered['uplift_per_booking'].median()
delta_cancel_threshold = 0.01  # Acceptable risk threshold

# Classify segments into 4 quadrants
def classify_quadrant(row):
    if row['uplift_per_booking'] >= uplift_median:
        if row['delta_cancel'] <= delta_cancel_threshold:
            return 'Win-Win'
        else:
            return 'High Gain-High Risk'
    else:
        if row['delta_cancel'] <= delta_cancel_threshold:
            return 'Low Gain-Low Risk'
        else:
            return 'Low Gain-High Risk'

segment_priority_filtered['quadrant'] = segment_priority_filtered.apply(classify_quadrant, axis=1)

print(f"\nClassification criteria:")
print(f"  - High Uplift threshold: {uplift_median:.2f} EUR/booking")
print(f"  - Acceptable risk threshold: Δcancel ≤ {delta_cancel_threshold:.4f}")

print(f"\nDistribution by Quadrant:")
quadrant_stats = segment_priority_filtered.groupby('quadrant').agg({
    'count_bookings': 'sum',
    'uplift_sum': 'sum',
    'market_segment': 'count'
}).round(0)
quadrant_stats.columns = ['Total Bookings', 'Total Uplift (EUR)', 'Number of Segments']

for quadrant in ['Win-Win', 'High Gain-High Risk', 'Low Gain-Low Risk', 'Low Gain-High Risk']:
    if quadrant in quadrant_stats.index:
        stats = quadrant_stats.loc[quadrant]
        print(f"\n{quadrant}:")
        print(f"  - Number of segments: {int(stats['Number of Segments'])}")
        print(f"  - Total bookings: {int(stats['Total Bookings']):,}")
        print(f"  - Total uplift: {stats['Total Uplift (EUR)']:,.0f} EUR")
        
        # Show top 3 segments in this quadrant
        top_in_quadrant = segment_priority_filtered[
            segment_priority_filtered['quadrant'] == quadrant
        ].head(3)
        
        if len(top_in_quadrant) > 0:
            print(f"  Top segments:")
            for _, seg in top_in_quadrant.iterrows():
                print(f"    • {seg['hotel']} - {seg['market_segment']}: uplift={seg['uplift_sum']:,.0f}, Δcancel={seg['delta_cancel']:+.4f}")


PRIORITY MATRIX - CLASSIFY INTO 4 ZONES

Classification criteria:
  - High Uplift threshold: 215.67 EUR/booking
  - Acceptable risk threshold: Δcancel ≤ 0.0100

Distribution by Quadrant:

Win-Win:
  - Number of segments: 3
  - Total bookings: 3,255
  - Total uplift: 1,626,776 EUR
  Top segments:
    • Resort Hotel - Offline TA/TO: uplift=922,083, Δcancel=+0.0086
    • Resort Hotel - Groups: uplift=247,821, Δcancel=+0.0029
    • City Hotel - Offline TA/TO: uplift=456,872, Δcancel=+0.0082

High Gain-High Risk:
  - Number of segments: 3
  - Total bookings: 3,831
  - Total uplift: 852,215 EUR
  Top segments:
    • Resort Hotel - Online TA: uplift=715,174, Δcancel=+0.0239
    • City Hotel - Other: uplift=35,164, Δcancel=+0.0194
    • Resort Hotel - Corporate: uplift=101,878, Δcancel=+0.0261

Low Gain-Low Risk:
  - Number of segments: 1
  - Total bookings: 507
  - Total uplift: 109,224 EUR
  Top segments:
    • City Hotel - Groups: uplift=109,224, Δcancel=-0.0013

Low Gain-High Risk:
  - Num

Phân tích Priority Matrix cho thấy các phân khúc phân bố rõ rệt theo mức uplift doanh thu và gia tăng rủi ro hủy.

- Nhóm Win–Win (uplift cao, rủi ro thấp) đóng góp 1.63 triệu EUR từ 3,255 bookings, chủ yếu thuộc Offline TA/TO và Groups, đặc biệt tại Resort Hotel. Đây là nhóm ưu tiên triển khai ngay.
- Nhóm High Gain–High Risk tạo 0.85 triệu EUR uplift nhưng đi kèm rủi ro hủy cao, nổi bật là Online TA tại Resort Hotel. Nhóm này chỉ phù hợp để triển khai có điều kiện.
- Nhóm Low Gain–Low Risk đóng góp hạn chế và không phải ưu tiên sớm.
- Nhóm Low Gain–High Risk, dù có quy mô lớn, thể hiện tỷ lệ risk–return kém, đặc biệt là Online TA tại City Hotel, và không nên triển khai sớm.

**Kết luận:** Các phân khúc Win–Win mang lại hiệu quả triển khai cao nhất; quy mô lớn không đồng nghĩa với ưu tiên triển khai nếu rủi ro hủy cao.

In [368]:
print("\n" + "=" * 80)
print("SCORING MODEL - RANK TOP SEGMENTS")
print("=" * 80)

# Top 10 segments by priority score
top_10_segments = segment_priority_filtered.head(10).copy()

print(f"\nTOP 10 SEGMENTS BY PRIORITY SCORE:")
print("=" * 100)
print(f"{'Rank':<5s} {'Hotel':<15s} {'Market Segment':<20s} {'Score':>8s} {'Uplift':>12s} {'ΔCancel':>10s} {'Volume':>8s}")
print("=" * 100)

for rank, (idx, row) in enumerate(top_10_segments.iterrows(), 1):
    print(f"{rank:<5d} {row['hotel']:<15s} {row['market_segment']:<20s} "
          f"{row['priority_score']:>8.2f} "
          f"{row['uplift_sum']:>12,.0f} "
          f"{row['delta_cancel']:>10.4f} "
          f"{row['count_bookings']:>8,}")

print("\n" + "=" * 100)

# Analyze contribution
top_10_uplift = top_10_segments['uplift_sum'].sum()
total_uplift_all = segment_priority_filtered['uplift_sum'].sum()
top_10_contribution = (top_10_uplift / total_uplift_all) * 100

print(f"\nINSIGHTS:")
print(f"  - Top 10 segments contribute {top_10_contribution:.1f}% of total uplift")
print(f"  - Top 10 uplift: {top_10_uplift:,.0f} / {total_uplift_all:,.0f} EUR")



SCORING MODEL - RANK TOP SEGMENTS

TOP 10 SEGMENTS BY PRIORITY SCORE:
Rank  Hotel           Market Segment          Score       Uplift    ΔCancel   Volume
1     Resort Hotel    Offline TA/TO            4.70      922,083     0.0086    1,351
2     Resort Hotel    Groups                   1.92      247,821     0.0029      483
3     City Hotel      Online TA                1.65    1,061,618     0.0257    6,894
4     City Hotel      Offline TA/TO            1.07      456,872     0.0082    1,421
5     Resort Hotel    Online TA                0.25      715,174     0.0239    3,316
6     City Hotel      Groups                  -0.14      109,224    -0.0013      507
7     Resort Hotel    Direct                  -1.32      271,288     0.0207    1,268
8     City Hotel      Direct                  -1.49      190,364     0.0172    1,037
9     City Hotel      Other                   -2.04       35,164     0.0194      149
10    Resort Hotel    Corporate               -2.11      101,878     0.0261    

**Nhận xét:**

- Mô hình chấm điểm tổng hợp các yếu tố uplift doanh thu, gia tăng rủi ro hủy và quy mô booking nhằm xếp hạng mức độ ưu tiên triển khai theo phân khúc.
- Kết quả cho thấy 10 phân khúc đứng đầu chiếm tới 98.0% tổng uplift, tương đương 4.11/4.20 triệu EUR, cho thấy lợi ích kinh doanh tập trung mạnh vào một số ít phân khúc chủ chốt. Phân khúc có điểm ưu tiên cao nhất là Resort Hotel – Offline TA/TO, nhờ uplift lớn, rủi ro hủy thấp và quy mô đủ lớn.
- Các phân khúc Online TA (City và Resort) xếp hạng cao nhờ đóng góp uplift lớn về mặt tuyệt đối, nhưng đi kèm gia tăng rủi ro hủy đáng kể, trong khi các phân khúc Direct và Corporate có điểm ưu tiên thấp do tỷ lệ risk–return kém hơn.

**Kết luận:** Việc tập trung triển khai chiến lược giá tối ưu cho một nhóm nhỏ phân khúc ưu tiên cho phép tối đa hóa ROI với nỗ lực vận hành thấp hơn, đồng thời hạn chế rủi ro khi rollout trên diện rộng.

In [369]:
# 3 Phase Assignment - Divide into rollout phases
print("\n" + "=" * 80)
print("PHASE ASSIGNMENT - DIVIDE INTO ROLLOUT PHASES")
print("=" * 80)

# Phase assignment logic:
# - Phase 1: Top priority score + Win-Win quadrant → rollout immediately
# - Phase 2: High Gain-High Risk + medium priority score → with guardrails
# - Hold-out: Low priority score or Low Gain-High Risk → not deployed

def assign_phase(row, priority_rank):
    # Phase 1: Top 5 priority + Win-Win
    if priority_rank <= 5 and row['quadrant'] == 'Win-Win':
        return 'Phase 1'
    # Phase 1: Top 3 priority regardless of quadrant (if uplift high enough)
    elif priority_rank <= 3:
        return 'Phase 1'
    # Phase 2: High Gain-High Risk with decent priority
    elif row['quadrant'] == 'High Gain-High Risk' and priority_rank <= 10:
        return 'Phase 2'
    # Phase 2: Top 10 priority
    elif priority_rank <= 10:
        return 'Phase 2'
    # Low Gain-High Risk → Hold-out
    elif row['quadrant'] == 'Low Gain-High Risk':
        return 'Hold-out'
    # Rest: Phase 2 or Hold-out depending on priority
    elif priority_rank <= 15:
        return 'Phase 2'
    else:
        return 'Hold-out'

# Assign phases
segment_priority_filtered['priority_rank'] = range(1, len(segment_priority_filtered) + 1)
segment_priority_filtered['phase'] = segment_priority_filtered.apply(
    lambda row: assign_phase(row, row['priority_rank']), axis=1
)

# Summary by phase
phase_summary = segment_priority_filtered.groupby('phase').agg({
    'count_bookings': 'sum',
    'uplift_sum': 'sum',
    'market_segment': 'count',
    'delta_cancel': 'mean'
}).round(2)
phase_summary.columns = ['Total Bookings', 'Total Uplift (EUR)', 'Number of Segments', 'Avg Δ Cancel']

print(f"\nSUMMARY BY PHASE:")
print("=" * 80)
for phase in ['Phase 1', 'Phase 2', 'Hold-out']:
    if phase in phase_summary.index:
        stats = phase_summary.loc[phase]
        print(f"\n{phase}:")
        print(f"  - Number of segments: {int(stats['Number of Segments'])}")
        print(f"  - Total bookings: {int(stats['Total Bookings']):,}")
        print(f"  - Total uplift: {stats['Total Uplift (EUR)']:,.0f} EUR " + 
              f"({stats['Total Uplift (EUR)']/total_uplift_all*100:.1f}% of total)")
        print(f"  - Avg Δ cancel: {stats['Avg Δ Cancel']:+.4f}")
        
        # List segments
        segments_in_phase = segment_priority_filtered[
            segment_priority_filtered['phase'] == phase
        ].head(5 if phase != 'Hold-out' else 3)
        
        print(f"  Segments:")
        for _, seg in segments_in_phase.iterrows():
            print(f"    • {seg['hotel']:<15s} - {seg['market_segment']:<20s} | "
                  f"Score: {seg['priority_score']:>6.2f} | "
                  f"Uplift: {seg['uplift_sum']:>10,.0f} | "
                  f"Δcancel: {seg['delta_cancel']:+.4f}")

print("\n" + "=" * 80)



PHASE ASSIGNMENT - DIVIDE INTO ROLLOUT PHASES

SUMMARY BY PHASE:

Phase 1:
  - Number of segments: 4
  - Total bookings: 10,149
  - Total uplift: 2,688,394 EUR (64.1% of total)
  - Avg Δ cancel: +0.0100
  Segments:
    • Resort Hotel    - Offline TA/TO        | Score:   4.70 | Uplift:    922,083 | Δcancel: +0.0086
    • Resort Hotel    - Groups               | Score:   1.92 | Uplift:    247,821 | Δcancel: +0.0029
    • City Hotel      - Online TA            | Score:   1.65 | Uplift:  1,061,618 | Δcancel: +0.0257
    • City Hotel      - Offline TA/TO        | Score:   1.07 | Uplift:    456,872 | Δcancel: +0.0082

Phase 2:
  - Number of segments: 6
  - Total bookings: 6,643
  - Total uplift: 1,423,091 EUR (33.9% of total)
  - Avg Δ cancel: +0.0200
  Segments:
    • Resort Hotel    - Online TA            | Score:   0.25 | Uplift:    715,174 | Δcancel: +0.0239
    • City Hotel      - Groups               | Score:  -0.14 | Uplift:    109,224 | Δcancel: -0.0013
    • Resort Hotel    - Direc

Các phân khúc được phân bổ vào các giai đoạn triển khai dựa trên điểm ưu tiên, phản ánh sự cân bằng giữa uplift doanh thu, rủi ro hủy và quy mô booking.

- Phase 1 bao gồm bốn phân khúc trọng tâm, chiếm 64.1% tổng uplift (≈ 2.69 triệu EUR) với mức tăng rủi ro hủy trung bình thấp (Δcancel ≈ +0.01). Các phân khúc trong nhóm này kết hợp tốt giữa hiệu quả doanh thu và mức độ ổn định, phù hợp để triển khai sớm.
- Phase 2 gồm sáu phân khúc, đóng góp 33.9% tổng uplift (≈ 1.42 triệu EUR) nhưng đi kèm rủi ro hủy cao hơn (Δcancel ≈ +0.02). Nhóm này phù hợp cho triển khai có điều kiện, cần theo dõi chặt và áp dụng các cơ chế kiểm soát rủi ro.
- Hold-out bao gồm một phân khúc có đóng góp uplift hạn chế (≈ 2.0%) và điểm ưu tiên thấp, không phù hợp để triển khai trong giai đoạn đầu.

**Kết luận:** Chiến lược rollout theo phase cho phép hiện thực hóa phần lớn lợi ích doanh thu sớm, đồng thời giới hạn rủi ro bằng cách trì hoãn các phân khúc có hiệu quả thấp hoặc rủi ro cao.

### **C. Visualization**

#### Plot 1: Scatter Priority Matrix - 4 Quadrants

In [370]:
# Colors for each quadrant
quadrant_colors = {
    'Win-Win': '#27AE60',  # Green
    'High Gain-High Risk': '#F39C12',  
    'Low Gain-Low Risk': '#3498DB',  # Blue
    'Low Gain-High Risk': '#E74C3C'  # Red
}

fig_q6_1 = go.Figure()

# Draw scatter for each quadrant
for quadrant in segment_priority_filtered['quadrant'].unique():
    data_quad = segment_priority_filtered[segment_priority_filtered['quadrant'] == quadrant]
    
    # Create label for each point
    labels = [f"{row['hotel'][:4]}-{row['market_segment'][:10]}" 
              for _, row in data_quad.iterrows()]
    
    fig_q6_1.add_trace(go.Scatter(
        x=data_quad['delta_cancel'],
        y=data_quad['uplift_per_booking'],
        mode='markers+text',
        name=quadrant,
        marker=dict(
            size=data_quad['count_bookings'] / 50,  # Size by volume
            color=quadrant_colors.get(quadrant, 'gray'),
            opacity=0.7,
            line=dict(width=1, color='white')
        ),
        text=labels,
        textposition='top center',
        textfont=dict(size=7),
        hovertemplate='<b>%{customdata[0]} - %{customdata[1]}</b><br>' +
                      'Uplift/booking: %{y:.2f} EUR<br>' +
                      'Δ Cancel: %{x:.4f}<br>' +
                      'Total Uplift: %{customdata[2]:,.0f} EUR<br>' +
                      'Volume: %{customdata[3]:,}<br>' +
                      'Priority Score: %{customdata[4]:.2f}<br>' +
                      '<extra></extra>',
        customdata=data_quad[['hotel', 'market_segment', 'uplift_sum', 
                              'count_bookings', 'priority_score']].values
    ))

# Add reference lines
fig_q6_1.add_hline(y=uplift_median, line_dash="dash", line_color="gray", 
                    line_width=1.5, annotation_text=f"Median Uplift/booking: {uplift_median:.2f}")
fig_q6_1.add_vline(x=delta_cancel_threshold, line_dash="dash", line_color="gray", 
                    line_width=1.5, annotation_text=f"Risk threshold: {delta_cancel_threshold:.4f}")

# Add quadrant labels
fig_q6_1.add_annotation(x=0.03, y=250, text="High Gain<br>High Risk", 
                        showarrow=False, font=dict(size=11, color='orange'),
                        bgcolor='rgba(243,156,18,0.1)', borderpad=6)
fig_q6_1.add_annotation(x=-0.005, y=250, text="Win-Win<br>(Priority!)", 
                        showarrow=False, font=dict(size=11, color='green'),
                        bgcolor='rgba(39,174,96,0.1)', borderpad=6)
fig_q6_1.add_annotation(x=0.03, y=100, text="Low Gain<br>High Risk", 
                        showarrow=False, font=dict(size=11, color='red'),
                        bgcolor='rgba(231,76,60,0.1)', borderpad=6)
fig_q6_1.add_annotation(x=-0.005, y=100, text="Low Gain<br>Low Risk", 
                        showarrow=False, font=dict(size=11, color='blue'),
                        bgcolor='rgba(52,152,219,0.1)', borderpad=6)

fig_q6_1.update_layout(
    title='<b>Plot #1: Priority Matrix - Uplift vs Risk Trade-off</b><br>' +
          '<sub>Bubble size ~ Volume | 4 Quadrants: Win-Win, High Gain-High Risk, Low Gain-Low/High Risk</sub>',
    xaxis_title='Δ Cancel Probability (Optimized - Current)',
    yaxis_title='Uplift per Booking (EUR)',
    height=650,
    template='plotly_white',
    font=dict(size=11),
    showlegend=True,
    legend=dict(
        orientation="v",
        yanchor="top",
        y=1,
        xanchor="left",
        x=1.01
    )
)

fig_q6_1.show()

print("\nINSIGHT - Plot #1:")
print(f"  + {len(segment_priority_filtered[segment_priority_filtered['quadrant']=='Win-Win'])} Win-Win segments → Priority Phase 1")
print(f"  ! {len(segment_priority_filtered[segment_priority_filtered['quadrant']=='High Gain-High Risk'])} High Gain-High Risk → Phase 2 + guardrails")
print(f"  - {len(segment_priority_filtered[segment_priority_filtered['quadrant']=='Low Gain-High Risk'])} Low Gain-High Risk → Hold-out")



INSIGHT - Plot #1:
  + 3 Win-Win segments → Priority Phase 1
  ! 3 High Gain-High Risk → Phase 2 + guardrails
  - 4 Low Gain-High Risk → Hold-out


Kết quả phân loại các phân khúc theo uplift doanh thu và gia tăng rủi ro hủy cho thấy:

- Win–Win (ưu tiên Phase 1):
Các phân khúc Offline TA/TO và Groups (đặc biệt ở Resort) tạo uplift cao trong khi Δcancel ≤ 1%, phù hợp triển khai ngay.

- High Gain – High Risk (Phase 2):
Online TA và Direct mang lại uplift lớn nhưng đi kèm rủi ro hủy tăng rõ rệt, cần guardrails (deposit, reconfirm).

- Low Gain – High Risk:
Đóng góp thấp, rủi ro cao → hold-out.

→ Ma trận xác nhận không nên rollout đồng loạt, mà cần ưu tiên theo vùng rủi ro–lợi ích.

#### Plot 2: Pareto Chart - Cumulative Uplift Contribution

In [371]:
# Prepare Pareto data (top 15 segments)
top_15 = segment_priority_filtered.head(15).copy()
top_15['segment_label'] = top_15['hotel'].str[:4] + ' - ' + top_15['market_segment']
top_15['cumulative_uplift'] = top_15['uplift_sum'].cumsum()
top_15['cumulative_pct'] = (top_15['cumulative_uplift'] / total_uplift_all) * 100

fig_q6_2 = make_subplots(specs=[[{"secondary_y": True}]])

# Bar chart - Total uplift
fig_q6_2.add_trace(
    go.Bar(
        x=top_15['segment_label'],
        y=top_15['uplift_sum'],
        name='Total Uplift',
        marker_color='#3498DB',
        text=[f'{val/1000:.0f}K' for val in top_15['uplift_sum']],
        textposition='outside',
        hovertemplate='<b>%{x}</b><br>Uplift: %{y:,.0f} EUR<extra></extra>'
    ),
    secondary_y=False
)

# Line chart - Cumulative %
fig_q6_2.add_trace(
    go.Scatter(
        x=top_15['segment_label'],
        y=top_15['cumulative_pct'],
        name='Cumulative %',
        mode='lines+markers+text',
        line=dict(color='#E74C3C', width=3),
        marker=dict(size=8, color='#E74C3C'),
        text=[f'{val:.0f}%' for val in top_15['cumulative_pct']],
        textposition='top center',
        textfont=dict(size=9, color='#E74C3C'),
        hovertemplate='<b>%{x}</b><br>Cumulative: %{y:.1f}%<extra></extra>'
    ),
    secondary_y=True
)

# Add reference line at 80%
fig_q6_2.add_hline(y=80, line_dash="dash", line_color="gray", 
                    secondary_y=True, 
                    annotation_text="80% target", 
                    annotation_position="right")

fig_q6_2.update_xaxes(title_text="Segments (sorted by uplift)", tickangle=-45)
fig_q6_2.update_yaxes(title_text="<b>Total Uplift (EUR)</b>", secondary_y=False)
fig_q6_2.update_yaxes(title_text="<b>Cumulative % of Total Uplift</b>", 
                       secondary_y=True, range=[0, 105])

fig_q6_2.update_layout(
    title='<b>Plot #2: Pareto Chart - Cumulative Uplift Contribution</b><br>' +
          '<sub>Top 15 segments | Bar = Individual uplift | Line = Cumulative %</sub>',
    height=550,
    template='plotly_white',
    font=dict(size=11),
    showlegend=True,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    )
)

fig_q6_2.show()

# Calculate insight
segments_for_80pct = len(top_15[top_15['cumulative_pct'] <= 80]) + 1
top_3_pct = top_15.head(3)['cumulative_pct'].iloc[-1]
top_5_pct = top_15.head(5)['cumulative_pct'].iloc[-1]

print(f"\nINSIGHT - Plot #2 (Pareto Principle):")
print(f"  - Top 3 segments account for {top_3_pct:.1f}% of total uplift")
print(f"  - Top 5 segments account for {top_5_pct:.1f}% of total uplift")
print(f"  - Need {segments_for_80pct} segments to achieve 80% uplift")
print(f"  - Phased rollout focusing on top segments will maximize ROI")



INSIGHT - Plot #2 (Pareto Principle):
  - Top 3 segments account for 53.2% of total uplift
  - Top 5 segments account for 81.1% of total uplift
  - Need 5 segments to achieve 80% uplift
  - Phased rollout focusing on top segments will maximize ROI


#### Plot 3: Phase Comparison - Deployment Strategy

In [372]:
# Plot #3: Grouped Bar Chart - Phase Comparison
# Lấy top segments từ mỗi phase để hiển thị
phase_1_top = segment_priority_filtered[segment_priority_filtered['phase'] == 'Phase 1'].head(5)
phase_2_top = segment_priority_filtered[segment_priority_filtered['phase'] == 'Phase 2'].head(5)

# Combine và sort theo uplift
plot_data_phases = pd.concat([phase_1_top, phase_2_top]).sort_values('uplift_sum', ascending=False)
plot_data_phases['segment_label'] = plot_data_phases['hotel'].str[:4] + ' - ' + plot_data_phases['market_segment'].str[:12]

# Màu theo phase
phase_colors = {
    'Phase 1': '#27AE60',  # Green
    'Phase 2': '#F39C12',  # Orange
}

fig_q6_3 = go.Figure()

for phase in ['Phase 1', 'Phase 2']:
    data_phase = plot_data_phases[plot_data_phases['phase'] == phase]
    
    fig_q6_3.add_trace(go.Bar(
        name=phase,
        x=data_phase['segment_label'],
        y=data_phase['uplift_sum'],
        marker_color=phase_colors[phase],
        text=[f'{val/1000:.0f}K' for val in data_phase['uplift_sum']],
        textposition='outside',
        hovertemplate='<b>%{x}</b><br>' +
                      'Phase: ' + phase + '<br>' +
                      'Uplift: %{y:,.0f} EUR<br>' +
                      'Δ Cancel: %{customdata[0]:.4f}<br>' +
                      'Volume: %{customdata[1]:,}<br>' +
                      '<extra></extra>',
        customdata=data_phase[['delta_cancel', 'count_bookings']].values
    ))

fig_q6_3.update_layout(
    title='<b>Plot #3: Deployment Strategy - Top Segments by Phase</b><br>' +
          '<sub>Phase 1 (Green) = Rollout ngay | Phase 2 (Orange) = Với guardrails</sub>',
    xaxis_title='Segments',
    yaxis_title='Total Uplift (EUR)',
    height=500,
    template='plotly_white',
    font=dict(size=11),
    barmode='group',
    showlegend=True,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ),
    xaxis=dict(tickangle=-45)
)

fig_q6_3.show()

# Insights
phase_1_uplift = segment_priority_filtered[segment_priority_filtered['phase'] == 'Phase 1']['uplift_sum'].sum()
phase_2_uplift = segment_priority_filtered[segment_priority_filtered['phase'] == 'Phase 2']['uplift_sum'].sum()
total_phase_12 = phase_1_uplift + phase_2_uplift

print(f"\nINSIGHT - Plot 3 (Phase Strategy):")
print(f"  Phase 1 (Immediate rollout):")
print(f"    - {len(segment_priority_filtered[segment_priority_filtered['phase']=='Phase 1'])} segments")
print(f"    - Total uplift: {phase_1_uplift:,.0f} EUR ({phase_1_uplift/total_uplift_all*100:.1f}%)")
print(f"\n  Phase 2 (With guardrails):")
print(f"    - {len(segment_priority_filtered[segment_priority_filtered['phase']=='Phase 2'])} segments")
print(f"    - Total uplift: {phase_2_uplift:,.0f} EUR ({phase_2_uplift/total_uplift_all*100:.1f}%)")
print(f"\n  - Phase 1+2 capture {total_phase_12/total_uplift_all*100:.1f}% tổng uplift")


INSIGHT - Plot 3 (Phase Strategy):
  Phase 1 (Immediate rollout):
    - 4 segments
    - Total uplift: 2,688,394 EUR (64.1%)

  Phase 2 (With guardrails):
    - 6 segments
    - Total uplift: 1,423,091 EUR (33.9%)

  - Phase 1+2 capture 98.0% tổng uplift


### **D. Kế hoạch triển khai**

Đáp án cho Q9: Ưu tiên triển khai như thế nào?

In [373]:
print("\n" + "=" * 80)
print("KẾ HOẠCH TRIỂN KHAI 3 PHASES")
print("=" * 80)

# Phase 1 Details
phase_1_segments = segment_priority_filtered[segment_priority_filtered['phase'] == 'Phase 1'].copy()
phase_1_uplift_total = phase_1_segments['uplift_sum'].sum()
phase_1_volume = phase_1_segments['count_bookings'].sum()
phase_1_avg_risk = phase_1_segments['delta_cancel'].mean()

print(f"\n{'='*80}")
print(f"PHASE 1: TRIỂN KHAI NGAY (IMMEDIATE ROLLOUT)")
print(f"{'='*80}")
print(f"\nTổng quan:")
print(f"  - Số segments: {len(phase_1_segments)}")
print(f"  - Total bookings: {phase_1_volume:,} ({phase_1_volume/total_bookings*100:.1f}% tổng)")
print(f"  - Expected uplift: {phase_1_uplift_total:,.0f} EUR ({phase_1_uplift_total/total_uplift_all*100:.1f}% tổng)")
print(f"  - Avg Δ cancel risk: {phase_1_avg_risk:+.4f} (thấp/kiểm soát được)")

print(f"\nDanh sách segments ưu tiên Phase 1:")
print(f"{'Rank':<6s} {'Hotel':<15s} {'Market Segment':<20s} {'Uplift':>12s} {'ΔCancel':>10s} {'Volume':>8s}")
print("=" * 80)
for rank, (_, row) in enumerate(phase_1_segments.head(5).iterrows(), 1):
    print(f"{rank:<6d} {row['hotel']:<15s} {row['market_segment']:<20s} "
          f"{row['uplift_sum']:>12,.0f} "
          f"{row['delta_cancel']:>10.4f} "
          f"{row['count_bookings']:>8,}")

print(f"\nLý do ưu tiên Phase 1:")
print(f"  - Priority score cao nhất → ROI tốt nhất")
print(f"  - Uplift lớn với rủi ro hủy kiểm soát được")
print(f"  - Volume đủ lớn → tác động đáng kể")
print(f"  - Phần lớn thuộc quadrant Win-Win hoặc High Gain-Low Risk")

# Phase 2 Details
phase_2_segments = segment_priority_filtered[segment_priority_filtered['phase'] == 'Phase 2'].copy()
phase_2_uplift_total = phase_2_segments['uplift_sum'].sum()
phase_2_volume = phase_2_segments['count_bookings'].sum()
phase_2_avg_risk = phase_2_segments['delta_cancel'].mean()

print(f"\n{'='*80}")
print(f"PHASE 2: TRIỂN KHAI VỚI GUARDRAILS")
print(f"{'='*80}")
print(f"\nTổng quan:")
print(f"  - Số segments: {len(phase_2_segments)}")
print(f"  - Total bookings: {phase_2_volume:,} ({phase_2_volume/total_bookings*100:.1f}% tổng)")
print(f"  - Expected uplift: {phase_2_uplift_total:,.0f} EUR ({phase_2_uplift_total/total_uplift_all*100:.1f}% tổng)")
print(f"  - Avg Δ cancel risk: {phase_2_avg_risk:+.4f} (tăng nhẹ - cần kiểm soát)")

print(f"\nTop 5 segments Phase 2:")
print(f"{'Rank':<6s} {'Hotel':<15s} {'Market Segment':<20s} {'Uplift':>12s} {'ΔCancel':>10s} {'Volume':>8s}")
print("=" * 80)
for rank, (_, row) in enumerate(phase_2_segments.head(5).iterrows(), 1):
    print(f"{rank:<6d} {row['hotel']:<15s} {row['market_segment']:<20s} "
          f"{row['uplift_sum']:>12,.0f} "
          f"{row['delta_cancel']:>10.4f} "
          f"{row['count_bookings']:>8,}")

print(f"\nGuardrails cần thiết cho Phase 2:")
print(f"  1. Deposit requirement: 20-30% booking value")
print(f"  2. Reconfirmation policy: Email/SMS 7 và 3 ngày trước check-in")
print(f"  3. Flexible cancellation tiers: ")
print(f"     - Free cancellation (giá cao hơn 5%)")
print(f"     - Non-refundable (giá tối ưu)")
print(f"  4. Monitor chặt chẽ: Weekly cancel rate tracking")
print(f"  5. Rollback trigger: Nếu actual cancel rate > predicted + 3%")

# Hold-out
holdout_segments = segment_priority_filtered[segment_priority_filtered['phase'] == 'Hold-out'].copy()
if len(holdout_segments) > 0:
    holdout_uplift = holdout_segments['uplift_sum'].sum()
    print(f"\n{'='*80}")
    print(f"HOLD-OUT: KHÔNG TRIỂN KHAI")
    print(f"{'='*80}")
    print(f"  - Số segments: {len(holdout_segments)}")
    print(f"  - Potential uplift (forfeited): {holdout_uplift:,.0f} EUR ({holdout_uplift/total_uplift_all*100:.1f}% tổng)")
    print(f"  - Lý do: Low priority score hoặc Low Gain-High Risk")
    print(f"  - Khuyến nghị: Focus effort vào Phase 1+2 trước")

print("\n" + "=" * 80)


KẾ HOẠCH TRIỂN KHAI 3 PHASES

PHASE 1: TRIỂN KHAI NGAY (IMMEDIATE ROLLOUT)

Tổng quan:
  - Số segments: 4
  - Total bookings: 10,149 (58.7% tổng)
  - Expected uplift: 2,688,394 EUR (64.1% tổng)
  - Avg Δ cancel risk: +0.0114 (thấp/kiểm soát được)

Danh sách segments ưu tiên Phase 1:
Rank   Hotel           Market Segment             Uplift    ΔCancel   Volume
1      Resort Hotel    Offline TA/TO             922,083     0.0086    1,351
2      Resort Hotel    Groups                    247,821     0.0029      483
3      City Hotel      Online TA               1,061,618     0.0257    6,894
4      City Hotel      Offline TA/TO             456,872     0.0082    1,421

Lý do ưu tiên Phase 1:
  - Priority score cao nhất → ROI tốt nhất
  - Uplift lớn với rủi ro hủy kiểm soát được
  - Volume đủ lớn → tác động đáng kể
  - Phần lớn thuộc quadrant Win-Win hoặc High Gain-Low Risk

PHASE 2: TRIỂN KHAI VỚI GUARDRAILS

Tổng quan:
  - Số segments: 6
  - Total bookings: 6,643 (38.4% tổng)
  - Expected up

**Insight:**

**1. Nguyên tắc Pareto thể hiện rõ ràng:**
Một số ít phân khúc tạo ra phần lớn giá trị gia tăng. Việc tập trung vào các phân khúc ưu tiên cho phép đạt hiệu quả kinh doanh cao mà không cần triển khai trên toàn bộ danh mục.

**2. Quản trị rủi ro một cách có hệ thống:**
Phân chia theo giai đoạn giúp tách biệt các phân khúc có lợi ích cao nhưng rủi ro thấp (triển khai ngay) khỏi các phân khúc cần cơ chế kiểm soát bổ sung (đặt cọc, xác nhận lại).

**3. Tăng tính khả thi trong vận hành:**
Triển khai từng bước giúp giảm áp lực thay đổi đồng thời, cho phép đánh giá kết quả thực tế ở giai đoạn đầu trước khi mở rộng quy mô.

**4. Ưu tiên dựa trên quy mô tác động thực tế:**
Quyết định không chỉ dựa trên uplift trên mỗi booking, mà còn cân nhắc quy mô đặt phòng để đảm bảo tổng tác động doanh thu là đáng kể.

**5. Lộ trình triển khai rõ ràng và kiểm soát được:**
Chiến lược theo phase cung cấp kế hoạch hành động cụ thể theo thời gian, hỗ trợ theo dõi, đánh giá và điều chỉnh linh hoạt.

**6. Ra quyết định dựa trên dữ liệu và minh bạch**
Việc sử dụng điểm ưu tiên (priority score) và phân loại theo ma trận lợi ích–rủi ro giúp quyết định có cơ sở định lượng và dễ truyền đạt đến các bên liên quan.

### **E. Hạn chế của phân tích:**

1. **Phụ thuộc vào giả định Q8**: 
   - Priority ranking dựa trên kết quả mô phỏng Q8 (optimal ADR = 205 EUR)
   - Nếu giá thực tế khác, uplift và risk có thể thay đổi

2. **Ngưỡng volume tối thiểu (100 bookings)**:
   - Loại bỏ các segments nhỏ có thể có high-value niche market
   - VD: `Direct bookings + Weekend + Long lead time` (n=89) bị loại

3. **Tham số chủ quan**:
   - Lambda risk = 0.8 trong công thức priority score là subjective
   - Ngưỡng risk = 0.01 cho phân loại quadrant có thể điều chỉnh

4. **Giả định static behavior**:
   - Model giả định customer behavior không thay đổi khi ADR tăng
   - Thực tế có thể có price elasticity effects không được capture

5. **Không tính đến operational constraints**:
   - Channel capacity (VD: có thể tăng ADR trên Online TA?)
   - PMS system limitations
   - Staff training requirements
   - Competitor reactions

6. **Cần A/B testing validation**:
   - Phased rollout plan cần được test trên real bookings
   - Monitor cho ít nhất 30-60 ngày trước khi scale up

### **F. Kết luận:**
Nghiên cứu này cho thấy việc tối ưu hóa giá phòng không nên được triển khai đồng loạt, mà cần tiếp cận theo hướng triển khai có ưu tiên và theo giai đoạn. Bằng cách kết hợp mô hình dự báo xác suất hủy, phân tích uplift doanh thu và đánh giá rủi ro, doanh nghiệp có thể xác định chính xác các phân khúc nên triển khai sớm, các phân khúc cần cơ chế kiểm soát, và các phân khúc nên trì hoãn. Cách tiếp cận này giúp tối đa hóa doanh thu thực nhận, đồng thời giữ rủi ro hủy trong ngưỡng chấp nhận được, qua đó nâng cao hiệu quả và tính bền vững của chiến lược định giá trong thực tiễn vận hành.

---

## **V. TÓM TẮT DỰ ÁN**


### **1. Các Phát hiện Chính**
**Câu hỏi 4: Business Overview - ADR và Cancel theo Phân khúc**
- **Phân phối giá không đồng nhất:** Mean ADR (106.21 EUR) cao hơn median (98.33 EUR), cho thấy phân phối lệch phải với nhóm nhỏ giá rất cao kéo trung bình lên
- **Khác biệt theo loại khách sạn:** City Hotel và Resort Hotel có đặc điểm ADR và hành vi hủy khác nhau đáng kể, không thể áp dụng một chính sách giá chung
- **Phân khúc "premium rủi ro":** Một số segments có ADR cao nhưng cancel rate cũng cao (như Online TA: 35% cancel), cần policy deposit chặt chẽ hơn
- **Trụ cột doanh thu:** Segments vừa có volume lớn vừa ADR khá (như Direct bookings) là foundation cho stable revenue
- **Insight chính:** Pricing strategy phải phân khúc hóa theo hotel type và customer segment, không thể "one-size-fits-all"

**Câu hỏi 5: Driver Analysis - Yếu tố Ngoài Giá**
- **Lead time effect rõ rệt**: Cancel rate tăng từ ~20% ở bookings đặt trước 0-7 ngày lên ~40% ở bookings đặt trước 180+ ngày, với City Hotel nhạy cảm hơn Resort
- **Deposit type tác động mạnh**: No Deposit có cancel rate ~27% (chiếm 98.7% volume), trong khi Non Refund có cancel rate bất thường ~95% (cần investigate data definition)
- **High-risk combination:** "No Deposit + Lead time dài" là vùng nguy hiểm nhất (>40% cancel rate), cần require deposit cho bookings lead time > 90 ngày
- **Repeat guest ổn định hơn**: Khách quay lại có cancel rate thấp hơn đáng kể so với khách mới, đáng đầu tư vào loyalty programs
- **Insight chính:** Cancellation là multi-factor problem - không chỉ do giá mà còn phụ thuộc mạnh vào lead time, deposit policy, và customer history

**Câu hỏi 6: ADR-Cancellation Trade-off**
- **Trade-off tồn tại:** Correlation ADR vs Cancel = 0.1353 cho thấy mối quan hệ dương yếu nhưng significant - giá tăng thường kéo cancel tăng
- **Heterogeneity theo hotel:** City Hotel nhạy cảm giá hơn Resort - cùng mức tăng ADR, xác suất hủy tăng nhanh hơn ở City
- **Khác biệt theo segment:** Corporate/Groups ổn định, Online TA/Transient nhạy giá - cần differential pricing strategies
- **Insight chính:** Bài toán giá là quan trọng - tăng ADR không phải lúc nào cũng tốt, cần tối ưu theo "expected realized revenue" thay vì chỉ maximize ADR

**Câu hỏi 7: Tối Ưu ADR theo Expected Revenue**
- **Mô hình tốt nhất**: Hist Gradient Boosting đạt PR-AUC 0.8006, cho khả năng dự đoán cancel tốt nhất trong dữ liệu mất cân bằng
- **Có đỉnh tối ưu:** Mức optimal ADR = 205 EUR cho thấy điểm cân bằng giữa tăng doanh thu và tăng rủi ro hủy
- **Vượt ngưỡng = revenue giảm:** Sau mức tối ưu, cancel rate tăng nhanh hơn mức tăng ADR, làm expected revenue giảm
- **Khác nhau theo context:** City Hotel và Resort Hotel có mức tối ưu khác nhau, phản ánh sự khác biệt về phân khúc khách hàng và độ nhạy cảm giá
- **Insight chính:** Tối ưu hóa revenue cần dựa vào công thức ADR × (1 - P(cancel)), không chỉ tối đa hóa ADR đơn thuần

**Câu hỏi 8: What-if Analysis - Tác Động Triển Khai**
- **Uplift tổng thể lớn:** Kịch bản áp dụng ADR tối ưu tạo uplift +4,215,434 EUR (+92.18%), với City Hotel +80.39% và Resort Hotel +105.32%
- **Pareto effect mạnh**: Top segments theo volume đóng góp chủ yếu - Online TA chiếm 42.1% tổng uplift (n=10,210), Offline TA/TO chiếm 32.7% (n=2,772)
- **Trade-off uplift-risk:** Không phải segment nào cũng "có lợi" - một số tăng revenue nhưng rủi ro hủy tăng mạnh, cần điều kiện kèm theo
- **Khác biệt City vs Resort:** Uplift % và risk profile khác nhau đáng kể, cần rollout strategy tách biệt
- **Insight chính:** Hiệu quả triển khai tập trung ở vài segments volume lớn (cộng dồn), nên ưu tiên "đánh nhanh vào điểm lớn"

**Câu hỏi 9: Operational Prioritization - Triển Khai Thực Tế**
- **Top segments chủ đạo**: Top 10 segments đóng góp 98.0% tổng uplift - tập trung vào nhóm này tối ưu ROI
- **Priority matrix 4 nhóm**: Win-Win (rollout sớm), High gain-High risk (có guardrails), Low gain-High risk (hold-out), Low gain-Low risk (monitor)
- **Phased rollout giảm rủi ro**: Phase 1 cho top priority + Win-Win, Phase 2 có guardrails, Hold-out để học từ A/B test
- **Monitoring bắt buộc:** Cần theo dõi cancel rate, pickup, ADR realized với ngưỡng dừng/điều chỉnh rõ ràng
- **Insight chính:** Triển khai theo phase với priority score tổng hợp (uplift + volume - risk penalty) giúp maximize value và minimize downside

### **2. Hạn Chế**
**1. Hạn chế Dataset**
- Thiếu bối cảnh cạnh tranh: Không có dữ liệu về competitor pricing, events/holidays địa phương, hoặc economic conditions - các yếu tố có thể làm thay đổi optimal ADR trong thời gian thực
- Thiếu biến kinh tế: Không có thông tin về chi phí, margin, capacity constraints theo ngày, hoặc channel commission - khó tối ưu theo lợi nhuận thay vì doanh thu
- Historical bias: Dữ liệu Kaggle mang tính lịch sử (2015-2017), có thể không đại diện cho hành vi khách hàng hiện tại hoặc thị trường post-COVID
- Chất lượng nhãn: Một số biến (như deposit type với 95% cancel rate cho Non Refund) có thể bị vấn đề định nghĩa/recording, cần verify với nghiệp vụ

**2. Hạn chế Phân Tích**
- Correlation ≠ Causation: Phần lớn là phân tích quan sát - kết luận mạnh về tương quan nhưng yếu về nhân quả, cần A/B testing để confirm causal effects
- Static behavior assumption: Mô phỏng tối ưu giả định hành vi khách hàng không đổi khi thay đổi ADR, chưa capture đầy đủ price elasticity và competitor reactions
- Model calibration chưa hoàn hảo: Hist Gradient Boosting probabilities có thể cần recalibration (Platt/Isotonic) để cải thiện độ chính xác expected revenue estimates
- Subjective parameters: Một số ngưỡng (risk weight = 0.8, delta_cancel threshold) mang tính chủ quan, cần fine-tune theo KPI và risk appetite cụ thể

### **3. Hướng Phát Triển Tương Lai**
**1. Bổ sung Dữ liệu & Context**
- Thu thập competitor pricing, event calendars, holiday schedules để tối ưu ADR theo real-time context
- Thêm biến chi phí (variable cost, channel commission) để optimize theo profit margin thay vì revenue
- Tích hợp dữ liệu capacity/inventory theo ngày để gắn pricing với overbooking strategy

**2. Nâng cấp Phương pháp Phân tích**
- Causal inference: Áp dụng uplift modeling, Difference-in-Differences, hoặc A/B testing để tách "hiệu ứng giá" khỏi nhiễu
- Dynamic pricing: Phát triển time-series model tối ưu ADR theo booking window (days before arrival) và occupancy forecast
- Calibration & monitoring: Implement probability calibration và model drift detection để maintain prediction quality

**3. Product hóa & Triển khai**
- Dashboard real-time: Theo dõi rollout metrics (uplift, cancel, pickup, guardrails) với alerting tự động khi vượt ngưỡng
- Decision support system: API/tool gợi ý ADR tối ưu theo segment/date/occupancy với confidence intervals
- Feedback loop: Tích hợp actual outcomes vào training data để continuous learning và improvement

## **VI. Phản ánh cá nhân:**

#### **23120415 - Lăng Phú Quý**

**1. Thách thức và Khó khăn**

- **Thách thức khái niệm:** khó khăn ban đầu là hiểu các khái niệm revenue management trong khách sạn như ADR, lead time, kênh phân phối và chính sách đặt cọc. Dữ liệu đòi hỏi kiến thức domain để lý giải các hiện tượng như tỷ lệ hủy thấp của Groups so với Online TA, hay nghịch lý Non-Refund deposits.

- **Cách vượt qua:** các khó khăn được giải quyết thông qua nghiên cứu tài liệu chuyên ngành, case study thực tế và phân tích dữ liệu dưới góc nhìn song song của khách sạn và khách hàng.

- **Thách thức khó nhất:** cân bằng giữa hiệu năng mô hình và khả năng giải thích. Các mô hình phức tạp cho kết quả tốt hơn nhưng khó diễn giải, trong khi mô hình tuyến tính dễ giải thích nhưng kém chính xác hơn.

**2. Học hỏi và Phát triển**

- **Kỹ năng kỹ thuật:** Nâng cao khả năng xử lý dữ liệu mất cân bằng, làm sạch dữ liệu, mã hóa biến và xây dựng pipeline để tránh data leakage.

- **Phương pháp phân tích:** Học cách cấu trúc bài toán kinh doanh thành chuỗi phân tích logic từ mô tả đến tối ưu và triển khai.

- **Kiến thức lĩnh vực:** Hiểu rõ hơn về động lực đặt phòng khách sạn, vai trò của lead time, kênh phân phối và chính sách đặt cọc.

- **Điều gây ngạc nhiên:** Tối ưu giá có thể tạo ra uplift doanh thu rất lớn mà không cần tăng volume; nguyên tắc Pareto và mối quan hệ phi tuyến giữa ADR và tỷ lệ hủy thể hiện rõ.

- **Định hình hiểu biết:** Dự án khẳng định Data Science là lĩnh vực liên ngành, kết hợp kỹ thuật, thống kê, kiến thức lĩnh vực và tư duy kinh doanh.

#### **23120348 - Ngô Thị Thục Quyên**

**1. Thách thức và Khó khăn**

- **Thách thức kỹ thuật:** Việc xử lý tập dữ liệu lớn với nhiều biến phân loại và giá trị thiếu gặp nhiều khó khăn, đặc biệt khi thực hiện các phân tích theo thời gian, phân khúc khách hàng và quốc gia. Ban đầu, việc chuẩn hóa dữ liệu và lựa chọn chỉ số phù hợp để so sánh giữa các nhóm chưa rõ ràng, dễ dẫn đến kết quả phân tích bị lệch.
- **Cách vượt qua:** Khó khăn này được khắc phục bằng cách xem xét mục tiêu của từng câu hỏi phân tích, gộp các nhóm hiếm để giảm nhiễu, và sử dụng các thước đo như tỷ lệ, giá trị trung bình thay vì so sánh số lượng tuyệt đối.
- **Thách thức lớn nhất:** Thách thức lớn nhất là chuyển các kết quả phân tích thành kết luận có thể hỗ trợ ra quyết định, thay vì chỉ mô tả sự khác biệt giữa các nhóm bằng số liệu và biểu đồ.

**2. Học hỏi và Phát triển**

- **Kỹ năng kỹ thuật:** Kỹ năng xử lý và tổng hợp dữ liệu để trả lời các câu hỏi kinh doanh cụ thể đã được cải thiện, đặc biệt trong việc xây dựng các chỉ số như số lượng booking, ADR, số đêm lưu trú và doanh thu trên mỗi booking nhằm so sánh giữa các nhóm khác nhau.
- **Phương pháp phân tích:** Nhận thức rõ hơn về tầm quan trọng của việc xác định đúng câu hỏi phân tích trước khi lựa chọn phương pháp xử lý và so sánh dữ liệu. Việc sử dụng các thước đo phù hợp giúp tránh các kết luận sai lệch khi so sánh giữa các phân khúc khách hàng, mùa vụ và thị trường quốc gia.
- **Kiến thức lĩnh vực:** Hiểu rõ hơn về đặc điểm nhu cầu khách sạn, sự khác biệt giữa City Hotel và Resort Hotel, cũng như cách mùa vụ, phân khúc khách hàng và thị trường địa lý ảnh hưởng đến doanh thu và hành vi đặt phòng.
- **Điều gây ngạc nhiên:** Một phát hiện đáng chú ý là các phân khúc hoặc thị trường có số lượng booking không lớn vẫn có thể đóng góp giá trị doanh thu cao, cho thấy quy mô không phải lúc nào cũng phản ánh hiệu quả kinh doanh.
- **Định hình hiểu biết:** Dự án này giúp làm rõ rằng Khoa học Dữ liệu không chỉ là kỹ thuật phân tích, mà là quá trình chuyển dữ liệu thành insight có ý nghĩa để hỗ trợ quyết định thực tế.

#### **23120265 - Nguyễn Thái Hoàng**

**1. Thách thức và Khó khăn**

- **Thách thức kỹ thuật:** Xử lý tập dữ liệu lớn với 119,390 giao dịch đặt phòng và 32 đặc trưng, trong đó có 31,994 dòng trùng lặp (~26.8%), nhiều giá trị thiếu (company 94%, agent 14%) và các giá trị không hợp lệ (ADR ≤ 0, adults = 0, lead_time âm). Việc quyết định giữ hay loại bỏ các outliers khi ADR > €5000 và lead_time lên đến hàng trăm ngày là một thách thức lớn.

- **Cách vượt qua:** Áp dụng chiến lược xử lý dữ liệu có hệ thống: loại bỏ duplicates và invalid values, sử dụng kiến thức lĩnh vực để xử lý missing values (children = 0 cho booking không có trẻ em, agent/company = "Unknown" cho đặt phòng trực tiếp), phân tích IQR và Z-score để đánh giá outliers. Thực hiện các kiểm định thống kê để xác nhận mối quan hệ với biến mục tiêu trước khi quyết định giữ hoặc loại bỏ đặc trưng.

- **Thách thức khó nhất:** Cân bằng giữa chất lượng dữ liệu và bảo toàn thông tin - quyết định có nên loại bỏ biến company (94% missing) hay giữ lại vì "missing = personal booking" có thể mang thông tin dự đoán quan trọng. Phải hiểu sâu về ngữ cảnh kinh doanh khách sạn để đưa ra quyết định tiền xử lý hợp lý, không chỉ dựa vào kỹ thuật thuần túy.

**2. Học hỏi và Phát triển**

- **Kỹ năng kỹ thuật:** Thành thạo quy trình EDA toàn diện từ phân tích kiểu dữ liệu (18 numerical, 14 categorical) đến phát hiện vấn đề chất lượng, phân tích thống kê (skewness, kurtosis, correlation), phát hiện outliers và kiểm định giả thuyết. Học được cách sử dụng hiệu quả các hàm pandas (`.duplicated()`, `.isna()`, `.describe()`, `.corr()`) và công cụ trực quan hóa (seaborn, matplotlib) để khám phá dữ liệu.

- **Phương pháp phân tích:** Nhận ra EDA không chỉ là "xem qua dữ liệu" mà là quá trình điều tra có hệ thống với các bước rõ ràng: Tổng quan → Phân tích Numerical → Phân tích Categorical → Missing Data → Mối quan hệ → Insights. Hiểu được tầm quan trọng của domain knowledge trong việc giải thích các mẫu dữ liệu (ví dụ: lead_time cao thường đi kèm cancellation risk cao).

- **Kiến thức lĩnh vực:** Hiểu rõ hơn về đặc điểm đặt phòng khách sạn: sự khác biệt giữa City Hotel và Resort Hotel, vai trò của travel agents so với đặt phòng trực tiếp, tác động của các loại deposit (Non-refund vs Refundable) lên hành vi hủy phòng, và các mô hình theo mùa trong nhu cầu. Nhận ra tỷ lệ hủy 37% là vấn đề nghiêm trọng cần giải quyết.

- **Điều gây ngạc nhiên:** Phát hiện lead_time và deposit_type có mối liên hệ mạnh với hủy phòng (p < 0.001), trong khi các yếu tố dự kiến như số người lớn hoặc chỗ đỗ xe lại không có ý nghĩa thống kê. Các biến có cardinality cao (country: 178 giá trị, agent: 334 IDs) tuy đặt ra thách thức encoding nhưng lại chứa thông tin quan trọng về phân khúc khách hàng.

- **Định hình hiểu biết:** Dự án này khẳng định Data Science trong bối cảnh kinh doanh đòi hỏi tư duy hai chiều: nghiêm ngặt về kỹ thuật (kiểm định thống kê, xử lý đúng các vấn đề dữ liệu) và hiểu biết kinh doanh (hiểu ý nghĩa của các con số đối với khách sạn). Quan trọng nhất là mindset "chất lượng dữ liệu trước tiên" - không thể xây dựng mô hình tốt trên dữ liệu kém chất lượng.